In [1]:
import os
os.environ['R_HOME'] = "C:/PROGRA~1/R/R-44~1.2"  # Use forward slashes for Windows paths in Python

import rpy2.robjects as robjects
from rpy2.robjects.packages import importr

In [2]:
pip install sqlalchemy pyodbc pandas openpyxl requests XlsxWriter pyyaml rpy2 statsmodels tenacity nltk


   ---------------------------------------- 0.0/1.5 MB ? eta -:--:--
   ---------------------------------------- 1.5/1.5 MB 15.9 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: C:\Users\JulianHeron\Software Projects\Database Administration\env\Scripts\python.exe -m pip install --upgrade pip


In [3]:
pip install --upgrade pyodbc sqlalchemy

Note: you may need to restart the kernel to use updated packages.Requirement already satisfied: pyodbc in c:\users\julianheron\software projects\database administration\env\lib\site-packages (5.2.0)




[notice] A new release of pip is available: 24.3.1 -> 25.0
[notice] To update, run: C:\Users\JulianHeron\Software Projects\Database Administration\env\Scripts\python.exe -m pip install --upgrade pip


In [4]:
import rpy2.robjects as robjects
from rpy2.robjects.packages import importr

# Import R packages
base = importr('base')
utils = importr('utils')
aqrr = importr('aqrr')  # Assuming you've installed the 'aqrr' package in R
dplyr = importr('dplyr')


In [5]:
pip install --upgrade certifi

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.3.1 -> 25.0
[notice] To update, run: C:\Users\JulianHeron\Software Projects\Database Administration\env\Scripts\python.exe -m pip install --upgrade pip


In [6]:
import pyodbc
import sqlalchemy
print("PyODBC version:", pyodbc.version)
print("SQLAlchemy version:", sqlalchemy.__version__)

PyODBC version: 5.2.0
SQLAlchemy version: 2.0.37


In [7]:
import rpy2.robjects as robjects
from rpy2.robjects.packages import importr
import pandas as pd
import numpy as np

aqrr = importr('aqrr')

# Get monthly BAB data
bab_data = aqrr.aqr_bab_monthly()

# Convert R DataFrame to numpy array, then to pandas DataFrame
bab_np = np.array(bab_data)
bab_df = pd.DataFrame(bab_np)

# If you need column names or index, you'll have to add them manually
# Example:
# bab_df.columns = ['Column1', 'Column2', ...]  # Adjust according to actual data structure
# bab_df.index = pd.to_datetime(bab_df.iloc[:, 0])  # If the first column is dates, for instance

print(bab_df.head())

R[write to console]: 
R[write to console]: -
                                                                              
R[write to console]: 
R[write to console]: 
R[write to console]: /
                                                                              
R[write to console]: 
R[write to console]: 
R[write to console]: -
                                                                              
R[write to console]: 


      0         1         2         3         4         5         6      \
0  -14246.0  -14246.0  -14246.0  -14246.0  -14246.0  -14246.0  -14246.0   
1       AUS       AUT       BEL       CAN       CHE       DEU       DNK   
2       nan       nan       nan       nan       nan       nan       nan   

      7         8         9      ...                  32180  \
0  -14246.0  -14246.0  -14246.0  ...                19508.0   
1       ESP       FIN       FRA  ...                    NZL   
2       nan       nan       nan  ...  -0.019241410420476744   

                 32181                 32182                 32183  \
0              19508.0               19508.0               19508.0   
1                  PRT                   SGP                   SWE   
2  0.03327881593321119  0.043234163794845605  -0.04640383808659797   

                  32184                 32185                   32186  \
0               19508.0               19508.0                 19508.0   
1                  

In [15]:
ycapi= "yIIphqbsQysnTvWWxfW33w"


In [6]:
from sqlalchemy import create_engine
from sqlalchemy import text

# Define your connection string using Windows Authentication
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?trusted_connection=yes&driver=SQL+Server"

# Create the engine with the connection string
engine = create_engine(connection_string)

# Test the connection
with engine.connect() as connection:
    result = connection.execute(text("SELECT 1"))
    print("Database connection successful:", result.fetchone()[0] == 1)

Database connection successful: True


In [8]:
#Excel import of RJ Funds on platform
import pandas as pd
from sqlalchemy import create_engine, Table, Column, Integer, String, MetaData

# Corrected Connection String
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"

# Create the engine with fast_executemany for bulk inserts
engine = create_engine(connection_string, fast_executemany=True)

# Metadata object for table definitions
metadata = MetaData()

# Function to determine SQLAlchemy column type
def guess_type(pandas_series):
    if pd.api.types.is_integer_dtype(pandas_series):
        return Integer
    elif pd.api.types.is_numeric_dtype(pandas_series):
        return String(20)  # Allow room for decimals
    else:
        max_length = pandas_series.astype(str).str.len().max()
        return String(max_length if pd.notna(max_length) else 255)  # Default to 255 if empty

# Function to create a table from Excel content
def create_table_from_excel(excel_file_path, table_name, sheet_name='Sheet1'):
    # Read Excel file into a pandas DataFrame
    df = pd.read_excel(excel_file_path, sheet_name=sheet_name)

    # Clean table name: Replace spaces with underscores
    table_name = table_name.strip().replace(' ', '_')

    # Clean column names: Replace spaces with underscores, remove special characters
    df.columns = df.columns.str.strip().str.replace(r'[^A-Za-z0-9_]', '', regex=True).str.replace(' ', '_')

    # Define columns based on DataFrame with max character length
    columns = [Column(column_name, guess_type(df[column_name])) for column_name in df.columns]

    # Create table if not exists
    table = Table(table_name, metadata, *columns)
    metadata.create_all(engine)

    # Insert data into the table with smaller chunks
    with engine.connect() as connection:
        for i in range(0, len(df), 500):  # Insert 500 rows at a time
            chunk = df.iloc[i:i+500]
            chunk.to_sql(table_name, con=engine, if_exists='append', index=False)
    
    print(f"Table '{table_name}' created and data inserted.")

# Example usage
excel_file_path = r"C:\Users\JulianHeron\Software Projects\Database Project Files\RJ import list.xlsx"
table_name = 'RJ Import'  # Original table name with spaces

create_table_from_excel(excel_file_path, table_name)


Table 'RJ_Import' created and data inserted.


In [ ]:
#YCharts Broad Category Mapping
import requests
import sqlalchemy
import pandas as pd
from concurrent.futures import ThreadPoolExecutor
import time

# ✅ SQLAlchemy Connection String
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"
engine = sqlalchemy.create_engine(connection_string)

# ✅ Start Timer
start_time = time.time()

# ✅ Fetch Symbols that Need Categorization
step_start = time.time()
print("🔄 Fetching tickers that need categorization...")
query = """
    SELECT SymbolCUSIP, Fund_Type_ID 
    FROM RJ_Import
    WHERE YC_Broad_Category_ID IS NULL
"""
funds = pd.read_sql(query, engine)
print(f"✅ Retrieval Complete. {len(funds)} tickers need categorization. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Define API Key
ycapi = "yIIphqbsQysnTvWWxfW33w"

# ✅ Function to determine correct API URL format
def get_api_url(symbol, fund_type_id):
    if fund_type_id == 3:  # Mutual Funds need "M:"
        return f"https://api.ycharts.com/v3/mutual_funds/M:{symbol}/info/broad_category_group?retrieve_ttl=true"
    else:  # ETFs & Closed-End Funds use /companies/
        return f"https://api.ycharts.com/v3/companies/{symbol}/info/broad_category_group?retrieve_ttl=true"

# ✅ Headers copied from Fiddler
headers = {
    "X-YCHARTSAUTHORIZATION": ycapi,
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "X-YCHARTSIP": "50.58.50.123",
    "Host": "api.ycharts.com",
    "Connection": "Keep-Alive"
}

# ✅ Fetch Broad Categories in Parallel (Only for Missing Symbols)
def fetch_category(row):
    """Fetch broad category from YCharts API."""
    symbol, fund_type_id = row["SymbolCUSIP"], row["Fund_Type_ID"]
    api_url = get_api_url(symbol, fund_type_id)
    response = requests.get(api_url, headers=headers)

    if response.status_code == 200:
        data = response.json()
        response_key = f"M:{symbol}" if fund_type_id == 3 else symbol
        return symbol, data["response"].get(response_key, {}).get("results", {}).get("broad_category_group", {}).get("data", "Uncategorized")
    return symbol, "Uncategorized"

step_start = time.time()
print("🔄 Fetching Broad Categories in parallel...")
with ThreadPoolExecutor(max_workers=15) as executor:  # Adjust max_workers for API limits
    results = list(executor.map(fetch_category, funds.to_dict(orient="records")))
print(f"✅ API Data Retrieval Complete. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Count Results
broad_categories = dict(results)
num_successful = sum(1 for v in broad_categories.values() if v != "Uncategorized")
num_unsuccessful = sum(1 for v in broad_categories.values() if v == "Uncategorized")
print(f"✅ Successfully Categorized: {num_successful}, Unsuccessful: {num_unsuccessful}, Labeled 'Uncategorized': {num_unsuccessful}")

# ✅ Batch Insert Unique Broad Categories into `YC_Broad_Category_List`
step_start = time.time()
print("🔄 Storing Unique Broad Categories...")

# ✅ Remove None values and sort
unique_categories = sorted(set(filter(None, broad_categories.values())))  

if unique_categories:
    with engine.begin() as conn:
        conn.execute(
            sqlalchemy.text("""
                INSERT INTO YC_Broad_Category_List (Broad_Category_Name)
                SELECT DISTINCT v.Broad_Category_Name
                FROM (VALUES """ +
                ", ".join(f"(:c{i})" for i in range(len(unique_categories))) + 
                """) AS v (Broad_Category_Name)
                WHERE NOT EXISTS (
                    SELECT 1 FROM YC_Broad_Category_List y WHERE y.Broad_Category_Name = v.Broad_Category_Name
                )
            """),
            {f"c{i}": unique_categories[i] for i in range(len(unique_categories))}
        )
    print(f"✅ {len(unique_categories)} broad categories stored. (⏱ {time.time() - step_start:.2f} sec)")
else:
    print("⚠️ No valid broad categories found to store.")

# ✅ Retrieve Updated Category IDs
step_start = time.time()
print("🔄 Mapping Categories to IDs...")
category_mapping = pd.read_sql("SELECT ID, Broad_Category_Name FROM YC_Broad_Category_List", engine)
category_mapping_dict = dict(zip(category_mapping["Broad_Category_Name"], category_mapping["ID"]))
print(f"✅ Mapping complete. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Batch Update `RJ_Import` with `YC_Broad_Category_ID`
step_start = time.time()
print("🔄 Updating RJ_Import with Category IDs...")

update_values = [
    f"('{symbol}', {category_mapping_dict.get(category, 'NULL')})"
    for symbol, category in broad_categories.items()
    if category in category_mapping_dict  # Only include known categories
]

if update_values:
    with engine.begin() as conn:
        conn.execute(
            sqlalchemy.text("""
                UPDATE RJ_Import 
                SET YC_Broad_Category_ID = v.YC_Broad_Category_ID
                FROM (VALUES """ +
                ", ".join(update_values) + 
                """) AS v (SymbolCUSIP, YC_Broad_Category_ID)
                WHERE RJ_Import.SymbolCUSIP = v.SymbolCUSIP
            """)
        )
    print(f"✅ RJ_Import update complete. (⏱ {time.time() - step_start:.2f} sec)")
else:
    print("⚠️ No valid category IDs to update.")

print(f"\n🎉 **Process Completed Successfully! Total time: {time.time() - start_time:.2f} sec**")


In [ ]:
# YCharts Broad Asset Class Category Mapping

import requests
import sqlalchemy
import pandas as pd
from concurrent.futures import ThreadPoolExecutor
import time

# ✅ SQLAlchemy Connection String
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"
engine = sqlalchemy.create_engine(connection_string)

# ✅ Start Timer
start_time = time.time()

# ✅ Fetch Symbols that Need Categorization
step_start = time.time()
print("🔄 Fetching tickers that need categorization...")
query = """
    SELECT SymbolCUSIP, Fund_Type_ID 
    FROM RJ_Import
    WHERE YC_Broad_Asset_Class_ID IS NULL
"""
funds = pd.read_sql(query, engine)
print(f"✅ Retrieval Complete. {len(funds)} tickers need categorization. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Define API Key
ycapi = "yIIphqbsQysnTvWWxfW33w"

# ✅ Function to determine correct API URL format
def get_api_url(symbol, fund_type_id):
    if fund_type_id == 3:  # Mutual Funds need "M:"
        return f"https://api.ycharts.com/v3/mutual_funds/M:{symbol}/info/broad_asset_class?retrieve_ttl=true"
    else:  # ETFs & Closed-End Funds use /companies/
        return f"https://api.ycharts.com/v3/companies/{symbol}/info/broad_asset_class?retrieve_ttl=true"

# ✅ Headers copied from Fiddler
headers = {
    "X-YCHARTSAUTHORIZATION": ycapi,
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "X-YCHARTSIP": "50.58.50.123",
    "Host": "api.ycharts.com",
    "Connection": "Keep-Alive"
}

# ✅ Fetch Broad Asset Classes in Parallel (Only for Missing Symbols)
def fetch_asset_class(row):
    """Fetch broad asset class from YCharts API."""
    symbol, fund_type_id = row["SymbolCUSIP"], row["Fund_Type_ID"]
    api_url = get_api_url(symbol, fund_type_id)
    response = requests.get(api_url, headers=headers)

    if response.status_code == 200:
        data = response.json()
        response_key = f"M:{symbol}" if fund_type_id == 3 else symbol
        return symbol, data["response"].get(response_key, {}).get("results", {}).get("broad_asset_class", {}).get("data", "Uncategorized")
    return symbol, "Uncategorized"

step_start = time.time()
print("🔄 Fetching Broad Asset Classes in parallel...")
with ThreadPoolExecutor(max_workers=10) as executor:  # Adjust max_workers for API limits
    results = list(executor.map(fetch_asset_class, funds.to_dict(orient="records")))
print(f"✅ API Data Retrieval Complete. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Count Results
broad_asset_classes = dict(results)
num_successful = sum(1 for v in broad_asset_classes.values() if v != "Uncategorized")
num_unsuccessful = sum(1 for v in broad_asset_classes.values() if v == "Uncategorized")
print(f"✅ Successfully Categorized: {num_successful}, Unsuccessful: {num_unsuccessful}, Labeled 'Uncategorized': {num_unsuccessful}")

# ✅ Batch Insert Unique Broad Asset Classes into `YC_Broad_Asset_Class_List`
step_start = time.time()
print("🔄 Storing Unique Broad Asset Classes...")

# ✅ Remove None values and sort
unique_classes = sorted(set(filter(None, broad_asset_classes.values())))  

if unique_classes:
    with engine.begin() as conn:
        conn.execute(
            sqlalchemy.text("""
                INSERT INTO YC_Broad_Asset_Class_List (Broad_Asset_Class_Name)
                SELECT DISTINCT v.Broad_Asset_Class_Name
                FROM (VALUES """ +
                ", ".join(f"(:c{i})" for i in range(len(unique_classes))) + 
                """) AS v (Broad_Asset_Class_Name)
                WHERE NOT EXISTS (
                    SELECT 1 FROM YC_Broad_Asset_Class_List y WHERE y.Broad_Asset_Class_Name = v.Broad_Asset_Class_Name
                )
            """),
            {f"c{i}": unique_classes[i] for i in range(len(unique_classes))}
        )
    print(f"✅ {len(unique_classes)} asset classes stored. (⏱ {time.time() - step_start:.2f} sec)")
else:
    print("⚠️ No valid asset classes found to store.")

# ✅ Retrieve Updated Asset Class IDs
step_start = time.time()
print("🔄 Mapping Asset Classes to IDs...")
asset_class_mapping = pd.read_sql("SELECT ID, Broad_Asset_Class_Name FROM YC_Broad_Asset_Class_List", engine)
asset_class_mapping_dict = dict(zip(asset_class_mapping["Broad_Asset_Class_Name"], asset_class_mapping["ID"]))
print(f"✅ Mapping complete. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Batch Update `RJ_Import` with `YC_Broad_Asset_Class_ID`
step_start = time.time()
print("🔄 Updating RJ_Import with Asset Class IDs...")

update_values = [
    f"('{symbol}', {asset_class_mapping_dict.get(asset_class, 'NULL')})"
    for symbol, asset_class in broad_asset_classes.items()
    if asset_class in asset_class_mapping_dict  # Only include known categories
]

if update_values:
    with engine.begin() as conn:
        conn.execute(
            sqlalchemy.text("""
                UPDATE RJ_Import 
                SET YC_Broad_Asset_Class_ID = v.YC_Broad_Asset_Class_ID
                FROM (VALUES """ +
                ", ".join(update_values) + 
                """) AS v (SymbolCUSIP, YC_Broad_Asset_Class_ID)
                WHERE RJ_Import.SymbolCUSIP = v.SymbolCUSIP
            """)
        )
    print(f"✅ RJ_Import update complete. (⏱ {time.time() - step_start:.2f} sec)")
else:
    print("⚠️ No valid asset class IDs to update.")

print(f"\n🎉 **Process Completed Successfully! Total time: {time.time() - start_time:.2f} sec**")


In [28]:
# YCharts Global Category Name Mapping

import requests
import sqlalchemy
import pandas as pd
from concurrent.futures import ThreadPoolExecutor
import time

# ✅ SQLAlchemy Connection String
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"
engine = sqlalchemy.create_engine(connection_string)

# ✅ Start Timer
start_time = time.time()

# ✅ Fetch Symbols that Need Categorization
step_start = time.time()
print("🔄 Fetching tickers that need categorization...")
query = """
    SELECT SymbolCUSIP, Fund_Type_ID 
    FROM RJ_Import
    WHERE YC_Global_Category_ID IS NULL
"""
funds = pd.read_sql(query, engine)
print(f"✅ Retrieval Complete. {len(funds)} tickers need categorization. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Define API Key
ycapi = "yIIphqbsQysnTvWWxfW33w"

# ✅ Function to determine correct API URL format
def get_api_url(symbol, fund_type_id):
    if fund_type_id == 3:  # Mutual Funds need "M:"
        return f"https://api.ycharts.com/v3/mutual_funds/M:{symbol}/info/global_category_name?retrieve_ttl=true"
    else:  # ETFs & Closed-End Funds use /companies/
        return f"https://api.ycharts.com/v3/companies/{symbol}/info/global_category_name?retrieve_ttl=true"

# ✅ Headers copied from Fiddler
headers = {
    "X-YCHARTSAUTHORIZATION": ycapi,
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "X-YCHARTSIP": "50.58.50.123",
    "Host": "api.ycharts.com",
    "Connection": "Keep-Alive"
}

# ✅ Fetch Global Categories in Parallel (Only for Missing Symbols)
def fetch_global_category(row):
    """Fetch global category name from YCharts API."""
    symbol, fund_type_id = row["SymbolCUSIP"], row["Fund_Type_ID"]
    api_url = get_api_url(symbol, fund_type_id)
    response = requests.get(api_url, headers=headers)

    if response.status_code == 200:
        data = response.json()
        response_key = f"M:{symbol}" if fund_type_id == 3 else symbol
        return symbol, data["response"].get(response_key, {}).get("results", {}).get("global_category_name", {}).get("data", "Uncategorized")
    return symbol, "Uncategorized"

step_start = time.time()
print("🔄 Fetching Global Categories in parallel...")
with ThreadPoolExecutor(max_workers=10) as executor:  # Adjust max_workers for API limits
    results = list(executor.map(fetch_global_category, funds.to_dict(orient="records")))
print(f"✅ API Data Retrieval Complete. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Count Results
global_categories = dict(results)
num_successful = sum(1 for v in global_categories.values() if v != "Uncategorized")
num_unsuccessful = sum(1 for v in global_categories.values() if v == "Uncategorized")
print(f"✅ Successfully Categorized: {num_successful}, Unsuccessful: {num_unsuccessful}, Labeled 'Uncategorized': {num_unsuccessful}")

# ✅ Batch Insert Unique Global Categories into `YC_Global_Category_List`
step_start = time.time()
print("🔄 Storing Unique Global Categories...")

# ✅ Remove None values and sort alphabetically
unique_categories = sorted(set(filter(None, global_categories.values())))  

if unique_categories:
    with engine.begin() as conn:
        conn.execute(
            sqlalchemy.text("""
                INSERT INTO YC_Global_Category_List (Global_Category_Name)
                SELECT DISTINCT v.Global_Category_Name
                FROM (VALUES """ +
                ", ".join(f"(:c{i})" for i in range(len(unique_categories))) + 
                """) AS v (Global_Category_Name)
                WHERE NOT EXISTS (
                    SELECT 1 FROM YC_Global_Category_List y WHERE y.Global_Category_Name = v.Global_Category_Name
                )
            """),
            {f"c{i}": unique_categories[i] for i in range(len(unique_categories))}
        )
    print(f"✅ {len(unique_categories)} global categories stored. (⏱ {time.time() - step_start:.2f} sec)")
else:
    print("⚠️ No valid global categories found to store.")

# ✅ Retrieve Updated Global Category IDs
step_start = time.time()
print("🔄 Mapping Global Categories to IDs...")
category_mapping = pd.read_sql("SELECT ID, Global_Category_Name FROM YC_Global_Category_List", engine)
category_mapping_dict = dict(zip(category_mapping["Global_Category_Name"], category_mapping["ID"]))
print(f"✅ Mapping complete. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Batch Update `RJ_Import` with `YC_Global_Category_ID`
step_start = time.time()
print("🔄 Updating RJ_Import with Global Category IDs...")

update_values = [
    f"('{symbol}', {category_mapping_dict.get(category, 'NULL')})"
    for symbol, category in global_categories.items()
    if category in category_mapping_dict  # Only include known categories
]

if update_values:
    with engine.begin() as conn:
        conn.execute(
            sqlalchemy.text("""
                UPDATE RJ_Import 
                SET YC_Global_Category_ID = v.YC_Global_Category_ID
                FROM (VALUES """ +
                ", ".join(update_values) + 
                """) AS v (SymbolCUSIP, YC_Global_Category_ID)
                WHERE RJ_Import.SymbolCUSIP = v.SymbolCUSIP
            """)
        )
    print(f"✅ RJ_Import update complete. (⏱ {time.time() - step_start:.2f} sec)")
else:
    print("⚠️ No valid global category IDs to update.")

print(f"\n🎉 **Process Completed Successfully! Total time: {time.time() - start_time:.2f} sec**")


🔄 Fetching tickers that need categorization...
✅ Retrieval Complete. 6699 tickers need categorization. (⏱ 0.03 sec)
🔄 Fetching Global Categories in parallel...
✅ API Data Retrieval Complete. (⏱ 380.42 sec)
✅ Successfully Categorized: 6524, Unsuccessful: 136, Labeled 'Uncategorized': 136
🔄 Storing Unique Global Categories...
✅ 60 global categories stored. (⏱ 0.02 sec)
🔄 Mapping Global Categories to IDs...
✅ Mapping complete. (⏱ 0.00 sec)
🔄 Updating RJ_Import with Global Category IDs...
✅ RJ_Import update complete. (⏱ 0.91 sec)

🎉 **Process Completed Successfully! Total time: 381.38 sec**


In [31]:
# YCharts Category Name Mapping

import requests
import sqlalchemy
import pandas as pd
from concurrent.futures import ThreadPoolExecutor
import time

# ✅ SQLAlchemy Connection String
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"
engine = sqlalchemy.create_engine(connection_string)

# ✅ Start Timer
start_time = time.time()

# ✅ Fetch Symbols that Need Categorization
step_start = time.time()
print("🔄 Fetching tickers that need categorization...")
query = """
    SELECT SymbolCUSIP, Fund_Type_ID 
    FROM RJ_Import
    WHERE YC_Category_ID IS NULL
"""
funds = pd.read_sql(query, engine)
print(f"✅ Retrieval Complete. {len(funds)} tickers need categorization. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Define API Key
ycapi = "yIIphqbsQysnTvWWxfW33w"

# ✅ Function to determine correct API URL format
def get_api_url(symbol, fund_type_id):
    if fund_type_id == 3:  # Mutual Funds need "M:"
        return f"https://api.ycharts.com/v3/mutual_funds/M:{symbol}/info/category_name?retrieve_ttl=true"
    else:  # ETFs & Closed-End Funds use /companies/
        return f"https://api.ycharts.com/v3/companies/{symbol}/info/category_name?retrieve_ttl=true"

# ✅ Headers copied from Fiddler
headers = {
    "X-YCHARTSAUTHORIZATION": ycapi,
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "X-YCHARTSIP": "50.58.50.123",
    "Host": "api.ycharts.com",
    "Connection": "Keep-Alive"
}

# ✅ Fetch Category Names in Parallel (Only for Missing Symbols)
def fetch_category(row):
    """Fetch category name from YCharts API."""
    symbol, fund_type_id = row["SymbolCUSIP"], row["Fund_Type_ID"]
    api_url = get_api_url(symbol, fund_type_id)
    response = requests.get(api_url, headers=headers)

    if response.status_code == 200:
        data = response.json()
        response_key = f"M:{symbol}" if fund_type_id == 3 else symbol
        return symbol, data["response"].get(response_key, {}).get("results", {}).get("category_name", {}).get("data", "Uncategorized")
    return symbol, "Uncategorized"

step_start = time.time()
print("🔄 Fetching Category Names in parallel...")
with ThreadPoolExecutor(max_workers=25) as executor:  # Adjust max_workers for API limits
    results = list(executor.map(fetch_category, funds.to_dict(orient="records")))
print(f"✅ API Data Retrieval Complete. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Count Results
categories = dict(results)
num_successful = sum(1 for v in categories.values() if v != "Uncategorized")
num_unsuccessful = sum(1 for v in categories.values() if v == "Uncategorized")
print(f"✅ Successfully Categorized: {num_successful}, Unsuccessful: {num_unsuccessful}, Labeled 'Uncategorized': {num_unsuccessful}")

# ✅ Batch Insert Unique Category Names into `YC_Category_List`
step_start = time.time()
print("🔄 Storing Unique Category Names...")

# ✅ Remove None values and sort alphabetically
unique_categories = sorted(set(filter(None, categories.values())))  

if unique_categories:
    with engine.begin() as conn:
        conn.execute(
            sqlalchemy.text("""
                INSERT INTO YC_Category_List (Category_Name)
                SELECT DISTINCT v.Category_Name
                FROM (VALUES """ +
                ", ".join(f"(:c{i})" for i in range(len(unique_categories))) + 
                """) AS v (Category_Name)
                WHERE NOT EXISTS (
                    SELECT 1 FROM YC_Category_List y WHERE y.Category_Name = v.Category_Name
                )
            """),
            {f"c{i}": unique_categories[i] for i in range(len(unique_categories))}
        )
    print(f"✅ {len(unique_categories)} categories stored. (⏱ {time.time() - step_start:.2f} sec)")
else:
    print("⚠️ No valid categories found to store.")

# ✅ Retrieve Updated Category IDs
step_start = time.time()
print("🔄 Mapping Categories to IDs...")
category_mapping = pd.read_sql("SELECT ID, Category_Name FROM YC_Category_List", engine)
category_mapping_dict = dict(zip(category_mapping["Category_Name"], category_mapping["ID"]))
print(f"✅ Mapping complete. (⏱ {time.time() - step_start:.2f} sec)")

# ✅ Batch Update `RJ_Import` with `YC_Category_ID`
step_start = time.time()
print("🔄 Updating RJ_Import with Category IDs...")

update_values = [
    f"('{symbol}', {category_mapping_dict.get(category, 'NULL')})"
    for symbol, category in categories.items()
    if category in category_mapping_dict  # Only include known categories
]

if update_values:
    with engine.begin() as conn:
        conn.execute(
            sqlalchemy.text("""
                UPDATE RJ_Import 
                SET YC_Category_ID = v.YC_Category_ID
                FROM (VALUES """ +
                ", ".join(update_values) + 
                """) AS v (SymbolCUSIP, YC_Category_ID)
                WHERE RJ_Import.SymbolCUSIP = v.SymbolCUSIP
            """)
        )
    print(f"✅ RJ_Import update complete. (⏱ {time.time() - step_start:.2f} sec)")
else:
    print("⚠️ No valid category IDs to update.")

print(f"\n🎉 **Process Completed Successfully! Total time: {time.time() - start_time:.2f} sec**")


🔄 Fetching tickers that need categorization...
✅ Retrieval Complete. 6699 tickers need categorization. (⏱ 0.03 sec)
🔄 Fetching Category Names in parallel...
✅ API Data Retrieval Complete. (⏱ 306.63 sec)
✅ Successfully Categorized: 6524, Unsuccessful: 136, Labeled 'Uncategorized': 136
🔄 Storing Unique Category Names...
✅ 125 categories stored. (⏱ 0.02 sec)
🔄 Mapping Categories to IDs...
✅ Mapping complete. (⏱ 0.01 sec)
🔄 Updating RJ_Import with Category IDs...
✅ RJ_Import update complete. (⏱ 0.78 sec)

🎉 **Process Completed Successfully! Total time: 307.47 sec**


In [36]:
import pandas as pd
import sqlalchemy

# ✅ SQLAlchemy Connection String
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"
engine = sqlalchemy.create_engine(connection_string)

# ✅ List Queries
queries = {
    "Broad_Category": "SELECT ID, Broad_Category_Name FROM YC_Broad_Category_List ORDER BY Broad_Category_Name",
    "Broad_Asset_Class": "SELECT ID, Broad_Asset_Class_Name FROM YC_Broad_Asset_Class_List ORDER BY Broad_Asset_Class_Name",
    "Global_Category": "SELECT ID, Global_Category_Name FROM YC_Global_Category_List ORDER BY Global_Category_Name",
    "Category_Name": "SELECT ID, Category_Name FROM YC_Category_List ORDER BY Category_Name"
}

# ✅ Extract Data
dataframes = {name: pd.read_sql(query, engine) for name, query in queries.items()}

# ✅ Save to Excel
output_file = "YC_Category_Lists.xlsx"
with pd.ExcelWriter(output_file, engine="xlsxwriter") as writer:
    for sheet_name, df in dataframes.items():
        df.to_excel(writer, sheet_name=sheet_name, index=False)

print(f"✅ Export complete! Data saved to {output_file}")


✅ Export complete! Data saved to YC_Category_Lists.xlsx


In [37]:
#Create unique category combinations from YC
import pandas as pd
import sqlalchemy

# ✅ SQLAlchemy Connection String
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"
engine = sqlalchemy.create_engine(connection_string)

# ✅ Query to Pull Unique Combinations of All 4 Categories
query = """
    SELECT DISTINCT 
        bc.Broad_Category_Name, 
        bac.Broad_Asset_Class_Name, 
        gc.Global_Category_Name, 
        c.Category_Name
    FROM RJ_Import rj
    LEFT JOIN YC_Broad_Category_List bc ON rj.YC_Broad_Category_ID = bc.ID
    LEFT JOIN YC_Broad_Asset_Class_List bac ON rj.YC_Broad_Asset_Class_ID = bac.ID
    LEFT JOIN YC_Global_Category_List gc ON rj.YC_Global_Category_ID = gc.ID
    LEFT JOIN YC_Category_List c ON rj.YC_Category_ID = c.ID
    ORDER BY bc.Broad_Category_Name, bac.Broad_Asset_Class_Name, gc.Global_Category_Name, c.Category_Name;
"""

# ✅ Extract Data
unique_combinations = pd.read_sql(query, engine)

# ✅ Save to Excel
output_file = "YC_Unique_Category_Combinations.xlsx"
unique_combinations.to_excel(output_file, sheet_name="Unique_Combinations", index=False)

print(f"✅ Export complete! Data saved to {output_file}")


✅ Export complete! Data saved to YC_Unique_Category_Combinations.xlsx


In [107]:
#First Level Categorization- CWA_Broad_Categories
from sqlalchemy import create_engine, text

# Your connection string
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database"
    "?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes"
    "&TrustServerCertificate=yes"
)

# Create the engine
engine = create_engine(connection_string)

print("✅ Initializaing Database Categorization Proceedures")
# SQL command to execute the stored procedure
sql_command = text("{CALL UpdateFundCategorization}")

try:
    # Execute the stored procedure
    with engine.connect() as connection:
        result = connection.execute(sql_command)
        connection.commit()
    print("Fund categorization updated successfully.")
except Exception as e:
    print(f"An error occurred: {e}")
finally:
    # Ensure the connection is closed
    engine.dispose()
print("✅ CWA Broad Category Mapping Complete!")

✅ Initializaing Database Categorization Proceedures
Fund categorization updated successfully.
✅ CWA Broad Category Mapping Complete!


In [115]:
#Moving categorized, covered funds into Screening table 
from sqlalchemy import create_engine, text

# Your connection string
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database"
    "?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes"
    "&TrustServerCertificate=yes"
)

# Create the engine
engine = create_engine(connection_string)

# SQL command to execute the stored procedure
sql_command = text("{CALL PopulateFundsToScreen}")

try:
    # Execute the stored procedure
    with engine.connect() as connection:
        result = connection.execute(sql_command)
        connection.commit()
    print("Funds_to_Screen table populated successfully.")
except Exception as e:
    print(f"An error occurred: {e}")
finally:
    # Ensure the connection is closed
    engine.dispose()

Funds_to_Screen table populated successfully.


In [ ]:
# Spotcheck of FULL RJ_Import table
import pandas as pd
import sqlalchemy
import logging
from sqlalchemy.exc import SQLAlchemyError

# Setup logging
log_path = r"C:\Users\JulianHeron\Software Projects\Database Project Files\categorization_spotcheck.log"
logging.basicConfig(level=logging.DEBUG, format='%(asctime)s - %(levelname)s - %(message)s', filename=log_path, filemode='w')
logger = logging.getLogger(__name__)

# Database connection string
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database"
    "?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes"
    "&TrustServerCertificate=yes"
)

# Output file path
output_path = r"C:\Users\JulianHeron\Software Projects\Database Project Files\RJ_Import_Full_Spotcheck.xlsx"

def main():
    try:
        # Connect to the database
        engine = sqlalchemy.create_engine(connection_string)
        with engine.connect() as conn:
            # ✅ Fully Fixed SQL Query (Including CWA_Broad_Category_Name)
            sql_query = sqlalchemy.text("""
                SELECT 
                    i.[SymbolCUSIP], i.[ProductName], 
                    i.[YC_Broad_Category_ID], bc.[Broad_Category_Name] as BroadCategoryName,
                    i.[YC_Broad_Asset_Class_ID], bac.[Broad_Asset_Class_Name] as BroadAssetClassName,
                    i.[YC_Global_Category_ID], gc.[Global_Category_Name] as GlobalCategoryName,
                    i.[YC_Category_ID], c.[Category_Name] as CategoryName,
                    i.[CWA_Broad_Category_ID], cwa.[CWA_Broad_Category_Name] as CWABroadCategoryName
                FROM RJ_Import i
                LEFT JOIN YC_Broad_Category_List bc ON i.[YC_Broad_Category_ID] = bc.[ID]
                LEFT JOIN YC_Broad_Asset_Class_List bac ON i.[YC_Broad_Asset_Class_ID] = bac.[ID]
                LEFT JOIN YC_Global_Category_List gc ON i.[YC_Global_Category_ID] = gc.[ID]
                LEFT JOIN YC_Category_List c ON i.[YC_Category_ID] = c.[ID]
                LEFT JOIN CWA_Broad_Category_List cwa ON i.[CWA_Broad_Category_ID] = cwa.[ID]
            """)

            # Execute query & fetch results into a Pandas DataFrame
            df = pd.read_sql(sql_query, conn)

            # Export to Excel
            df.to_excel(output_path, index=False)
            print(f"✅ Exported {len(df)} rows to {output_path}")
            logger.info(f"✅ Exported {len(df)} rows to {output_path}")

    except SQLAlchemyError as e:
        logger.error(f"Database error occurred: {e}")
        print(f"Database error occurred: {e}")
    except Exception as e:
        logger.error(f"An unexpected error occurred: {e}")
        print(f"An unexpected error occurred: {e}")

if __name__ == "__main__":
    main()


In [113]:
# Spotcheck Funds to Screen FULL export
from sqlalchemy import create_engine, text
import pandas as pd

# Your connection string
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database"
    "?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes"
    "&TrustServerCertificate=yes"
)

# Create the engine
engine = create_engine(connection_string)

# SQL query to fetch and merge data
sql_query = text("""
SELECT 
    fts.ProductName,
    fts.SymbolCUSIP,
    fts.ETFComplianceCategory,
    fts.ExpenseRatio,
    fts.Fund_Type_ID,
    bcl.Broad_Category_Name,
    acl.Broad_Asset_Class_Name,
    gcl.Global_Category_Name,
    cl.Category_Name,
    cwacl.CWA_Broad_Category_Name
FROM 
    Funds_to_Screen fts
LEFT JOIN YC_Broad_Category_List bcl ON fts.YC_Broad_Category_ID = bcl.ID
LEFT JOIN YC_Broad_Asset_Class_List acl ON fts.YC_Broad_Asset_Class_ID = acl.ID
LEFT JOIN YC_Global_Category_List gcl ON fts.YC_Global_Category_ID = gcl.ID
LEFT JOIN YC_Category_List cl ON fts.YC_Category_ID = cl.ID
LEFT JOIN CWA_Broad_Category_List cwacl ON fts.CWA_Broad_Category_ID = cwacl.ID;
""")

try:
    # Execute the query and fetch results into a DataFrame
    with engine.connect() as connection:
        result = connection.execute(sql_query)
        df = pd.DataFrame(result.fetchall(), columns=result.keys())
    
    # Export the DataFrame to Excel
    excel_file_path = 'Funds_with_Categories.xlsx'
    df.to_excel(excel_file_path, index=False)
    print(f"Data has been exported to {excel_file_path} successfully.")
    
except Exception as e:
    print(f"An error occurred: {e}")
finally:
    # Ensure the connection is closed
    engine.dispose()

Data has been exported to Funds_with_Categories.xlsx successfully.


In [1]:
#Database schema export
import json
from sqlalchemy import create_engine, inspect

def export_llm_friendly_schema(connection_string: str, export_filename: str):
    """
    Connect to the given SQL Server database using SQLAlchemy+pyodbc,
    inspect the schema, and export it as a JSON file in a format
    that is especially friendly for consumption by LLMs.
    """

    # Create the SQLAlchemy engine
    engine = create_engine(connection_string)

    # Create an inspector to gather schema information
    inspector = inspect(engine)

    # Collect all table names
    tables = inspector.get_table_names()

    # Build a top-level dictionary to hold the entire schema
    db_schema = {
        "database_name": None,   # Optional: fill in if you want a hard-coded DB name
        "tables": []
    }

    for table in tables:
        # Columns metadata
        # Each column is a dict with keys like: name, type, nullable, default, autoincrement
        columns_info = inspector.get_columns(table)
        formatted_columns = []
        for col in columns_info:
            formatted_columns.append({
                "name": col.get("name"),
                "type": str(col.get("type")),  # Convert SQLAlchemy type to string
                "nullable": col.get("nullable"),
                "default": col.get("default"),
                "autoincrement": col.get("autoincrement")
            })

        # Primary key metadata
        pk_info = inspector.get_pk_constraint(table)
        # pk_info is typically { 'constrained_columns': [col1, col2, ...], 'name': 'PK_name' }
        primary_keys = pk_info.get("constrained_columns", []) if pk_info else []

        # Foreign key metadata
        # Each fk is a dict with keys: 'constrained_columns', 'referred_schema',
        # 'referred_table', 'referred_columns', 'name'
        fk_info = inspector.get_foreign_keys(table)
        formatted_fks = []
        for fk in fk_info:
            formatted_fks.append({
                "constrained_columns": fk.get("constrained_columns"),
                "referred_schema": fk.get("referred_schema"),
                "referred_table": fk.get("referred_table"),
                "referred_columns": fk.get("referred_columns"),
                "name": fk.get("name")
            })

        # Index metadata
        # Each index is a dict with keys: 'name', 'unique', 'column_names'
        idx_info = inspector.get_indexes(table)
        formatted_indexes = []
        for idx in idx_info:
            formatted_indexes.append({
                "name": idx.get("name"),
                "unique": idx.get("unique"),
                "column_names": idx.get("column_names")
            })

        # Combine this table’s data
        table_info = {
            "table_name": table,
            "columns": formatted_columns,
            "primary_keys": primary_keys,
            "foreign_keys": formatted_fks,
            "indexes": formatted_indexes
        }

        db_schema["tables"].append(table_info)

    # Optionally, you can fill this in if you know the database name
    db_schema["database_name"] = "CWA_Fund_Database" 

    # Write out the schema JSON file
    with open(export_filename, 'w', encoding='utf-8') as f:
        json.dump(db_schema, f, indent=4, ensure_ascii=False)
    print(f"LLM-friendly database schema exported to {export_filename}")


if __name__ == "__main__":
    # Adjust the connection string as needed
    connection_string = (
        "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database"
        "?driver=ODBC+Driver+18+for+SQL+Server"
        "&trusted_connection=yes"
        "&TrustServerCertificate=yes"
    )

    # Export the schema in a single JSON file suitable for an LLM
    export_llm_friendly_schema(connection_string, "cwa_fund_schema.json")


LLM-friendly database schema exported to cwa_fund_schema.json


In [ ]:
#Add funds earliest performance date to funds_to_screen table
import requests
import sqlalchemy
import pandas as pd
import time

# ✅ Database Connection String
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"
engine = sqlalchemy.create_engine(connection_string)

# ✅ Fetch Funds Missing `EarliestPerformanceDate`
print("\n🔄 Fetching funds missing EarliestPerformanceDate...")
query = """
    SELECT SymbolCUSIP, Fund_Type_ID
    FROM Funds_to_Screen
    WHERE EarliestPerformanceDate IS NULL
"""
funds = pd.read_sql(query, engine)
print(f"✅ Retrieved {len(funds)} funds needing updates.\n")

# ✅ Headers Matching Excel's API Requests
headers = {
    "X-YCHARTSAUTHORIZATION": ycapi,  
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",  
    "X-YCHARTSEXCELVERSION": "4.4",  
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",  
    "X-YCHARTSIP": "",  
    "Host": "api.ycharts.com",
    "Connection": "Keep-Alive"
}

# ✅ Function to fetch `earliest_performance_date` for ETFs & Mutual Funds
def fetch_yci_data(symbol, fund_type_id):
    """Fetch earliest_performance_date, handling ETFs and Mutual Funds separately."""
    
    if fund_type_id == 3:  # ✅ Mutual Funds use "M:" and `/mutual_funds/`
        api_url = f"https://api.ycharts.com/v3/mutual_funds/M:{symbol}/info/earliest_performance_date?retrieve_ttl=true"
        print(f"🔎 Requesting M:{symbol} (Mutual Fund) - earliest_performance_date...")
    else:  # ✅ ETFs use `/companies/`
        api_url = f"https://api.ycharts.com/v3/companies/{symbol}/info/earliest_performance_date?retrieve_ttl=true"
        print(f"🔎 Requesting {symbol} (ETF) - earliest_performance_date...")

    for attempt in range(5):  # Retry up to 5 times
        response = requests.get(api_url, headers=headers)

        if response.status_code == 200:
            data = response.json()
            query_symbol = f"M:{symbol}" if fund_type_id == 3 else symbol  # Ensure correct key lookup

            # ✅ Check if "results" key exists before accessing it
            if "response" in data and query_symbol in data["response"]:
                results = data["response"][query_symbol].get("results", {})

                if "earliest_performance_date" in results:
                    date = pd.to_datetime(results["earliest_performance_date"]["data"]).date()
                    print(f"✅ {query_symbol} - Retrieved earliest_performance_date: {date}")
                    return symbol, date
                else:
                    print(f"⚠️ {query_symbol} - No `earliest_performance_date` found in API response.")
                    return symbol, None
            else:
                print(f"⚠️ {query_symbol} - Unexpected API response format: {data}")
                return symbol, None

        elif response.status_code == 403:  # API limit hit
            wait_time = 120  # Wait 2 minutes before retrying
            print(f"⚠️ API limit hit for {query_symbol}. Waiting {wait_time} seconds before retry ({attempt+1}/5)...")
            time.sleep(wait_time)
        
        else:
            print(f"❌ {query_symbol} - Error {response.status_code}: {response.text}")
            return symbol, None  # Stop trying on other errors

    print(f"⛔ {query_symbol} - Failed after 5 retries.")
    return symbol, None

# ✅ Process all funds (0.1-second delay per request to prevent API bans)
data_list = []
for index, row in funds.iterrows():
    symbol = row["SymbolCUSIP"]
    fund_type_id = row["Fund_Type_ID"]

    result = fetch_yci_data(symbol, fund_type_id)
    if result[1]:  # Only keep successful responses
        data_list.append(result)

    time.sleep(0.1)  # ✅ Fast execution unless rate limits increase

# ✅ Convert API results to DataFrame
df_yci = pd.DataFrame(data_list, columns=["SymbolCUSIP", "EarliestPerformanceDate"])

# ✅ Inspect DataFrame Before Writing to SQL
print("\n🔍 **YCI Data Preview:**")
print(df_yci.head())
print(df_yci.info())

# ✅ Store Data in SQL
if not df_yci.empty:
    with engine.begin() as conn:
        for index, row in df_yci.iterrows():
            conn.execute(
                sqlalchemy.text("""
                    UPDATE Funds_to_Screen 
                    SET EarliestPerformanceDate = :earliest_performance_date
                    WHERE SymbolCUSIP = :symbol
                """),
                {"earliest_performance_date": row["EarliestPerformanceDate"], "symbol": row["SymbolCUSIP"]}
            )
    print("✅ YCI Data Stored in Database.")
else:
    print("⚠️ No valid YCI data retrieved. Check API response.")

# ✅ Summary of Results
print("\n📊 **Summary:**")
print(f"✔️ Successfully retrieved: {len(df_yci)}")
print(f"❌ Failed requests: {len(funds) - len(df_yci)}")
print("🎯 Process Completed.")


In [44]:
#Add funds Inception Date to funds_to_screen table
import requests
import sqlalchemy
import pandas as pd
import time

# ✅ Database Connection String
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"
engine = sqlalchemy.create_engine(connection_string)

# ✅ Fetch Funds Missing `InceptionDate`
print("\n🔄 Fetching funds missing InceptionDate...")
query = """
    SELECT SymbolCUSIP, Fund_Type_ID
    FROM Funds_to_Screen
    WHERE InceptionDate IS NULL
"""
funds = pd.read_sql(query, engine)
print(f"✅ Retrieved {len(funds)} funds needing updates.\n")

# ✅ Headers Matching Excel's API Requests
headers = {
    "X-YCHARTSAUTHORIZATION": ycapi,  
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",  
    "X-YCHARTSEXCELVERSION": "4.4",  
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",  
    "X-YCHARTSIP": "",  
    "Host": "api.ycharts.com",
    "Connection": "Keep-Alive"
}

# ✅ Function to fetch `inception_date` for both ETFs & Mutual Funds
def fetch_yci_data(symbol, fund_type_id):
    """Fetch inception_date, handling ETFs and Mutual Funds separately."""
    
    if fund_type_id == 3:  # ✅ Mutual Funds use "M:" and `/mutual_funds/`
        api_url = f"https://api.ycharts.com/v3/mutual_funds/M:{symbol}/info/inception_date?retrieve_ttl=true"
        print(f"🔎 Requesting M:{symbol} (Mutual Fund) - inception_date...")
    else:  # ✅ ETFs use `/companies/`
        api_url = f"https://api.ycharts.com/v3/companies/{symbol}/info/inception_date?retrieve_ttl=true"
        print(f"🔎 Requesting {symbol} (ETF) - inception_date...")

    for attempt in range(5):  # Retry up to 5 times
        response = requests.get(api_url, headers=headers)

        if response.status_code == 200:
            data = response.json()
            query_symbol = f"M:{symbol}" if fund_type_id == 3 else symbol  # Ensure correct key lookup

            # ✅ Check if "results" key exists before accessing it
            if "response" in data and query_symbol in data["response"]:
                results = data["response"][query_symbol].get("results", {})

                if "inception_date" in results:
                    date = pd.to_datetime(results["inception_date"]["data"]).date()
                    print(f"✅ {query_symbol} - Retrieved inception_date: {date}")
                    return symbol, date
                else:
                    print(f"⚠️ {query_symbol} - No `inception_date` found in API response.")
                    return symbol, None
            else:
                print(f"⚠️ {query_symbol} - Unexpected API response format: {data}")
                return symbol, None

        elif response.status_code == 403:  # API limit hit
            wait_time = 120  # Wait 2 minutes before retrying
            print(f"⚠️ API limit hit for {query_symbol}. Waiting {wait_time} seconds before retry ({attempt+1}/5)...")
            time.sleep(wait_time)
        
        else:
            print(f"❌ {query_symbol} - Error {response.status_code}: {response.text}")
            return symbol, None  # Stop trying on other errors

    print(f"⛔ {query_symbol} - Failed after 5 retries.")
    return symbol, None

# ✅ Process all funds (0.1-second delay per request to prevent API bans)
data_list = []
for index, row in funds.iterrows():
    symbol = row["SymbolCUSIP"]
    fund_type_id = row["Fund_Type_ID"]

    result = fetch_yci_data(symbol, fund_type_id)
    if result[1]:  # Only keep successful responses
        data_list.append(result)

    time.sleep(0.1)  # ✅ Fast execution unless rate limits increase

# ✅ Convert API results to DataFrame
df_yci = pd.DataFrame(data_list, columns=["SymbolCUSIP", "InceptionDate"])

# ✅ Inspect DataFrame Before Writing to SQL
print("\n🔍 **YCI Data Preview:**")
print(df_yci.head())
print(df_yci.info())

# ✅ Store Data in SQL
if not df_yci.empty:
    with engine.begin() as conn:
        for index, row in df_yci.iterrows():
            conn.execute(
                sqlalchemy.text("""
                    UPDATE Funds_to_Screen 
                    SET InceptionDate = :inception_date
                    WHERE SymbolCUSIP = :symbol
                """),
                {"inception_date": row["InceptionDate"], "symbol": row["SymbolCUSIP"]}
            )
    print("✅ YCI Data Stored in Database.")
else:
    print("⚠️ No valid YCI data retrieved. Check API response.")

# ✅ Summary of Results
print("\n📊 **Summary:**")
print(f"✔️ Successfully retrieved: {len(df_yci)}")
print(f"❌ Failed requests: {len(funds) - len(df_yci)}")
print("🎯 Process Completed.")




🔄 Fetching funds missing InceptionDate...
✅ Retrieved 479 funds needing updates.

🔎 Requesting M:ARSYX (Mutual Fund) - inception_date...
✅ M:ARSYX - Retrieved inception_date: 1996-09-30
🔎 Requesting M:CBSYX (Mutual Fund) - inception_date...
✅ M:CBSYX - Retrieved inception_date: 1996-10-01
🔎 Requesting M:ABIYX (Mutual Fund) - inception_date...
✅ M:ABIYX - Retrieved inception_date: 2001-03-29
🔎 Requesting M:AAZYX (Mutual Fund) - inception_date...
✅ M:AAZYX - Retrieved inception_date: 2021-03-24
🔎 Requesting M:AUUYX (Mutual Fund) - inception_date...
✅ M:AUUYX - Retrieved inception_date: 2011-12-08
🔎 Requesting M:ATTYX (Mutual Fund) - inception_date...
✅ M:ATTYX - Retrieved inception_date: 2013-12-11
🔎 Requesting M:GOPIX (Mutual Fund) - inception_date...
✅ M:GOPIX - Retrieved inception_date: 2004-06-29
🔎 Requesting M:ADVDX (Mutual Fund) - inception_date...
✅ M:ADVDX - Retrieved inception_date: 2003-09-22
🔎 Requesting M:GWLIX (Mutual Fund) - inception_date...
✅ M:GWLIX - Retrieved inceptio

In [ ]:
#Batch metric into database with parallel processing, data check, and batch insertion - Grok

import math
import certifi
import ssl
import requests
import sqlalchemy
import pandas as pd
import datetime
from dateutil.relativedelta import relativedelta
import time
import concurrent.futures
from requests.adapters import HTTPAdapter

# Configuration
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)

YCHARTS_API_URL = "https://api.ycharts.com/v3/excel/points"

API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

METRIC = "three_total_monthly_return"

BATCH_SIZE = 5000  # Experiment with this value

# Create a custom SSL context
context = ssl.create_default_context()
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # For debugging only! Use CERT_REQUIRED for production.

# Custom HTTPAdapter to apply our SSL context
class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

# Create a session and mount the adapter for HTTPS requests
session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

# Date Configurations
TODAY = datetime.date.today()
END_DATE = datetime.date(TODAY.year, TODAY.month, 1) - datetime.timedelta(days=1)
TEN_YEARS_AGO = END_DATE.replace(year=END_DATE.year - 10)

def get_start_date(inception_date, earliest_perf_date, default_start):
    """Determine the start date for data fetching."""
    possible_starts = [date for date in (inception_date, earliest_perf_date) if pd.notnull(date)]
    if not possible_starts:
        return default_start
    return max(min(possible_starts), default_start)

def generate_month_end_dates(start_date, end_date):
    """Generate a list of month-end dates between start and end date."""
    dates = []
    current = start_date
    while current <= end_date:
        last_day = current.replace(day=1) + relativedelta(months=1) - datetime.timedelta(days=1)
        dates.append(last_day)
        current = last_day + datetime.timedelta(days=1)
    return dates

def build_points_lines(symbol, date, is_mutual):
    """Build lines for API payload in ycp format for one month."""
    symbol_prefix = "M:" if is_mutual else ""
    return f"{symbol_prefix}{symbol},{METRIC},{date.strftime('%Y-%m-%d')}"

def parse_ycp_response(json_data):
    """Parse the API response into a dictionary."""
    final_map = {}
    for symbol_key, symbol_block in json_data.get("response", {}).items():
        cleaned_sym = symbol_key.replace("M:", "")
        for metric_name, date_mapping in symbol_block.get("results", {}).items():
            for date_key, date_info in date_mapping.items():
                if len(date_info.get("results", [])) >= 2:
                    date_str, val = date_info["results"][:2]
                    if cleaned_sym not in final_map:
                        final_map[cleaned_sym] = {}
                    final_map[cleaned_sym][date_str] = {metric_name: val}
    return final_map

def insert_fund_data(engine, symbol, data_map):
    """Batch insert data for one fund into the database if data does not exist."""
    insert_sql = f"""
    INSERT INTO Fund_Returns_Timeseries (SymbolCUSIP, [Date], {METRIC})
    VALUES (:symbol, :date, :value)
    """
    batch_inserts = []
    
    for date_str, metric_data in data_map[symbol].items():
        for metric, value in metric_data.items():
            if value is not None:
                try:
                    date_obj = datetime.datetime.strptime(date_str, "%Y-%m-%d").date()
                    decimal_value = round(float(value), 6)
                    batch_inserts.append({
                        'symbol': symbol,
                        'date': date_obj,
                        'value': decimal_value
                    })
                    
                    # Insert batch if we've reached the defined batch size
                    if len(batch_inserts) >= BATCH_SIZE:
                        with engine.connect() as conn:
                            conn.execute(sqlalchemy.text(insert_sql), batch_inserts)
                            conn.commit()
                            print(f"Batch inserted {len(batch_inserts)} records for {symbol}")
                        batch_inserts = []  # Reset the batch
                except ValueError as ve:
                    print(f"Data conversion error for {symbol} on {date_str}: {ve}")

    # Insert any remaining records in the last batch
    if batch_inserts:
        with engine.connect() as conn:
            conn.execute(sqlalchemy.text(insert_sql), batch_inserts)
            conn.commit()
            print(f"Batch inserted {len(batch_inserts)} records for {symbol}")

def process_fund(fund_row):
    """Process one fund's data, fetch from API, store in memory, and batch insert into DB."""
    symbol = fund_row["SymbolCUSIP"]
    fund_type_id = fund_row["Fund_Type_ID"]
    inception_date = fund_row.get("InceptionDate")
    earliest_perf_date = fund_row.get("EarliestPerformanceDate")

    # Convert to date if they are Timestamp
    if isinstance(inception_date, pd.Timestamp):
        inception_date = inception_date.date()
    if isinstance(earliest_perf_date, pd.Timestamp):
        earliest_perf_date = earliest_perf_date.date()

    start_date = get_start_date(inception_date, earliest_perf_date, TEN_YEARS_AGO)
    if not start_date:
        print(f"Skipping {symbol}: no valid start date.")
        return

    date_list = generate_month_end_dates(start_date, END_DATE)
    if not date_list:
        print(f"Skipping {symbol}: no month-end dates.")
        return

    is_mutual = (fund_type_id == 3)
    data_map = {}

    for date in date_list:
        # Check if data for the specific metric already exists in the database
        engine = sqlalchemy.create_engine(connection_string)
        with engine.connect() as conn:
            check_sql = f"""
            SELECT 1 FROM Fund_Returns_Timeseries 
            WHERE SymbolCUSIP = :symbol 
              AND [Date] = :date 
              AND {METRIC} IS NOT NULL
            """
            params = {
                'symbol': symbol,
                'date': date
            }
            result = conn.execute(sqlalchemy.text(check_sql), params).fetchone()
            
            if result:  # Data for this specific metric exists, skip API call
                print(f"Data for {symbol} on {date} for metric '{METRIC}' already in database, skipping API call.")
                continue

        payload = f"points={build_points_lines(symbol, date, is_mutual)}"

        start_time = time.time()
        try:
            response = session.post(YCHARTS_API_URL, headers=API_HEADERS, data=payload)
            api_time = time.time() - start_time
            print(f"API call for {symbol} on {date} took {api_time:.2f} seconds")

            parsed_data = parse_ycp_response(response.json())
            if parsed_data and symbol in parsed_data:
                if symbol not in data_map:
                    data_map[symbol] = {}
                data_map[symbol].update(parsed_data[symbol])
            else:
                print(f"No data returned for {symbol} for {date}")

        except requests.exceptions.RequestException as e:
            print(f"API error for {symbol} for {date}: {e}")

        time.sleep(0.1)  # Small delay to avoid rate limiting

    if data_map:  # Only proceed with insertion if we have data
        insert_fund_data(engine, symbol, data_map)

    total_time = time.time() - start_time
    print(f"Total processing time for {symbol}: {total_time:.2f} seconds")

def main():
    print(f"🚀 Loading Metric: {METRIC}")
    
    start_read_time = time.time()
    engine = sqlalchemy.create_engine(connection_string)
    sql = """
    SELECT 
      SymbolCUSIP,
      Fund_Type_ID,
      InceptionDate,
      EarliestPerformanceDate
    FROM Funds_to_Screen
    WHERE SymbolCUSIP IS NOT NULL
    """
    all_funds_df = pd.read_sql(sql, engine)
    engine.dispose()
    end_read_time = time.time()
    print(f"🔎 Reading funds took {end_read_time - start_read_time:.2f} seconds")

    print(f"🔎 Found {len(all_funds_df)} funds.\n")

    # Convert DataFrame to list of dictionaries for processing
    funds_list = all_funds_df.to_dict(orient='records')

    # Number of threads can be adjusted based on your system capabilities
    num_threads = min(20, len(funds_list))  # Maximum 20 threads or number of funds if less than 20

    with concurrent.futures.ThreadPoolExecutor(max_workers=num_threads) as executor:
        # Map process_fund to each fund in the list
        future_to_fund = {executor.submit(process_fund, fund_row): fund_row for fund_row in funds_list}
        for future in concurrent.futures.as_completed(future_to_fund):
            fund_row = future_to_fund[future]
            try:
                future.result()  # Wait for the result without printing it
            except Exception as exc:
                symbol = fund_row['SymbolCUSIP']
                print(f'Processing fund {symbol} generated an exception: {exc}')

    print(f"\n🎉 All done loading metric={METRIC}!")

if __name__ == "__main__":
    main()

🚀 Loading Metric: three_total_monthly_return
🔎 Reading funds took 0.16 seconds
🔎 Found 1058 funds.

API call for HIPS on 2015-01-31 took 0.62 secondsAPI call for EAOK on 2020-06-30 took 0.66 seconds
API call for DYTA on 2023-03-31 took 0.63 seconds

API call for EAOA on 2020-06-30 took 0.69 seconds
API call for AOK on 2015-01-31 took 0.64 seconds
API call for INCM on 2023-06-30 took 0.75 seconds
API call for ICVT on 2015-06-30 took 0.69 seconds
API call for RORO on 2020-11-30 took 0.64 seconds
API call for GHTA on 2021-11-30 took 0.63 seconds
API call for LEXI on 2021-06-30 took 0.67 seconds
API call for CGBL on 2023-09-30 took 0.67 seconds
API call for NTSX on 2018-08-31 took 0.64 seconds
API call for ZHDG on 2021-07-31 took 0.74 seconds
API call for AOR on 2015-01-31 took 0.76 seconds
API call for AOM on 2015-01-31 took 0.69 seconds
API call for EAOR on 2020-06-30 took 0.69 seconds
API call for TFPN on 2023-07-31 took 0.80 seconds
API call for EAOM on 2020-06-30 took 0.76 seconds
API

In [7]:
#Batching of one metric using TS from YC, with parallel processing data check and batch inserts- Grok
#CHANGE VARIABLES: METRIC AND DATABASE NAME... THIS CODE IS 1 METRIC AT A TIME.

import math
import certifi
import ssl
import requests
import sqlalchemy
import pandas as pd
import datetime
from dateutil.relativedelta import relativedelta
import time
import concurrent.futures
from requests.adapters import HTTPAdapter

# Configuration
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)

YCHARTS_API_URL = "https://api.ycharts.com/v3"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

# New variable for metric configuration
METRIC = "five_year_total_monthly_return"
METRIC_DB_NAME = "5 Year Return"
BATCH_SIZE = 5000  # Experiment with this value

# Create a custom SSL context
context = ssl.create_default_context()
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # For debugging only! Use CERT_REQUIRED for production.

# Custom HTTPAdapter to apply our SSL context
class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

# Create a session and mount the adapter for HTTPS requests
session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

# Date Configurations
TODAY = datetime.date.today()
END_DATE = (TODAY.replace(day=1) - datetime.timedelta(days=1)).replace(year=2025, month=1)  # Last day of January 2025
TEN_YEARS_AGO = END_DATE.replace(year=END_DATE.year - 10)

def get_start_date(inception_date, earliest_perf_date, default_start):
    """Determine the start date for data fetching."""
    possible_starts = [date for date in (inception_date, earliest_perf_date) if pd.notnull(date)]
    if not possible_starts:
        return default_start
    return max(min(possible_starts), default_start)

def insert_fund_data(engine, symbol, data_map):
    insert_sql = """
    INSERT INTO Fund_Returns_Timeseries (SymbolCUSIP, Date, ReturnValue, Metric)
    VALUES (:symbol, :date, :value, :metric)
    """
    batch_inserts = []
    
    for date_str, metric_data in data_map[symbol].items():
        for metric, value in metric_data.items():
            if value is not None:
                try:
                    date_obj = datetime.datetime.strptime(date_str, "%Y-%m-%d").date()
                    decimal_value = round(float(value), 6)  # Convert to float then round for DECIMAL
                    batch_inserts.append({
                        'symbol': symbol,
                        'date': date_obj,
                        'value': decimal_value,
                        'metric': METRIC_DB_NAME  # Using the new variable for database metric name
                    })
                    
                    if len(batch_inserts) >= BATCH_SIZE:
                        with engine.connect() as conn:
                            conn.execute(sqlalchemy.text(insert_sql), batch_inserts)
                            conn.commit()
                        batch_inserts = []  # Reset the batch
                except ValueError as ve:
                    print(f"Data conversion error for {symbol} on {date_str}: {ve}")

    if batch_inserts:
        with engine.connect() as conn:
            conn.execute(sqlalchemy.text(insert_sql), batch_inserts)
            conn.commit()

def process_fund(fund_row, engine):  
    symbol = fund_row["SymbolCUSIP"]
    fund_type_id = fund_row["Fund_Type_ID"]
    inception_date = fund_row.get("InceptionDate")
    earliest_perf_date = fund_row.get("EarliestPerformanceDate")

    # Convert to date if they are Timestamp
    if isinstance(inception_date, pd.Timestamp):
        inception_date = inception_date.date()
    if isinstance(earliest_perf_date, pd.Timestamp):
        earliest_perf_date = earliest_perf_date.date()

    start_date = get_start_date(inception_date, earliest_perf_date, TEN_YEARS_AGO)
    if not start_date:
        print(f"Skipping {symbol}: no valid start date.")
        return

    # Ensure start_date is formatted correctly
    start_date_str = start_date.strftime('%Y-%m-%d')
    end_date_str = END_DATE.strftime('%Y-%m-%d')

    is_mutual = (fund_type_id == 3)
    symbol_for_api = f"M:{symbol}" if is_mutual else symbol
    api_endpoint = "mutual_funds" if is_mutual else "companies"

    print(f"Fetching data for {symbol}")

    api_url = f"{YCHARTS_API_URL}/{api_endpoint}/{symbol_for_api}/series/{METRIC}?retrieve_ttl=true&start_date={start_date_str}&end_date={end_date_str}"

    try:
        response = session.get(api_url, headers=API_HEADERS)
        response.raise_for_status()  # Will raise an HTTPError if the HTTP request returned an unsuccessful status code

        parsed_data = response.json()
        data_map = {}

        # Parse the JSON response
        if 'response' in parsed_data and symbol_for_api in parsed_data['response']:
            for date, value in parsed_data['response'][symbol_for_api]['results'][METRIC]['data']:
                if symbol not in data_map:
                    data_map[symbol] = {}
                data_map[symbol][date] = {METRIC: value}

    except requests.exceptions.RequestException as e:
        print(f"API error for {symbol}: {e}")

    if data_map:  
        print(f"Inserting {symbol} into DB")
        insert_fund_data(engine, symbol, data_map)

def main():
    print(f"🚀 Loading Metric: {METRIC}")
    
    start_time = time.time()
    
    engine = sqlalchemy.create_engine(connection_string)
    sql = """
    SELECT 
      SymbolCUSIP,
      Fund_Type_ID,
      InceptionDate,
      EarliestPerformanceDate
    FROM Funds_to_Screen
    WHERE SymbolCUSIP IS NOT NULL
    """
    all_funds_df = pd.read_sql(sql, engine)
    # Keep engine open for use by all threads

    print(f"🔎 Found {len(all_funds_df)} funds.\n")

    funds_list = all_funds_df.to_dict(orient='records')

    with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
        futures = []
        for fund_row in funds_list:
            futures.append(executor.submit(process_fund, fund_row, engine))  # Pass 'engine' to process_fund
        
        for future in concurrent.futures.as_completed(futures):
            try:
                future.result()
            except Exception as exc:
                print(f'An error occurred: {exc}')

    total_time = time.time() - start_time
    print(f"\n🎉 All done loading metric={METRIC}! Total time: {total_time:.2f} seconds")

    # Optionally, dispose of the engine after all operations are complete
    engine.dispose()

if __name__ == "__main__":
    main()

🚀 Loading Metric: five_year_total_monthly_return
🔎 Found 1058 funds.

Fetching data for NTSX
Fetching data for HIPS
Fetching data for EAOA
Fetching data for AOM
Fetching data for AOK
Fetching data for EAOK
Fetching data for EAOM
Fetching data for INCM
Fetching data for ICVT
Fetching data for ZHDG
Fetching data for DYTA
Fetching data for LEXI
Fetching data for RORO
Fetching data for TFPN
Fetching data for BAMY
Fetching data for CGBL
Fetching data for AOR
Fetching data for EAOR
Fetching data for BAMO
Fetching data for GHTA
Fetching data for MPRO
Fetching data for HCMT
Inserting NTSX into DB
Fetching data for THY
Inserting HIPS into DB
Fetching data for SPAX
Fetching data for FMF
Inserting AOM into DB
Fetching data for CTA
Fetching data for FAAR
Fetching data for VEGA
Inserting AOR into DB
Fetching data for BUYW
Fetching data for FTLS
Fetching data for FFLS
Fetching data for CLSE
Fetching data for LBAY
Fetching data for EQLS
Inserting ICVT into DB
Fetching data for SPCX
Fetching data for 

In [11]:
#Batching of multiple metrics using TS from YC, with parallel processing data check and batch inserts- Grok

# Batch processing of multiple metrics using YCharts Timeseries API, with parallel processing, 
# data existence check, and batch inserts - Grok

import math
import certifi
import ssl
import requests
import sqlalchemy
import pandas as pd
import datetime
from dateutil.relativedelta import relativedelta
import time
import concurrent.futures
from requests.adapters import HTTPAdapter

# Configuration
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)

YCHARTS_API_URL = "https://api.ycharts.com/v3"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

METRICS = [
    ("five_year_total_monthly_return", "5 Year Return"),
    ("three_year_total_monthly_return", "3 Year Return"),
    ("one_year_total_monthly_return", "1 Year Return"),
    ("nine_total_monthly_return", "9 Month Return"),
    ("six_total_monthly_return", "6 Month Return"),
    ("three_total_monthly_return", "3 Month Return"),
    ("total_monthly_return", "1 Month Return")
]

BATCH_SIZE = 5000  # Experiment with this value

# Create a custom SSL context
context = ssl.create_default_context()
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # For debugging only! Use CERT_REQUIRED for production.

# Custom HTTPAdapter to apply our SSL context
class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

# Create a session and mount the adapter for HTTPS requests
session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

# Date Configurations
TODAY = datetime.date.today()
END_DATE = (TODAY.replace(day=1) - datetime.timedelta(days=1)).replace(year=2025, month=1)  # Last day of January 2025
TEN_YEARS_AGO = END_DATE.replace(year=END_DATE.year - 10)

def get_start_date(inception_date, earliest_perf_date, default_start):
    """Determine the start date for data fetching."""
    possible_starts = [date for date in (inception_date, earliest_perf_date) if pd.notnull(date)]
    if not possible_starts:
        return default_start
    return max(min(possible_starts), default_start)

def check_existing_data(engine, symbol, metric_db_name, start_date, end_date):
    """Check if there's data for the fund, metric, and date range in the database."""
    check_sql = """
    SELECT COUNT(*) 
    FROM Fund_Returns_Timeseries 
    WHERE SymbolCUSIP = :symbol 
      AND Metric = :metric 
      AND Date BETWEEN :start_date AND :end_date
    """
    with engine.connect() as conn:
        count = conn.execute(sqlalchemy.text(check_sql), {
            'symbol': symbol,
            'metric': metric_db_name,
            'start_date': start_date,
            'end_date': end_date
        }).scalar()
        return count > 0  # True if data exists, False otherwise

def insert_fund_data(engine, batch_data, batch_size=5000):
    """Insert data into the database in batches, checking for duplicates."""
    insert_sql = """
    INSERT INTO Fund_Returns_Timeseries (SymbolCUSIP, Date, ReturnValue, Metric)
    VALUES (:symbol, :date, :value, :metric)
    """
    
    check_sql = """
    SELECT 1 
    FROM Fund_Returns_Timeseries 
    WHERE SymbolCUSIP = :symbol 
      AND Date = :date 
      AND Metric = :metric
    """
    
    unique_data = []
    inserted_count = 0
    with engine.connect() as conn:
        try:
            for item in batch_data:
                existing = conn.execute(sqlalchemy.text(check_sql), item).fetchone()
                if not existing:  # Data doesn't exist, proceed with insert
                    unique_data.append(item)
                    inserted_count += 1
                    if len(unique_data) >= batch_size:
                        conn.execute(sqlalchemy.text(insert_sql), unique_data)
                        conn.commit()
                        unique_data = []  # Reset the batch
            if unique_data:  # Insert any remaining data
                conn.execute(sqlalchemy.text(insert_sql), unique_data)
                conn.commit()
            print(f"Inserted {inserted_count} new data points out of {len(batch_data)}.")
        except sqlalchemy.exc.SQLAlchemyError as sqle:
            print(f"Database error in batch insert: {sqle}")
            conn.rollback()
    return inserted_count

def process_fund(fund_row, metric, metric_db_name, engine):
    """Process each fund for a specific metric, check existing data before API call."""
    symbol = fund_row["SymbolCUSIP"]
    fund_type_id = fund_row["Fund_Type_ID"]
    inception_date = fund_row.get("InceptionDate")
    earliest_perf_date = fund_row.get("EarliestPerformanceDate")

    # Convert to date if they are Timestamp
    if isinstance(inception_date, pd.Timestamp):
        inception_date = inception_date.date()
    if isinstance(earliest_perf_date, pd.Timestamp):
        earliest_perf_date = earliest_perf_date.date()

    start_date = get_start_date(inception_date, earliest_perf_date, TEN_YEARS_AGO)
    if not start_date:
        print(f"Skipping {symbol} for {metric}: no valid start date.")
        return None

    # Check if data already exists for this fund, metric, and date range
    if check_existing_data(engine, symbol, metric_db_name, start_date, END_DATE):
        print(f"Data for {symbol} and {metric} already exists, skipping API call.")
        return None

    # Ensure start_date is formatted correctly
    start_date_str = start_date.strftime('%Y-%m-%d')
    end_date_str = END_DATE.strftime('%Y-%m-%d')

    is_mutual = (fund_type_id == 3)
    symbol_for_api = f"M:{symbol}" if is_mutual else symbol
    api_endpoint = "mutual_funds" if is_mutual else "companies"

    print(f"Fetching {metric} data for {symbol}")

    api_url = f"{YCHARTS_API_URL}/{api_endpoint}/{symbol_for_api}/series/{metric}?retrieve_ttl=true&start_date={start_date_str}&end_date={end_date_str}"

    try:
        response = session.get(api_url, headers=API_HEADERS)
        response.raise_for_status()  # Will raise an HTTPError if the HTTP request returned an unsuccessful status code

        parsed_data = response.json()
        data_map = {}

        # Parse the JSON response
        if 'response' in parsed_data and symbol_for_api in parsed_data['response']:
            for date, value in parsed_data['response'][symbol_for_api]['results'][metric]['data']:
                if symbol not in data_map:
                    data_map[symbol] = {}
                data_map[symbol][date] = {metric: value}

    except requests.exceptions.RequestException as e:
        print(f"API error for {symbol} on metric {metric}: {e}")
        return None

    if data_map:  
        print(f"Processed {symbol} for {metric}")
        return data_map
    return None

def main():
    start_time = time.time()
    
    engine = sqlalchemy.create_engine(connection_string, 
                                      pool_size=20, 
                                      max_overflow=50,
                                      pool_timeout=300)  # Increase pool size and overflow
    sql = """
    SELECT 
      SymbolCUSIP,
      Fund_Type_ID,
      InceptionDate,
      EarliestPerformanceDate
    FROM Funds_to_Screen
    WHERE SymbolCUSIP IS NOT NULL
    """
    all_funds_df = pd.read_sql(sql, engine)
    funds_list = all_funds_df.to_dict(orient='records')

    total_inserted = 0
    for metric, metric_db_name in METRICS:
        print(f"\n🚀 Loading Metric: {metric}")
        all_data = []  # Collect all data for this metric
        
        with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
            futures = []
            for fund_row in funds_list:
                futures.append(executor.submit(process_fund, fund_row, metric, metric_db_name, engine))  
            
            for future in concurrent.futures.as_completed(futures):
                try:
                    data_map = future.result()
                    if data_map:
                        for symbol, dates in data_map.items():
                            for date_str, metric_data in dates.items():
                                for metric_val, value in metric_data.items():
                                    if value is not None:
                                        try:
                                            date_obj = datetime.datetime.strptime(date_str, "%Y-%m-%d").date()
                                            decimal_value = round(float(value), 6)
                                            all_data.append({
                                                'symbol': symbol,
                                                'date': date_obj,
                                                'value': decimal_value,
                                                'metric': metric_db_name
                                            })
                                        except ValueError as ve:
                                            print(f"Data conversion error for {symbol} on {date_str}: {ve}")
                except Exception as exc:
                    print(f'An error occurred for {metric}: {exc}')

        # Insert all collected data in one go
        if all_data:
            total_inserted += insert_fund_data(engine, all_data)

    total_time = time.time() - start_time
    print(f"\n🎉 All done loading all metrics! Total time: {total_time:.2f} seconds")
    print(f"Total data points inserted: {total_inserted}")
    print(f"Total funds processed: {len(funds_list)}")
    print(f"Average time per fund per metric: {total_time / (len(funds_list) * len(METRICS)):.2f} seconds")

    # Check pool status for debugging
    pool_stats = engine.pool.status()
    print(f"Pool Status: {pool_stats}")

    engine.dispose()

if __name__ == "__main__":
    main()


🚀 Loading Metric: five_year_total_monthly_return
Fetching five_year_total_monthly_return data for ZHDG
Fetching five_year_total_monthly_return data for GHTA
Data for AOM and five_year_total_monthly_return already exists, skipping API call.
Fetching five_year_total_monthly_return data for MPRO
Fetching five_year_total_monthly_return data for TFPN
Fetching five_year_total_monthly_return data for INCM
Fetching five_year_total_monthly_return data for HCMT
Fetching five_year_total_monthly_return data for THY
Fetching five_year_total_monthly_return data for SPAX
Fetching five_year_total_monthly_return data for DYTA
Fetching five_year_total_monthly_return data for BAMY
Data for FAAR and five_year_total_monthly_return already exists, skipping API call.
Fetching five_year_total_monthly_return data for LEXI
Data for VEGA and five_year_total_monthly_return already exists, skipping API call.
Fetching five_year_total_monthly_return data for BUYW
Fetching five_year_total_monthly_return data for EAO

In [18]:
#Data extraction to prep logic for factor regressions

from sqlalchemy import create_engine, text
import pandas as pd
import openpyxl

# Database Connection
engine = create_engine('mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes')

# Fetch data from Funds_to_Screen
funds_data = pd.read_sql_query("""
    SELECT ProductName, SymbolCUSIP, YC_Broad_Category_ID, YC_Broad_Asset_Class_ID, 
           YC_Global_Category_ID, YC_Category_ID, CWA_Broad_Category_ID
    FROM Funds_to_Screen
""", engine)

# Function to fetch names for IDs from a given table
def fetch_names_for_ids(df, column, table_name, name_column):
    query = f"""
    SELECT {table_name}.ID, {table_name}.{name_column} AS Name
    FROM {table_name}
    """
    names_data = pd.read_sql_query(query, engine)
    return df.merge(names_data, left_on=column, right_on='ID', how='left').drop(columns=['ID'])

# Mapping for table and column names
table_name_mapping = {
    'YC_Broad_Category_ID': ('YC_Broad_Category_List', 'Broad_Category_Name'),
    'YC_Broad_Asset_Class_ID': ('YC_Broad_Asset_Class_List', 'Broad_Asset_Class_Name'),
    'YC_Global_Category_ID': ('YC_Global_Category_List', 'Global_Category_Name'),
    'YC_Category_ID': ('YC_Category_List', 'Category_Name'),
    'CWA_Broad_Category_ID': ('CWA_Broad_Category_List', 'CWA_Broad_Category_Name')
}

# Fetch names for each category
for column in ['YC_Broad_Category_ID', 'YC_Broad_Asset_Class_ID', 'YC_Global_Category_ID', 'YC_Category_ID', 'CWA_Broad_Category_ID']:
    list_table, name_column = table_name_mapping.get(column, (None, None))  # Use None if not found
    if list_table and name_column:
        funds_data = fetch_names_for_ids(funds_data, column, list_table, name_column)
        funds_data = funds_data.rename(columns={'Name': column + '_Name'})

# Output to Excel - First sheet
with pd.ExcelWriter('Funds_to_Screen_With_Names.xlsx', engine='openpyxl') as writer:
    funds_data.to_excel(writer, index=False, sheet_name='Fund Information')
    
    # Create a second sheet with unique combinations of IDs and their names
    id_columns = ['YC_Broad_Category_ID', 'YC_Broad_Asset_Class_ID', 'YC_Global_Category_ID', 'YC_Category_ID', 'CWA_Broad_Category_ID']
    name_columns = [col + '_Name' for col in id_columns]
    all_columns = id_columns + name_columns

    # Get unique combinations including both IDs and names
    unique_combinations = funds_data[all_columns].drop_duplicates().reset_index(drop=True)
    
    # Write unique combinations to a new sheet
    unique_combinations.to_excel(writer, index=False, sheet_name='Unique ID Combinations')

print("Data has been written to Funds_to_Screen_With_Names.xlsx with two sheets.")

Data has been written to Funds_to_Screen_With_Names.xlsx with two sheets.


In [10]:
#Run rolling factor regressions on each fund and update DB

import time
import rpy2.robjects as robjects
from rpy2.robjects.packages import importr
from rpy2.robjects import pandas2ri
from rpy2.robjects.conversion import localconverter, get_conversion
from sqlalchemy import create_engine
import pandas as pd
import logging

# Set up logging
logging.basicConfig(level=logging.DEBUG, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# ----------------------------------------------------
# 0) INITIAL SETUP
# ----------------------------------------------------
start_time = time.time()

# Setup R environment
base = importr('base')
aqrr = importr('aqrr')
stats = importr('stats')
dplyr = importr('dplyr')
pandas2ri.activate()

# Database Connection (adjust for your environment)
engine = create_engine(
    'mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database'
    '?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes'
)

# ----------------------------------------------------
# 1) DETERMINE REGION LOGIC
# ----------------------------------------------------
region_logic = {
    (1, 65, None): 'USA',
    (1, 66, None): 'USA',
    (1, 67, None): 'USA',
    (1, 100, None): 'Global',
    (1, 33, None): 'Global',
    (1, 7, None): 'USA',
    (1, 1, None): 'Global',
    (2, 99, None): 'USA',
    (2, 57, None): 'USA',
    (2, 22, None): 'USA',
    (2, 25, None): 'USA',
    (2, 69, None): 'USA',
    (2, 40, None): 'Global',
    (3, None, None): 'USA',
    (5, None, None): 'Global',
    (6, None, None): 'Global Ex USA',
    (11, None, None): 'Global Ex USA',
    (12, None, None): 'Global',
    (13, None, None): 'Global',
    (14, None, None): 'Global Ex USA',
    (16, None, None): 'USA',
    (17, None, None): 'USA',
    (18, None, None): 'USA',
    (19, 88, None): 'Global Ex USA',
    (19, 55, None): 'Global Ex USA',
    (19, 24, None): 'Global Ex USA',
    (19, 3, None): 'Global Ex USA',
    (20, None, None): 'USA',
    (21, None, None): 'USA',
    (22, None, None): 'USA',
    (23, 13, None): 'USA',
    (23, 33, 38): 'USA',
    (23, 100, None): 'USA',
    (23, 59, None): 'USA',
    (23, 1, None): 'USA',
    (23, 54, None): 'USA',
    (23, 33, 2): 'Global',
    (23, 33, 39): 'Global',
    (24, None, None): 'USA',
    (28, None, None): 'USA'
}

def determine_region(cwa_broad_category_id, yc_category_id, yc_global_category_id):
    """
    Determine the region based on category IDs.
    """
    for key, region in region_logic.items():
        if (key[0] == cwa_broad_category_id or key[0] is None) and \
           (key[1] == yc_category_id or key[1] is None) and \
           (key[2] == yc_global_category_id or key[2] is None):
            return region
    return 'USA'  # Default if no match

# ----------------------------------------------------
# 2) FACTOR SELECTION LOGIC
# ----------------------------------------------------
factor_selection = {
    # ... (as before, unchanged)
}

# ----------------------------------------------------
# 3) MAP FACTOR -> COLUMN NAME (PER REGION)
# ----------------------------------------------------
factor_to_aqr = {
    'Market':       {'USA': 'MKT', 'Global': 'MKT', 'Global Ex USA': 'MKT'},
    'Factor Premia':{'USA': 'Factor_Premia', 'Global': 'Factor_Premia', 'Global Ex USA': 'Factor_Premia'},
    'HML':          {'USA': 'HML_Devil', 'Global': 'HML_Devil', 'Global Ex USA': 'HML_Devil'},
    'SMB':          {'USA': 'SMB', 'Global': 'SMB', 'Global Ex USA': 'SMB'},
    'UMD':          {'USA': 'UMD', 'Global': 'UMD', 'Global Ex USA': 'UMD'},
    'Trend':        {'USA': 'Momentum', 'Global': 'Momentum', 'Global Ex USA': 'Momentum'},
    'QMJ':          {'USA': 'QMJ', 'Global': 'QMJ', 'Global Ex USA': 'QMJ'},
    'BAB':          {'USA': 'BAB', 'Global': 'BAB', 'Global Ex USA': 'BAB'},
    'Credit':       {'USA': 'Credit_Risk_Premium', 'Global': 'Credit_Risk_Premium', 'Global Ex USA': 'Credit_Risk_Premium'},
    'Commodities':  {'USA': 'Commodities_Long_Run', 'Global': 'Commodities_Long_Run', 'Global Ex USA': 'Commodities_Long_Run'}
}

# ----------------------------------------------------
# 4) MAP FACTOR -> AQR FUNCTION NAME
# ----------------------------------------------------
aqr_functions = {
    'aqr_hml_devil_monthly':      aqrr.aqr_hml_devil_monthly,
    'aqr_bab_monthly':            aqrr.aqr_bab_monthly,
    'aqr_mkt_monthly':            aqrr.aqr_mkt_monthly,
    'aqr_qmj_monthly':            aqrr.aqr_qmj_monthly,
    'aqr_smb_monthly':            aqrr.aqr_smb_monthly,
    'aqr_umd_monthly':            aqrr.aqr_umd_monthly,
    'aqr_momentum_monthly':       aqrr.aqr_momentum_monthly,
    'aqr_factor_premia_monthly':  aqrr.aqr_factor_premia_monthly,
    'aqr_credit_risk_premium':    aqrr.aqr_credit_risk_premium,
    'aqr_commodities_long_run':   aqrr.aqr_commodities_long_run
}

# Matches each factor name to the *key* in the aqr_functions dict above
factor_to_aqr_function = {
    'Market':         'aqr_mkt_monthly',
    'Factor Premia':  'aqr_factor_premia_monthly',
    'HML':            'aqr_hml_devil_monthly',
    'SMB':            'aqr_smb_monthly',
    'UMD':            'aqr_umd_monthly',
    'Trend':          'aqr_momentum_monthly',
    'QMJ':            'aqr_qmj_monthly',
    'BAB':            'aqr_bab_monthly',
    'Credit':         'aqr_credit_risk_premium',
    'Commodities':    'aqr_commodities_long_run'
}

# ----------------------------------------------------
# 5) AQR REGION MAPPING: match your code's "GLOBAL" → dataset's "Global"
# ----------------------------------------------------
region_aqr_mapping = {
    'USA': 'USA',
    'Global': 'Global',
    'Global Ex USA': 'Global Ex USA'
}

# Exclude lists for regions, not used in this script but included for reference
USA_Excludes = ["AUS", "AUT", "BEL", "CAN", "CHE", "DEU", "DNK","ESP", "FIN", "FRA", "GBR", "GRC", "HKG", "IRL", "ISR", "ITA", "JPN", "NLD", "NOR", "NZL", "PRT", "SGP", "SWE", "Global", "Global Ex USA", "Europe", "North America"]
Global_Excludes = ["AUS", "AUT", "BEL", "CAN", "CHE", "DEU", "DNK","ESP", "FIN", "FRA", "GBR", "GRC", "HKG", "IRL", "ISR", "ITA", "JPN", "NLD", "NOR", "NZL", "PRT", "SGP", "SWE", "USA", "Global Ex USA", "Europe", "North America"]
Global_X_USA_Excludes = ["AUS", "AUT", "BEL", "CAN", "CHE", "DEU", "DNK","ESP", "FIN", "FRA", "GBR", "GRC", "HKG", "IRL", "ISR", "ITA", "JPN", "NLD", "NOR", "NZL", "PRT", "SGP", "SWE", "Global", "USA", "Europe", "North America"]

# ----------------------------------------------------
# 6) FETCH FUND INFO & RETURNS
# ----------------------------------------------------
fund_info = pd.read_sql_query(
    "SELECT SymbolCUSIP, CWA_Broad_Category_ID, YC_Category_ID, YC_Global_Category_ID FROM Funds_to_Screen",
    engine
)
logger.debug(f"Fund Info fetched: {fund_info.shape}")

fund_returns = pd.read_sql_query(
    """
    SELECT SymbolCUSIP AS Symbol, Date, Metric AS [1mReturn]
    FROM Fund_Returns_Timeseries
    WHERE Metric = '1 Month Return'
    """,
    engine
)
fund_returns['Date'] = pd.to_datetime(fund_returns['Date'])
logger.debug(f"Fund Returns fetched: {fund_returns.shape}")

# ----------------------------------------------------
# 7) FETCH AQR DATA FOR A SPECIFIC FACTOR & REGION
# ----------------------------------------------------
def fetch_aqr_data(aqr_func, region_key):
    """
    Fetch AQR data for a specific region and convert to pandas DataFrame.
    If the dataset has a 'name' column, we'll filter on the mapped region.
    'region_key' is your internal region, like 'Global' or 'USA'.
    """
    actual_region = region_aqr_mapping.get(region_key, None)
    if actual_region is None:
        logger.warning(f"Region '{region_key}' not recognized in region_aqr_mapping.")
        return pd.DataFrame()

    # Convert R object to Pandas
    with localconverter(robjects.default_converter + pandas2ri.converter):
        r_data = aqr_func()
        df = get_conversion().rpy2py(r_data)

    # Filter by region if 'name' column exists
    if 'name' in df.columns:
        df = df[df['name'] == actual_region]

    if df.empty:
        logger.info(f"No data returned from function (region='{actual_region}')")
        return pd.DataFrame()

    # Standard rename
    df = df.rename(columns={'date': 'Date', 'value': 'Value'})
    df['Date'] = pd.to_datetime(df['Date'])

    return df[['Date', 'Value']]

# ----------------------------------------------------
# 8) PREPARE FACTOR DATA FOR A GIVEN REGION
# ----------------------------------------------------
def prepare_factor_data(region):
    """
    Build a wide DataFrame of factor columns for the given region.
    Each factor's column is named according to factor_to_aqr[factor][region].
    """
    logger.debug(f"Preparing factor data for region: {region}")
    factor_data_list = []

    for factor, func_key in factor_to_aqr_function.items():
        if region not in factor_to_aqr[factor]:
            logger.warning(f"Factor '{factor}' not available for region '{region}'")
            continue

        if func_key not in aqr_functions:
            logger.warning(f"Missing function '{func_key}' for factor '{factor}'")
            continue

        aqr_func = aqr_functions[func_key]
        df = fetch_aqr_data(aqr_func, region)
        if df.empty:
            logger.warning(f"No factor data returned for '{factor}' with region='{region}'")
            continue

        new_col = factor_to_aqr[factor][region]
        df = df.rename(columns={'Value': new_col})
        factor_data_list.append(df)

    if not factor_data_list:
        logger.warning(f"No factor data collected for region '{region}'")
        return pd.DataFrame()

    factor_data = factor_data_list[0]
    for other_df in factor_data_list[1:]:
        factor_data = pd.merge(factor_data, other_df, on='Date', how='outer')

    factor_data.sort_values('Date', inplace=True)
    factor_data.reset_index(drop=True, inplace=True)
    logger.debug(f"Factor data for {region} prepared. Shape: {factor_data.shape}")
    return factor_data

# ----------------------------------------------------
# 9) ROLLING MULTI-LINEAR REGRESSION
# ----------------------------------------------------
def run_multilinear_regression_r(fund_symbol, fund_data, factor_data, factors, window):
    """
    Run multilinear regression in R for a rolling window (e.g. 12 months).
    'factors' is a list of factor-data column names, e.g. ['MKT', 'SMB', 'HML_Devil'].
    """
    logger.debug(f"Starting regression for {fund_symbol} with factors: {factors}")

    fund_data_sym = fund_data[fund_data['Symbol'] == fund_symbol]
    if fund_data_sym.empty:
        logger.warning(f"No return data for symbol={fund_symbol}")
        return pd.DataFrame()

    merged_data = pd.merge(fund_data_sym, factor_data[['Date'] + factors], on='Date', how='inner')
    merged_data.sort_values('Date', inplace=True)
    merged_data.reset_index(drop=True, inplace=True)
    
    if merged_data.empty:
        logger.warning(f"Merged data is empty for {fund_symbol}")
        return pd.DataFrame()

    all_results = []
    for i in range(len(merged_data) - window + 1):
        window_data = merged_data.iloc[i : i + window]
        if len(window_data) < window:
            continue

        with localconverter(robjects.default_converter + pandas2ri.converter):
            r_df = get_conversion().py2rpy(window_data)

        formula = '1mReturn ~ ' + ' + '.join(factors)
        model = stats.lm(robjects.Formula(formula), data=r_df)
        summary = stats.summary_lm(model)

        with localconverter(robjects.default_converter + pandas2ri.converter):
            coefs = get_conversion().rpy2py(summary.rx2('coefficients'))

        result = {
            'Date':   window_data['Date'].iloc[-1],
            'Symbol': fund_symbol
        }
        for coef_name in coefs.index:
            result[coef_name]            = coefs.loc[coef_name, 'Estimate']
            result[f'{coef_name}_SE']    = coefs.loc[coef_name, 'Std. Error']
            result[f'{coef_name}_TStat'] = coefs.loc[coef_name, 't value']
            result[f'{coef_name}_PValue']= coefs.loc[coef_name, 'Pr(>|t|)']

        all_results.append(result)

    return pd.DataFrame(all_results)

# ----------------------------------------------------
# 10) MAIN LOOP
# ----------------------------------------------------
all_results = []
funds_updated = 0
not_processed_due_to_data = []

for _, row in fund_info.iterrows():
    symbol = row['SymbolCUSIP']
    cwa_category = row['CWA_Broad_Category_ID']
    
    region = determine_region(
        row['CWA_Broad_Category_ID'],
        row['YC_Category_ID'],
        row['YC_Global_Category_ID']
    )
    
    factor_names = factor_selection.get(cwa_category, [])
    aqr_factor_columns = [factor_to_aqr[f][region] for f in factor_names if f in factor_to_aqr and region in factor_to_aqr[f]]

    factor_data = prepare_factor_data(region)
    logger.debug(f"Factor data for {symbol}: {factor_data.shape}")

    symbol_data = fund_returns[fund_returns['Symbol'] == symbol]
    available_months = len(symbol_data)
    logger.debug(f"Available months for {symbol}: {available_months}")

    if available_months < 12:
        logger.info(f"Not enough data for {symbol} (<12 months). Found {available_months}. Skipping.")
        not_processed_due_to_data.append(symbol)
        continue

    try:
        result_df = run_multilinear_regression_r(symbol, fund_returns, factor_data, aqr_factor_columns, 12)
        if result_df.empty:
            logger.warning(f"Regression for {symbol} returned empty.")
        else:
            all_results.append(result_df)
            funds_updated += 1
    except Exception as e:
        logger.error(f"Exception for {symbol}: {e}")
        not_processed_due_to_data.append(symbol)

# ----------------------------------------------------
# 11) WRITE RESULTS TO DATABASE
# ----------------------------------------------------
if all_results:
    results_df = pd.concat(all_results, ignore_index=True)
    logger.info(f"Writing {len(results_df)} total regression rows to DB...")
    results_df.to_sql('Fund_Factors', engine, if_exists='append', index=False)
else:
    logger.info("No regression results to write to the database.")

end_time = time.time()
logger.info(f"Process completed in {end_time - start_time:.2f} seconds. {funds_updated} funds updated.")

# ----------------------------------------------------
# 12) PRINT ANY FUNDS NOT PROCESSED
# ----------------------------------------------------
if not_processed_due_to_data:
    count = len(not_processed_due_to_data)
    logger.info(f"The following {count} funds could not be processed:")
    for fund in not_processed_due_to_data:
        logger.info(f" - {fund}")
else:
    logger.info("All funds were processed successfully.")

2025-02-05 12:33:56,618 - DEBUG - Fund Info fetched: (1058, 4)
2025-02-05 12:33:58,309 - DEBUG - Fund Returns fetched: (96233, 3)
2025-02-05 12:33:58,311 - DEBUG - Preparing factor data for region: Global
2025-02-05 12:34:01,878 - WARNING - R[write to console]: 
2025-02-05 12:34:01,880 - WARNING - R[write to console]: -
2025-02-05 12:34:01,910 - WARNING - R[write to console]: 
2025-02-05 12:34:01,911 - WARNING - R[write to console]: /
                                                                              
2025-02-05 12:34:01,912 - WARNING - R[write to console]: 
2025-02-05 12:34:01,915 - WARNING - R[write to console]: 
2025-02-05 12:34:01,917 - WARNING - R[write to console]: /
                                                                              
2025-02-05 12:34:01,918 - WARNING - R[write to console]: 
2025-02-05 12:34:01,959 - WARNING - R[write to console]: 
2025-02-05 12:34:01,960 - WARNING - R[write to console]: -
                                                     

KeyboardInterrupt: 

In [ ]:
import rpy2.robjects as robjects
from rpy2.robjects.packages import importr
from rpy2.robjects import pandas2ri
from rpy2.robjects.conversion import localconverter, get_conversion
import pandas as pd

# Import the 'aqrr' R package
aqrr = importr('aqrr')

# Map function names -> references
aqr_function_map = {
    'aqr_hml_devil_monthly':      aqrr.aqr_hml_devil_monthly,
    'aqr_bab_monthly':            aqrr.aqr_bab_monthly,
    'aqr_mkt_monthly':            aqrr.aqr_mkt_monthly,
    'aqr_qmj_monthly':            aqrr.aqr_qmj_monthly,
    'aqr_smb_monthly':            aqrr.aqr_smb_monthly,
    'aqr_umd_monthly':            aqrr.aqr_umd_monthly,
    'aqr_momentum_monthly':       aqrr.aqr_momentum_monthly,
    'aqr_factor_premia_monthly':  aqrr.aqr_factor_premia_monthly,
    'aqr_credit_risk_premium':    aqrr.aqr_credit_risk_premium,
    'aqr_commodities_long_run':   aqrr.aqr_commodities_long_run
}

# Enable automatic Pandas <-> R DataFrame conversion
pandas2ri.activate()

for func_name, func_ref in aqr_function_map.items():
    print(f"\n--- Checking function: {func_name} ---")
    with localconverter(robjects.default_converter + pandas2ri.converter):
        r_df = func_ref()  # Call the R function
        df = get_conversion().rpy2py(r_df)

    # Show the top 5 rows
    print(df.head(5))

    # If there's a 'name' column, show unique region values
    if 'name' in df.columns:
        print("Unique 'name' values in data:", df['name'].unique())
    else:
        print("No 'name' column in this dataset.")


In [9]:
import rpy2.robjects as robjects
from rpy2.robjects.packages import importr
from rpy2.robjects import pandas2ri
from rpy2.robjects.conversion import localconverter, get_conversion
import pandas as pd

aqrr = importr("aqrr")
pandas2ri.activate()

with localconverter(robjects.default_converter + pandas2ri.converter):
    r_data = aqrr.aqr_mkt_monthly()  # Just this one call
    df = get_conversion().rpy2py(r_data)

print(df.head())
if 'name' in df.columns:
    print("Unique regions:", df['name'].unique())


R[write to console]: 
R[write to console]: -
R[write to console]: 
R[write to console]: /
                                                                              
R[write to console]: 
R[write to console]: 
R[write to console]: /
                                                                              
R[write to console]: 
R[write to console]: 
R[write to console]: -
                                                                              
R[write to console]: 


      date name  value
1 -15860.0  AUS    NaN
2 -15860.0  AUT    NaN
3 -15860.0  BEL    NaN
4 -15860.0  CAN    NaN
5 -15860.0  CHE    NaN
Unique regions: ['AUS' 'AUT' 'BEL' 'CAN' 'CHE' 'DEU' 'DNK' 'ESP' 'FIN' 'FRA' 'GBR' 'GRC'
 'HKG' 'IRL' 'ISR' 'ITA' 'JPN' 'NLD' 'NOR' 'NZL' 'PRT' 'SGP' 'SWE' 'USA'
 'Global' 'Global Ex USA' 'Europe' 'North America' 'Pacific']


In [3]:
import requests
import sqlalchemy
import pandas as pd
import time
import numpy as np

# Database Connection String
connection_string = "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"
engine = sqlalchemy.create_engine(connection_string)

# Headers for YCharts API requests
headers = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "X-YCHARTSIP": "107.2.197.229",
    "Host": "api.ycharts.com",
    "Connection": "Keep-Alive"
}

# List of symbols you want to fetch data for
symbols = [
    "P:1048205", "P:1048204", "P:795964", "^ALMLPTR", "^BCTR", "^BBEMUSDATR", "^BBGATR", 
    "^BIUSGCRTR", "^BBMBTR", "^BMBHYTR", "^BBUSATR", "^BBUSCOTR", "^BBUSCOHYTR", "^BBUGCR13YT",
    "^BBUGCR15YT", "^BBUSLGCRTR", "^BBUTB13MTR", "^CBSPXCC", "^CRUSREITTR", "^LGESAUPM", 
    "^MSACPCXJPT", "^MSACASPCTR", "^MSACASTR", "^MSACXUSGTR", "^MSACUSSMCT", "^MSACXUSTR", 
    "^MSACXUSVTR", "^MSACWIGTR", "^MSACWIIBTR", "^MSACWINTR", "^MSACSMCTR", "^MSACWITR", 
    "^MSACWIVTR", "^MSAUTR", "^MSCATR", "^MSCNTR", "^MSEMLATR", "^MSEMTR", "^MSEURSMCTR", 
    "^MSEURTR", "^MSINTR", "^MSJPTR", "^MSKRTR", "^MSMXTR", "^MSTHTR", "^MSUKTR", 
    "^MSUSAMVUTR", "^NA1003LTR", "^RLGTR", "^RDGTR", "^SP15CMSVST", "^SP15CNDSTR", 
    "^SP15CNSSTR", "^SP15NRGSTR", "^SP15FINSTR", "^SP15HCSTR", "^SP15INSTR", "^SP15MSTR", 
    "^SP15RESTR", "^SP15IFTSTR", "^SP15USTR", "^SP400TR", "^SP400VTR", "^STRS", 
    "^SPXTR", "^SPXVTR", "^SP6GTR", "^SP6TR", "^SNRU", "^SPGREITNTR", "^SPUSPSNTR"
]

# Function to fetch benchmark data
def fetch_benchmark_data(symbol, metric):
    """Fetch specific metric data for a given benchmark symbol."""
    api_url = f"https://api.ycharts.com/v3/indices/{symbol}/info/{metric}?retrieve_ttl=true"
    print(f"🔎 Requesting {symbol} - {metric}...")
    
    for attempt in range(5):  # Retry up to 5 times
        response = requests.get(api_url, headers=headers)

        if response.status_code == 200:
            data = response.json()
            if "response" in data and symbol in data["response"]:
                results = data["response"][symbol].get("results", {})
                
                if metric in results:
                    value = results[metric]["data"]
                    print(f"✅ {symbol} - Retrieved {metric}: {value}")
                    return symbol, value
                else:
                    print(f"⚠️ {symbol} - No `{metric}` found in API response.")
                    return symbol, None
            else:
                print(f"⚠️ {symbol} - Unexpected API response format: {data}")
                return symbol, None

        elif response.status_code == 403:  # API limit hit
            wait_time = 120  # Wait 2 minutes before retrying
            print(f"⚠️ API limit hit for {symbol}. Waiting {wait_time} seconds before retry ({attempt+1}/5)...")
            time.sleep(wait_time)
        
        else:
            print(f"❌ {symbol} - Error {response.status_code}: {response.text}")
            return symbol, None  # Stop trying on other errors

    print(f"⛔ {symbol} - Failed after 5 retries for {metric}.")
    return symbol, None

# Metrics to fetch for each symbol
metrics = ["name", "description"]  # Add or change these as needed

# Fetch data for all symbols and metrics
data_list = []
for symbol in symbols:
    for metric in metrics:
        result = fetch_benchmark_data(symbol, metric)
        if result[1]:  # If data was successfully fetched
            data_list.append({
                "Benchmark_Symbol": symbol,
                "metric": metric,
                "value": result[1]
            })
        time.sleep(0.1)  # Small delay to avoid rate limiting

# Convert to DataFrame for easier manipulation
df = pd.DataFrame(data_list)

# Pivot the data to match table structure
df_pivoted = df.pivot(index='Benchmark_Symbol', columns='metric', values='value').reset_index()
df_pivoted.columns.name = None  # Remove the 'metric' label from column names
df_pivoted = df_pivoted.rename(columns={
    'name': 'Benchmark_Name',
    'description': 'Description'
})

# Add static data if needed
df_pivoted['Datasource'] = 'YCharts'
df_pivoted['CWA_Broad_Category'] = 'Benchmark'
df_pivoted['Bench_Creator'] = 'Unknown'  # Adjust this if you have creator data

# Replace NaN with an empty string or a default value for string columns
df_pivoted['Description'] = df_pivoted['Description'].replace(np.nan, '')

# Insert or update data in SQL Server using MERGE
with engine.begin() as conn:
    for index, row in df_pivoted.iterrows():
        merge_sql = sqlalchemy.text("""
            MERGE Benchmarks AS target
            USING (SELECT :symbol AS Benchmark_Symbol, :name AS Benchmark_Name, :datasource AS Datasource, :category AS CWA_Broad_Category, :creator AS Bench_Creator, :description AS Description) AS source
            ON (target.Benchmark_Symbol = source.Benchmark_Symbol)
            WHEN MATCHED THEN
                UPDATE SET 
                    Benchmark_Name = source.Benchmark_Name,
                    Datasource = source.Datasource,
                    CWA_Broad_Category = source.CWA_Broad_Category,
                    Bench_Creator = source.Bench_Creator,
                    Description = source.Description
            WHEN NOT MATCHED THEN
                INSERT (Benchmark_Symbol, Benchmark_Name, Datasource, CWA_Broad_Category, Bench_Creator, Description)
                VALUES (source.Benchmark_Symbol, source.Benchmark_Name, source.Datasource, source.CWA_Broad_Category, source.Bench_Creator, source.Description);
        """)
        conn.execute(merge_sql, 
                     {"symbol": row["Benchmark_Symbol"],
                      "name": row["Benchmark_Name"],
                      "datasource": row["Datasource"],
                      "category": row["CWA_Broad_Category"],
                      "creator": row["Bench_Creator"],
                      "description": row["Description"]}
                     )

print("✅ Data inserted/updated in Benchmarks table.")

# Summary of Results
print("\n📊 **Summary:**")
print(f"✔️ Successfully fetched for {len(df_pivoted)} benchmarks")
print("🎯 Process Completed.")

🔎 Requesting P:1048205 - name...
❌ P:1048205 - Error 404: 








<!doctype html>
<html lang="en" ng-jq>
    <head>
        <!-- Google Tag Manager -->
<script>(function(w,d,s,l,i){w[l]=w[l]||[];w[l].push({'gtm.start':
    new Date().getTime(),event:'gtm.js'});var f=d.getElementsByTagName(s)[0],
    j=d.createElement(s),dl=l!='dataLayer'?'&l='+l:'';j.async=true;j.src=
    'https://www.googletagmanager.com/gtm.js?id='+i+dl;f.parentNode.insertBefore(j,f);
    })(window,document,'script','dataLayer','GTM-KHF6SRC');</script>
    <!-- End Google Tag Manager -->
        <title>
        404: Sorry we can not find that!
        </title>

        <meta name="viewport" content="width=device-width, initial-scale=1.0" />
<!-- This code allows us to correctly display the page on mobile devices -->
<script defer>
    var viewport = document.querySelector('meta[name=viewport]');
    if (viewport) {
        var minWidth = 700;
        if (screen.width < minWidth) {
            document.head.removeChi

In [5]:
#Insert benchmark monthly returns

import math
import certifi
import ssl
import requests
import sqlalchemy
import pandas as pd
import datetime
from dateutil.relativedelta import relativedelta
import time
import concurrent.futures
from requests.adapters import HTTPAdapter

# Configuration
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)

YCHARTS_API_URL = "https://api.ycharts.com/v3"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

# Metrics for benchmarks
METRICS = [
    ("total_monthly_return", "Monthly Return")
]

BATCH_SIZE = 5000  # Experiment with this value

# Create a custom SSL context
context = ssl.create_default_context()
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # For debugging only! Use CERT_REQUIRED for production.

# Custom HTTPAdapter to apply our SSL context
class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

# Create a session and mount the adapter for HTTPS requests
session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

# Date Configurations
TODAY = datetime.date.today()
END_DATE = TODAY.replace(day=1) - datetime.timedelta(days=1)  # Last day of the previous month
TWENTY_YEARS_AGO = END_DATE - relativedelta(years=20)

def get_start_date(earliest_date, default_start):
    """Determine the start date for data fetching."""
    if earliest_date and earliest_date > default_start:
        return earliest_date
    return default_start

def check_existing_data(engine, symbol, metric_db_name, start_date, end_date):
    """Check if there's data for the benchmark, metric, and date range in the database."""
    check_sql = """
    SELECT COUNT(*) 
    FROM Benchmark_Returns_Timeseries 
    WHERE Benchmark_Symbol = :symbol 
      AND Metric = :metric 
      AND Date BETWEEN :start_date AND :end_date
    """
    with engine.connect() as conn:
        count = conn.execute(sqlalchemy.text(check_sql), {
            'symbol': symbol,
            'metric': metric_db_name,
            'start_date': start_date,
            'end_date': end_date
        }).scalar()
        return count > 0  # True if data exists, False otherwise

def insert_benchmark_data(engine, batch_data, batch_size=5000):
    """Insert data into the database in batches, checking for duplicates."""
    insert_sql = """
    INSERT INTO Benchmark_Returns_Timeseries (Benchmark_Symbol, Date, ReturnValue, Metric)
    VALUES (:symbol, :date, :value, :metric)
    """
    
    check_sql = """
    SELECT 1 
    FROM Benchmark_Returns_Timeseries 
    WHERE Benchmark_Symbol = :symbol 
      AND Date = :date 
      AND Metric = :metric
    """
    
    unique_data = []
    inserted_count = 0
    with engine.connect() as conn:
        try:
            for item in batch_data:
                existing = conn.execute(sqlalchemy.text(check_sql), item).fetchone()
                if not existing:  # Data doesn't exist, proceed with insert
                    unique_data.append(item)
                    inserted_count += 1
                    if len(unique_data) >= batch_size:
                        conn.execute(sqlalchemy.text(insert_sql), unique_data)
                        conn.commit()
                        unique_data = []  # Reset the batch
            if unique_data:  # Insert any remaining data
                conn.execute(sqlalchemy.text(insert_sql), unique_data)
                conn.commit()
            print(f"Inserted {inserted_count} new data points out of {len(batch_data)}.")
        except sqlalchemy.exc.SQLAlchemyError as sqle:
            print(f"Database error in batch insert: {sqle}")
            conn.rollback()
    return inserted_count

def process_benchmark(symbol, metric, metric_db_name, engine):
    """Process each benchmark for a specific metric, check existing data before API call."""
    
    # Since benchmarks might not have inception dates like funds, we use a fixed start date
    start_date = get_start_date(None, TWENTY_YEARS_AGO)
    if not start_date:
        print(f"Skipping {symbol} for {metric}: no valid start date.")
        return None

    # Check if data already exists for this benchmark, metric, and date range
    if check_existing_data(engine, symbol, metric_db_name, start_date, END_DATE):
        print(f"Data for {symbol} and {metric} already exists, skipping API call.")
        return None

    # Ensure start_date is formatted correctly
    start_date_str = start_date.strftime('%Y-%m-%d')
    end_date_str = END_DATE.strftime('%Y-%m-%d')

    api_url = f"{YCHARTS_API_URL}/indices/{symbol}/series/{metric}?retrieve_ttl=true&start_date={start_date_str}&end_date={end_date_str}"

    try:
        response = session.get(api_url, headers=API_HEADERS)
        response.raise_for_status()  # Will raise an HTTPError if the HTTP request returned an unsuccessful status code

        parsed_data = response.json()
        data_map = {}

        # Parse the JSON response
        if 'response' in parsed_data and symbol in parsed_data['response']:
            for date, value in parsed_data['response'][symbol]['results'][metric]['data']:
                if symbol not in data_map:
                    data_map[symbol] = {}
                data_map[symbol][date] = {metric: value}

    except requests.exceptions.RequestException as e:
        print(f"API error for {symbol} on metric {metric}: {e}")
        return None

    if data_map:  
        print(f"Processed {symbol} for {metric}")
        return data_map
    return None

def main():
    start_time = time.time()
    
    engine = sqlalchemy.create_engine(connection_string, 
                                      pool_size=20, 
                                      max_overflow=50,
                                      pool_timeout=300)  # Increase pool size and overflow
    
    # Fetch symbols from the Benchmarks table
    sql = """
    SELECT Benchmark_Symbol
    FROM Benchmarks
    """
    symbols_df = pd.read_sql(sql, engine)
    symbols = symbols_df['Benchmark_Symbol'].tolist()

    total_inserted = 0
    for metric, metric_db_name in METRICS:
        print(f"\n🚀 Loading Metric: {metric}")
        all_data = []  # Collect all data for this metric
        
        with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
            futures = []
            for symbol in symbols:
                futures.append(executor.submit(process_benchmark, symbol, metric, metric_db_name, engine))  
            
            for future in concurrent.futures.as_completed(futures):
                try:
                    data_map = future.result()
                    if data_map:
                        for symbol, dates in data_map.items():
                            for date_str, metric_data in dates.items():
                                for metric_val, value in metric_data.items():
                                    if value is not None:
                                        try:
                                            date_obj = datetime.datetime.strptime(date_str, "%Y-%m-%d").date()
                                            decimal_value = round(float(value), 6)
                                            all_data.append({
                                                'symbol': symbol,
                                                'date': date_obj,
                                                'value': decimal_value,
                                                'metric': metric_db_name
                                            })
                                        except ValueError as ve:
                                            print(f"Data conversion error for {symbol} on {date_str}: {ve}")
                except Exception as exc:
                    print(f'An error occurred for {metric}: {exc}')

        # Insert all collected data in one go
        if all_data:
            total_inserted += insert_benchmark_data(engine, all_data)

    total_time = time.time() - start_time
    print(f"\n🎉 All done loading all metrics! Total time: {total_time:.2f} seconds")
    print(f"Total data points inserted: {total_inserted}")
    print(f"Total benchmarks processed: {len(symbols)}")
    print(f"Average time per benchmark per metric: {total_time / (len(symbols) * len(METRICS)):.2f} seconds")

    # Check pool status for debugging
    pool_stats = engine.pool.status()
    print(f"Pool Status: {pool_stats}")

    engine.dispose()

if __name__ == "__main__":
    main()


🚀 Loading Metric: total_monthly_return
Processed ^BBGATR for total_monthly_return
Processed ^BBUGCR13YT for total_monthly_return
Processed ^MSACASPCTR for total_monthly_return
Processed ^BBMBTR for total_monthly_return
Processed ^BMBHYTR for total_monthly_return
Processed ^BBEMUSDATR for total_monthly_return
Processed ^BCTR for total_monthly_return
Processed ^BBUGCR15YT for total_monthly_return
Processed ^BBUTB13MTR for total_monthly_return
Processed ^BBUSATR for total_monthly_return
Processed ^BBUSCOTR for total_monthly_return
Processed ^BIUSGCRTR for total_monthly_return
Processed ^CRUSREITTR for total_monthly_return
Processed ^MSACASTR for total_monthly_return
Processed ^MSACPCXJPT for total_monthly_return
Processed ^BBUSLGCRTR for total_monthly_return
Processed ^BBUSCOHYTR for total_monthly_return
Processed ^MSACSMCTR for total_monthly_return
Processed ^MSACUSSMCT for total_monthly_return
Processed ^MSACXUSGTR for total_monthly_return
Processed ^MSACXUSTR for total_monthly_return


In [6]:
import math
import certifi
import ssl
import requests
import sqlalchemy
import pandas as pd
import datetime
from dateutil.relativedelta import relativedelta
import time
import concurrent.futures
from requests.adapters import HTTPAdapter

# Configuration
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)

YCHARTS_API_URL = "https://api.ycharts.com/v3"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

METRICS = [
    ("five_year_total_monthly_return", "5 Year Return"),
    ("three_year_total_monthly_return", "3 Year Return"),
    ("one_year_total_monthly_return", "1 Year Return"),
    ("nine_total_monthly_return", "9 Month Return"),
    ("six_total_monthly_return", "6 Month Return"),
    ("three_total_monthly_return", "3 Month Return"),
    ("total_monthly_return", "1 Month Return")
]

BATCH_SIZE = 5000  # Experiment with this value

# Create a custom SSL context
context = ssl.create_default_context()
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # For debugging only! Use CERT_REQUIRED for production.

# Custom HTTPAdapter to apply our SSL context
class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

# Create a session and mount the adapter for HTTPS requests
session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

# Date Configurations
TODAY = datetime.date.today()
END_DATE = TODAY.replace(day=1) - datetime.timedelta(days=1)  # Last day of the previous month
TWENTY_YEARS_AGO = END_DATE - relativedelta(years=20)

def get_start_date(earliest_date, default_start):
    """Determine the start date for data fetching."""
    if earliest_date and earliest_date > default_start:
        return earliest_date
    return default_start

def check_existing_data(engine, symbol, metric_db_name, start_date, end_date):
    """Check if there's data for the benchmark, metric, and date range in the database."""
    check_sql = """
    SELECT COUNT(*) 
    FROM Benchmark_Returns_Timeseries 
    WHERE Benchmark_Symbol = :symbol 
      AND Metric = :metric 
      AND Date BETWEEN :start_date AND :end_date
    """
    with engine.connect() as conn:
        count = conn.execute(sqlalchemy.text(check_sql), {
            'symbol': symbol,
            'metric': metric_db_name,
            'start_date': start_date,
            'end_date': end_date
        }).scalar()
        return count > 0  # True if data exists, False otherwise

def insert_benchmark_data(engine, batch_data, batch_size=5000):
    """Insert data into the database in batches, checking for duplicates."""
    insert_sql = """
    INSERT INTO Benchmark_Returns_Timeseries (Benchmark_Symbol, Date, ReturnValue, Metric)
    VALUES (:symbol, :date, :value, :metric)
    """
    
    check_sql = """
    SELECT 1 
    FROM Benchmark_Returns_Timeseries 
    WHERE Benchmark_Symbol = :symbol 
      AND Date = :date 
      AND Metric = :metric
    """
    
    unique_data = []
    inserted_count = 0
    with engine.connect() as conn:
        try:
            for item in batch_data:
                existing = conn.execute(sqlalchemy.text(check_sql), item).fetchone()
                if not existing:  # Data doesn't exist, proceed with insert
                    unique_data.append(item)
                    inserted_count += 1
                    if len(unique_data) >= batch_size:
                        conn.execute(sqlalchemy.text(insert_sql), unique_data)
                        conn.commit()
                        unique_data = []  # Reset the batch
            if unique_data:  # Insert any remaining data
                conn.execute(sqlalchemy.text(insert_sql), unique_data)
                conn.commit()
            print(f"Inserted {inserted_count} new data points out of {len(batch_data)}.")
        except sqlalchemy.exc.SQLAlchemyError as sqle:
            print(f"Database error in batch insert: {sqle}")
            conn.rollback()
    return inserted_count

def process_benchmark(symbol, metric, metric_db_name, engine):
    """Process each benchmark for a specific metric, check existing data before API call."""
    
    # Since benchmarks might not have inception dates like funds, we use a fixed start date
    start_date = get_start_date(None, TWENTY_YEARS_AGO)
    if not start_date:
        print(f"Skipping {symbol} for {metric}: no valid start date.")
        return None

    # Check if data already exists for this benchmark, metric, and date range
    if check_existing_data(engine, symbol, metric_db_name, start_date, END_DATE):
        print(f"Data for {symbol} and {metric} already exists, skipping API call.")
        return None

    # Ensure start_date is formatted correctly
    start_date_str = start_date.strftime('%Y-%m-%d')
    end_date_str = END_DATE.strftime('%Y-%m-%d')

    api_url = f"{YCHARTS_API_URL}/indices/{symbol}/series/{metric}?retrieve_ttl=true&start_date={start_date_str}&end_date={end_date_str}"

    try:
        response = session.get(api_url, headers=API_HEADERS)
        response.raise_for_status()  # Will raise an HTTPError if the HTTP request returned an unsuccessful status code

        parsed_data = response.json()
        data_map = {}

        # Parse the JSON response
        if 'response' in parsed_data and symbol in parsed_data['response']:
            for date, value in parsed_data['response'][symbol]['results'][metric]['data']:
                if symbol not in data_map:
                    data_map[symbol] = {}
                data_map[symbol][date] = {metric: value}

    except requests.exceptions.RequestException as e:
        print(f"API error for {symbol} on metric {metric}: {e}")
        return None

    if data_map:  
        print(f"Processed {symbol} for {metric}")
        return data_map
    return None

def main():
    start_time = time.time()
    
    engine = sqlalchemy.create_engine(connection_string, 
                                      pool_size=20, 
                                      max_overflow=50,
                                      pool_timeout=300)  # Increase pool size and overflow
    
    # Fetch symbols from the Benchmarks table
    sql = """
    SELECT Benchmark_Symbol
    FROM Benchmarks
    """
    symbols_df = pd.read_sql(sql, engine)
    symbols = symbols_df['Benchmark_Symbol'].tolist()

    total_inserted = 0
    for metric, metric_db_name in METRICS:
        print(f"\n🚀 Loading Metric: {metric}")
        all_data = []  # Collect all data for this metric
        
        with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
            futures = []
            for symbol in symbols:
                futures.append(executor.submit(process_benchmark, symbol, metric, metric_db_name, engine))  
            
            for future in concurrent.futures.as_completed(futures):
                try:
                    data_map = future.result()
                    if data_map:
                        for symbol, dates in data_map.items():
                            for date_str, metric_data in dates.items():
                                for metric_val, value in metric_data.items():
                                    if value is not None:
                                        try:
                                            date_obj = datetime.datetime.strptime(date_str, "%Y-%m-%d").date()
                                            decimal_value = round(float(value), 6)
                                            all_data.append({
                                                'symbol': symbol,
                                                'date': date_obj,
                                                'value': decimal_value,
                                                'metric': metric_db_name
                                            })
                                        except ValueError as ve:
                                            print(f"Data conversion error for {symbol} on {date_str}: {ve}")
                except Exception as exc:
                    print(f'An error occurred for {metric}: {exc}')

        # Insert all collected data in one go
        if all_data:
            total_inserted += insert_benchmark_data(engine, all_data)

    total_time = time.time() - start_time
    print(f"\n🎉 All done loading all metrics! Total time: {total_time:.2f} seconds")
    print(f"Total data points inserted: {total_inserted}")
    print(f"Total benchmarks processed: {len(symbols)}")
    print(f"Average time per benchmark per metric: {total_time / (len(symbols) * len(METRICS)):.2f} seconds")

    # Check pool status for debugging
    pool_stats = engine.pool.status()
    print(f"Pool Status: {pool_stats}")

    engine.dispose()

if __name__ == "__main__":
    main()


🚀 Loading Metric: five_year_total_monthly_return
Processed ^BBEMUSDATR for five_year_total_monthly_return
Processed ^BBUGCR13YT for five_year_total_monthly_return
Processed ^ALMLPTR for five_year_total_monthly_return
Processed ^BBUTB13MTR for five_year_total_monthly_return
Processed ^BCTR for five_year_total_monthly_return
Processed ^MSACASPCTR for five_year_total_monthly_return
Processed ^MSACPCXJPT for five_year_total_monthly_return
Processed ^BBUGCR15YT for five_year_total_monthly_return
Processed ^BBMBTR for five_year_total_monthly_return
Processed ^CRUSREITTR for five_year_total_monthly_return
Processed ^BMBHYTR for five_year_total_monthly_return
Processed ^BBUSCOTR for five_year_total_monthly_return
Processed ^BBUSATR for five_year_total_monthly_return
Processed ^BBGATR for five_year_total_monthly_return
Processed ^MSACASTR for five_year_total_monthly_return
Processed ^BBUSLGCRTR for five_year_total_monthly_return
Processed ^BBUSCOHYTR for five_year_total_monthly_return
Processe

In [ ]:
#Add style box information in funds to screen

import math
import certifi
import ssl
import requests
import sqlalchemy
import pandas as pd
import datetime
from dateutil.relativedelta import relativedelta
import time
import concurrent.futures
from requests.adapters import HTTPAdapter
import logging

# Set up logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# Configuration
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)

YCHARTS_API_URL = "https://api.ycharts.com"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

METRICS = [
    # ... (Same list of metrics as before)
]

FUND_SYMBOLS_SQL = """
SELECT DISTINCT SymbolCUSIP AS Fund_Symbol, Fund_Type_ID
FROM Funds_to_Screen
"""

# Create a custom SSL context
context = ssl.create_default_context()
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # For debugging only! Use CERT_REQUIRED for production.

# Custom HTTPAdapter to apply our SSL context
class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

# Create a session and mount the adapter for HTTPS requests
session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

def convert_metric_to_column_name(metric):
    """Convert YCharts metric names to database column names."""
    # ... (Same function as before)

def fetch_metric_data(symbol, metric, fund_type_id):
    """Fetch data for a specific metric from YCharts API, adjusting for fund type."""
    start_date = (datetime.date.today() - relativedelta(years=1)).strftime('%Y-%m-%d')  # Example: last year
    end_date = datetime.date.today().strftime('%Y-%m-%d')
    
    is_mutual = (fund_type_id == 3)
    symbol_for_api = f"M:{symbol}" if is_mutual else symbol
    api_endpoint = "mutual_funds" if is_mutual else "companies"
    
    api_url = f"{YCHARTS_API_URL}/v3/{api_endpoint}/{symbol_for_api}/series/{metric}?retrieve_ttl=true&start_date={start_date}&end_date={end_date}"
    
    logger.info(f"Fetching data for {symbol} on metric {metric} with endpoint {api_endpoint}")
    try:
        response = session.get(api_url, headers=API_HEADERS)
        response.raise_for_status()
        data = response.json()
        if 'response' in data and symbol_for_api in data['response']:
            value = data['response'][symbol_for_api]['results'][metric]['data'][-1][1]  # Fetch the last data point
            logger.info(f"Successfully fetched {metric} for {symbol}: {value}")
            return value
        logger.warning(f"No data or invalid response for {symbol} on metric {metric}")
        return None
    except requests.exceptions.RequestException as e:
        logger.error(f"API error for {symbol} on metric {metric}: {e}")
        return None

def check_and_update_fund_data(engine, symbol, data):
    """Check if data exists and update or insert new data into the Funds_to_Screen table."""
    query_sql = """
    SELECT 1 FROM Funds_to_Screen WHERE SymbolCUSIP = :symbol
    """
    
    insert_sql = """
    INSERT INTO Funds_to_Screen (SymbolCUSIP, LCG, LCB, LCV, MCG, MCB, MCV, SCG, SCB, SCV, Giant_Cap_Exposure, Large_Cap_Exposure, Medium_Cap_Exposure, Micro_Cap_Exposure, Sensitive_Exposure, Small_Cap_Exposure, Cyclical_Exposure, Defensive_Exposure, AAA_Rated, AA_Rated, A_Rated, BBB_Rated, B_Rated, BB_Rated, Below_B_Rated, Not_Rated, Term_10_15_Y, Term_1_3_Y, Term_15_20_Y, Term_1_7_D, Term_183_364_D, Term_20_30_Y, Term_30_Plus_Y, Term_31_90_D, Term_3_5_Y, Term_5_7_Y, Term_7_10_Y, Term_8_30_D, Term_91_182_D, LT_Exposure, Interm_Exposure, ST_Exposure)
    VALUES (:symbol, :LCG, :LCB, :LCV, :MCG, :MCB, :MCV, :SCG, :SCB, :SCV, :Giant_Cap_Exposure, :Large_Cap_Exposure, :Medium_Cap_Exposure, :Micro_Cap_Exposure, :Sensitive_Exposure, :Small_Cap_Exposure, :Cyclical_Exposure, :Defensive_Exposure, :AAA_Rated, :AA_Rated, :A_Rated, :BBB_Rated, :B_Rated, :BB_Rated, :Below_B_Rated, :Not_Rated, :Term_10_15_Y, :Term_1_3_Y, :Term_15_20_Y, :Term_1_7_D, :Term_183_364_D, :Term_20_30_Y, :Term_30_Plus_Y, :Term_31_90_D, :Term_3_5_Y, :Term_5_7_Y, :Term_7_10_Y, :Term_8_30_D, :Term_91_182_D, :LT_Exposure, :Interm_Exposure, :ST_Exposure)
    """
    
    update_sql = """
    UPDATE Funds_to_Screen 
    SET LCG = :LCG, 
        LCB = :LCB, 
        LCV = :LCV,
        MCG = :MCG,
        MCB = :MCB,
        MCV = :MCV,
        SCG = :SCG,
        SCB = :SCB,
        SCV = :SCV,
        Giant_Cap_Exposure = :Giant_Cap_Exposure,
        Large_Cap_Exposure = :Large_Cap_Exposure,
        Medium_Cap_Exposure = :Medium_Cap_Exposure,
        Micro_Cap_Exposure = :Micro_Cap_Exposure,
        Sensitive_Exposure = :Sensitive_Exposure,
        Small_Cap_Exposure = :Small_Cap_Exposure,
        Cyclical_Exposure = :Cyclical_Exposure,
        Defensive_Exposure = :Defensive_Exposure,
        AAA_Rated = :AAA_Rated,
        AA_Rated = :AA_Rated,
        A_Rated = :A_Rated,
        BBB_Rated = :BBB_Rated,
        B_Rated = :B_Rated,
        BB_Rated = :BB_Rated,
        Below_B_Rated = :Below_B_Rated,
        Not_Rated = :Not_Rated,
        Term_10_15_Y = :Term_10_15_Y,
        Term_1_3_Y = :Term_1_3_Y,
        Term_15_20_Y = :Term_15_20_Y,
        Term_1_7_D = :Term_1_7_D,
        Term_183_364_D = :Term_183_364_D,
        Term_20_30_Y = :Term_20_30_Y,
        Term_30_Plus_Y = :Term_30_Plus_Y,
        Term_31_90_D = :Term_31_90_D,
        Term_3_5_Y = :Term_3_5_Y,
        Term_5_7_Y = :Term_5_7_Y,
        Term_7_10_Y = :Term_7_10_Y,
        Term_8_30_D = :Term_8_30_D,
        Term_91_182_D = :Term_91_182_D,
        LT_Exposure = :LT_Exposure,
        Interm_Exposure = :Interm_Exposure,
        ST_Exposure = :ST_Exposure
    WHERE SymbolCUSIP = :symbol
    """
    
    with engine.connect() as conn:
        try:
            # Check if the symbol already exists in the database
            result = conn.execute(sqlalchemy.text(query_sql), {'symbol': symbol}).fetchone()
            
            if all(value is not None for value in data.values() if value != 'symbol'):
                if result:
                    # Update existing record
                    conn.execute(sqlalchemy.text(update_sql), data)
                    logger.info(f"Updated existing data for {symbol}")
                else:
                    # Insert new record
                    conn.execute(sqlalchemy.text(insert_sql), data)
                    logger.info(f"Inserted new data for {symbol}")
                
                conn.commit()
            else:
                logger.warning(f"Data for {symbol} is incomplete, skipping update/insert.")
                for key, value in data.items():
                    if value is None:
                        logger.info(f"Missing value for {symbol} on field {key}")
        except sqlalchemy.exc.SQLAlchemyError as e:
            logger.error(f"Database operation error for {symbol}: {e}")
            conn.rollback()

def call_update_derived_metrics(engine):
    """Call the SQL stored procedure to update derived metrics."""
    with engine.connect() as conn:
        try:
            conn.execute(sqlalchemy.text("EXEC UpdateDerivedMetrics"))
            conn.commit()
            logger.info("Successfully executed stored procedure to update metrics.")
        except sqlalchemy.exc.SQLAlchemyError as e:
            logger.error(f"Error executing stored procedure: {e}")
            conn.rollback()

def main():
    start_time = time.time()
    logger.info("Starting data fetch and insertion process.")
    
    engine = sqlalchemy.create_engine(connection_string, 
                                      pool_size=20, 
                                      max_overflow=50,
                                      pool_timeout=300)
    
    symbols_df = pd.read_sql(FUND_SYMBOLS_SQL, engine)
    symbols = symbols_df[['Fund_Symbol', 'Fund_Type_ID']].values.tolist()
    
    logger.info(f"Processing {len(symbols)} symbols.")
    
    for symbol, fund_type_id in symbols:
        data = {'symbol': symbol}
        for metric in METRICS:
            column_name = convert_metric_to_column_name(metric)
            data[column_name] = fetch_metric_data(symbol, metric, fund_type_id)
        
        check_and_update_fund_data(engine, symbol, data)

    # After all data has been processed, call the stored procedure
    call_update_derived_metrics(engine)

    total_time = time.time() - start_time
    logger.info(f"🎉 All done loading all metrics! Total time: {total_time:.2f} seconds")

    engine.dispose()

if __name__ == "__main__":
    main()

2025-02-10 07:54:24,041 - INFO - Starting data fetch and insertion process.
2025-02-10 07:54:24,215 - INFO - Processing 1058 symbols.
2025-02-10 07:54:24,219 - ERROR - Database operation error for NTSX: (sqlalchemy.exc.InvalidRequestError) A value is required for bind parameter 'LCG'
[SQL: 
    UPDATE Funds_to_Screen 
    SET LCG = ?, 
        LCB = ?, 
        LCV = ?,
        MCG = ?,
        MCB = ?,
        MCV = ?,
        SCG = ?,
        SCB = ?,
        SCV = ?,
        Giant_Cap_Exposure = ?,
        Large_Cap_Exposure = ?,
        Medium_Cap_Exposure = ?,
        Micro_Cap_Exposure = ?,
        Sensitive_Exposure = ?,
        Small_Cap_Exposure = ?,
        Cyclical_Exposure = ?,
        Defensive_Exposure = ?,
        AAA_Rated = ?,
        AA_Rated = ?,
        A_Rated = ?,
        BBB_Rated = ?,
        B_Rated = ?,
        BB_Rated = ?,
        Below_B_Rated = ?,
        Not_Rated = ?,
        Term_10_15_Y = ?,
        Term_1_3_Y = ?,
        Term_15_20_Y = ?,
        Ter

In [ ]:
#Update fund metadata

import math
import certifi
import ssl
import requests
import sqlalchemy
import pandas as pd
import datetime
import time
import concurrent.futures
from requests.adapters import HTTPAdapter
import logging

# -----------------------------
# Logging Configuration
# -----------------------------
logging.basicConfig(level=logging.INFO,
                    format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# -----------------------------
# Database and API Configuration
# -----------------------------
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)

YCHARTS_API_URL = "https://api.ycharts.com"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

# -----------------------------
# Metric Mapping Dictionary
# -----------------------------
# Maps database column names (the metrics we update) to corresponding YCharts function codes.
yc_metric_mapping = {
    # Stylebox (Equity Exposure) Metrics
    "LCG": "equity_stylebox_large_cap_growth_exposure",
    "LCB": "equity_stylebox_large_cap_blend_exposure",
    "LCV": "equity_stylebox_large_cap_value_exposure",
    "MCG": "equity_stylebox_mid_cap_growth_exposure",
    "MCB": "equity_stylebox_mid_cap_blend_exposure",
    "MCV": "equity_stylebox_mid_cap_value_exposure",
    "SCG": "equity_stylebox_small_cap_growth_exposure",
    "SCB": "equity_stylebox_small_cap_blend_exposure",
    "SCV": "equity_stylebox_small_cap_value_exposure",
    "Giant_Cap_Exposure": "giant_cap_exposure",
    "Large_Cap_Exposure": "large_cap_exposure",
    "Medium_Cap_Exposure": "medium_cap_exposure",
    "Micro_Cap_Exposure": "micro_cap_exposure",
    "Sensitive_Exposure": "sensitive_exposure",
    "Small_Cap_Exposure": "small_cap_exposure",
    "Cyclical_Exposure": "cyclical_exposure",
    "Defensive_Exposure": "defensive_exposure",
    # Bond Term (Maturity) Metrics
    "Term_10_15_Y": "10_to_15_years_maturity_bond_exposure",
    "Term_1_3_Y": "1_to_3_years_maturity_bond_exposure",
    "Term_15_20_Y": "15_to_20_years_maturity_bond_exposure",
    "Term_1_7_D": "1_to_7_days_maturity_bond_exposure",
    "Term_183_364_D": "183_to_364_days_maturity_bond_exposure",
    "Term_20_30_Y": "20_to_30_years_maturity_bond_exposure",
    "Term_30_Plus_Y": "over_30_years_maturity_bond_exposure",
    "Term_31_90_D": "31_to_90_days_maturity_bond_exposure",
    "Term_3_5_Y": "3_to_5_years_maturity_bond_exposure",
    "Term_5_7_Y": "5_to_7_years_maturity_bond_exposure",
    "Term_7_10_Y": "7_to_10_years_maturity_bond_exposure",
    "Term_8_30_D": "8_to_30_days_maturity_bond_exposure",
    "Term_91_182_D": "91_to_182_days_maturity_bond_exposure",
    # Term Exposure Metrics
    "LT_Exposure": "long_term_exposure",
    "Interm_Exposure": "intermediate_term_exposure",
    "ST_Exposure": "short_term_exposure",
    # Bond Rating Metrics
    "AAA_Rated": "aaa_bond_exposure",
    "AA_Rated": "aa_bond_exposure",
    "A_Rated": "a_bond_exposure",
    "BBB_Rated": "bbb_bond_exposure",
    "B_Rated": "b_bond_exposure",
    "BB_Rated": "bb_bond_exposure",
    "Below_B_Rated": "below_b_bond_exposure",
    "Not_Rated": "not_rated_bond_exposure"
}

# Use the keys from the mapping as the list of metrics (database column names) we update.
METRICS = list(yc_metric_mapping.keys())

# SQL to retrieve fund symbols and their Fund_Type_ID from the database.
FUND_SYMBOLS_SQL = """
SELECT DISTINCT SymbolCUSIP AS Fund_Symbol, Fund_Type_ID
FROM Funds_to_Screen
"""

# -----------------------------
# Custom SSL Context and HTTP Adapter
# -----------------------------
context = ssl.create_default_context()
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # For debugging only; in production, use CERT_REQUIRED.

class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

# -----------------------------
# Helper Functions for YCP Calls
# -----------------------------
def build_points_lines(symbol, yc_code, is_mutual):
    """
    Construct the points line for a YCP (data point) call.
    Format: "symbol_for_api,yc_code"
    The "M:" prefix is added only for mutual funds (when fund_type_id == 3).
    No date is included.
    """
    symbol_for_api = f"M:{symbol}" if is_mutual else symbol
    return f"{symbol_for_api},{yc_code}"

def fetch_data_point(symbol, metric, fund_type_id):
    """
    Fetch a single descriptive data point for the given metric using the YCP endpoint.
    Uses the yc_metric_mapping to obtain the proper YC function code.
    """
    is_mutual = (fund_type_id == 3)
    yc_code = yc_metric_mapping.get(metric)
    if not yc_code:
        logger.error(f"No YC mapping found for metric '{metric}'.")
        return None
    points_line = build_points_lines(symbol, yc_code, is_mutual)
    payload = f"points={points_line}"
    api_url = f"{YCHARTS_API_URL}/v3/excel/points"
    logger.info(f"Fetching data point for metric '{metric}' (YC Code: {yc_code}) for symbol '{symbol}' with payload: {payload}")
    try:
        response = session.post(api_url, headers=API_HEADERS, data=payload, timeout=60)
        response.raise_for_status()
        data = response.json()
        symbol_for_api = f"M:{symbol}" if is_mutual else symbol
        if 'response' in data and symbol_for_api in data['response']:
            results = data['response'][symbol_for_api].get("results", {})
            if yc_code in results:
                # First try the expected "data" key.
                datapoints = results[yc_code].get("data")
                if not datapoints:
                    # Fallback: try an empty string key and wrap its "results" in a list.
                    fallback = results[yc_code].get("")
                    if fallback and "results" in fallback:
                        datapoints = [fallback["results"]]
                if datapoints and isinstance(datapoints, list):
                    last_point = datapoints[-1]
                    if isinstance(last_point, list) and len(last_point) > 1:
                        value = last_point[1]
                        logger.info(f"Fetched {metric} for {symbol}: {value}")
                        return value
        logger.warning(f"No valid data returned for symbol '{symbol}' on metric '{metric}' (YC Code: {yc_code})")
        return None
    except requests.exceptions.RequestException as e:
        logger.error(f"API error for symbol '{symbol}' on metric '{metric}' (YC Code: {yc_code}): {e}")
        return None

# -----------------------------
# Other Helper Functions
# -----------------------------
def convert_metric_to_column_name(metric):
    """
    In this implementation, the database column name is the same as the metric key.
    """
    return metric

def verify_columns(engine, table_name, expected_columns):
    """
    Verify that all expected columns exist in the specified table.
    Logs any missing columns.
    """
    inspector = sqlalchemy.inspect(engine)
    actual_columns = [col['name'] for col in inspector.get_columns(table_name)]
    missing_columns = [col for col in expected_columns if col not in actual_columns]
    if missing_columns:
        logger.warning(f"Missing columns in {table_name}: {missing_columns}")
    else:
        logger.info(f"All expected columns are present in {table_name}.")

def check_and_update_fund_data(engine, symbol, data):
    """
    Check if a record for the given symbol exists in Funds_to_Screen.
    For updates, only the metrics columns are updated.
    For inserts, a default ProductName is supplied (using the symbol) to satisfy non‑nullable constraints.
    The SQL is built dynamically based solely on our METRICS.
    """
    query_sql = "SELECT ProductName FROM Funds_to_Screen WHERE SymbolCUSIP = :symbol"
    
    # Build dynamic SQL for updating only the metrics columns.
    update_sql = "UPDATE Funds_to_Screen SET " + ", ".join(f"{col} = :{col}" for col in METRICS) + " WHERE SymbolCUSIP = :symbol"
    
    # Build dynamic SQL for inserting a new record, including ProductName.
    columns = "SymbolCUSIP, ProductName, " + ", ".join(METRICS)
    placeholders = ":symbol, :ProductName, " + ", ".join(f":{col}" for col in METRICS)
    insert_sql = f"INSERT INTO Funds_to_Screen ({columns}) VALUES ({placeholders})"
    
    with engine.connect() as conn:
        try:
            result = conn.execute(sqlalchemy.text(query_sql), {'symbol': symbol}).fetchone()
            if result:
                conn.execute(sqlalchemy.text(update_sql), data)
                logger.info(f"Updated data for symbol {symbol}")
            else:
                # If new, set ProductName to symbol if not provided.
                if "ProductName" not in data or data["ProductName"] is None:
                    data["ProductName"] = symbol
                conn.execute(sqlalchemy.text(insert_sql), data)
                logger.info(f"Inserted new record for symbol {symbol}")
            conn.commit()
        except sqlalchemy.exc.SQLAlchemyError as e:
            logger.error(f"Database error for {symbol}: {e}")
            conn.rollback()

def call_update_derived_metrics(engine):
    """
    Call the SQL stored procedure to update derived metrics.
    """
    with engine.connect() as conn:
        try:
            conn.execute(sqlalchemy.text("EXEC UpdateDerivedMetrics"))
            conn.commit()
            logger.info("Executed stored procedure UpdateDerivedMetrics.")
        except sqlalchemy.exc.SQLAlchemyError as e:
            logger.error(f"Error executing stored procedure: {e}")
            conn.rollback()

def process_symbol(symbol, fund_type_id, engine):
    """
    Process a single symbol:
      - Fetch each metric using a YCP (data point) call.
      - Build a data dictionary keyed by the metric (database column) names.
      - Update or insert the record in the database.
      
    (Optional: Add logic to skip metrics not applicable for a given fund type.)
    """
    logger.info(f"Starting processing for symbol: {symbol}")
    data = {'symbol': symbol}
    for metric in METRICS:
        column_name = convert_metric_to_column_name(metric)
        value = fetch_data_point(symbol, metric, fund_type_id)
        data[column_name] = value
    # Ensure every metric key is present (even if its value is None)
    for key in METRICS:
        data.setdefault(key, None)
    logger.debug(f"Data dictionary for {symbol}: {data}")
    check_and_update_fund_data(engine, symbol, data)
    logger.info(f"Finished processing for symbol: {symbol}")

def main():
    start_time = time.time()
    logger.info("Starting data fetch and insertion process.")
    
    engine = sqlalchemy.create_engine(connection_string,
                                      pool_size=20,
                                      max_overflow=50,
                                      pool_timeout=300)
    
    # Verify that all expected columns exist in the Funds_to_Screen table.
    expected_columns = ['SymbolCUSIP', 'ProductName'] + METRICS
    verify_columns(engine, "Funds_to_Screen", expected_columns)
    
    # Retrieve all symbols from the database.
    symbols_df = pd.read_sql(FUND_SYMBOLS_SQL, engine)
    symbols_list = symbols_df[['Fund_Symbol', 'Fund_Type_ID']].values.tolist()
    logger.info(f"Processing {len(symbols_list)} symbols from the database.")
    
    # Process symbols in parallel using ThreadPoolExecutor.
    with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
        futures = []
        for symbol, fund_type_id in symbols_list:
            futures.append(executor.submit(process_symbol, symbol, fund_type_id, engine))
        for future in concurrent.futures.as_completed(futures):
            try:
                future.result()
            except Exception as exc:
                logger.error(f"Error processing symbol: {exc}")
    
    # Call the stored procedure to update derived metrics.
    call_update_derived_metrics(engine)
    
    total_time = time.time() - start_time
    logger.info(f"All metrics processed successfully in {total_time:.2f} seconds")
    engine.dispose()

if __name__ == "__main__":
    main()



2025-02-10 14:40:40,289 - INFO - Starting data fetch and insertion process.
2025-02-10 14:40:40,469 - INFO - All expected columns are present in Funds_to_Screen.
2025-02-10 14:40:40,504 - INFO - Processing 1060 symbols from the database.
2025-02-10 14:40:40,506 - INFO - Starting processing for symbol: NTSX
2025-02-10 14:40:40,508 - INFO - Starting processing for symbol: HIPS
2025-02-10 14:40:40,508 - INFO - Starting processing for symbol: EAOA
2025-02-10 14:40:40,508 - INFO - Fetching data point for metric 'LCG' (YC Code: equity_stylebox_large_cap_growth_exposure) for symbol 'NTSX' with payload: points=NTSX,equity_stylebox_large_cap_growth_exposure
2025-02-10 14:40:40,508 - INFO - Starting processing for symbol: AOM
2025-02-10 14:40:40,510 - INFO - Starting processing for symbol: AOK
2025-02-10 14:40:40,510 - INFO - Fetching data point for metric 'LCG' (YC Code: equity_stylebox_large_cap_growth_exposure) for symbol 'HIPS' with payload: points=HIPS,equity_stylebox_large_cap_growth_expos

In [ ]:
#Additional Metadata loading

import math
import ssl
import requests
import sqlalchemy
import pandas as pd
import time
import concurrent.futures
from requests.adapters import HTTPAdapter
import logging

# -----------------------------
# Logging Configuration
# -----------------------------
logging.basicConfig(level=logging.INFO,
                    format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# -----------------------------
# Database and API Configuration
# -----------------------------
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)
YCHARTS_API_URL = "https://api.ycharts.com"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

# -----------------------------
# New Metrics Mapping Dictionary
# -----------------------------
# Maps our new (shortened) column names to the corresponding YCharts function codes.
new_metrics_mapping = {
    "expense_ratio": "expense_ratio",
    "pct_top_10": "percent_of_assets_in_top_10_holdings",
    "pct_top_25": "percent_of_assets_in_top_25_holdings",
    "materials": "basic_materials_exposure",
    "comsvc": "communication_services_exposure",
    "concyc": "consumer_cyclical_exposure",
    "condef": "consumer_defensive_exposure",
    "energy": "energy_exposure",
    "finsvc": "financial_services_exposure",
    "healthcare": "healthcare_exposure",
    "industrials": "industrials_exposure",
    "realestate": "real_estate_exposure",
    "technology": "technology_exposure",
    "utilities": "utilities_exposure",
    "relative_composition": "relative_composition",
    "num_bonds": "number_of_bond_holdings",
    "num_stocks": "number_of_stock_holdings",
    "dev_mkt": "developed_market_exposure",
    "em_mkt": "emerging_market_exposure",
    "europe": "greater_europe_total_exposure",
    "lat_america": "latin_america_total_exposure",
    "namerica": "north_america_total_exposure",
    "africa_mideast": "africa_middle_east_total_exposure",
    "asia_em": "asia_emerging_total_exposure",
    "asia_dev": "asia_developed_total_exposure",
    "australia": "australasia_total_exposure",
    "india": "india_total_exposure",
    "w_avg_dc": "weighted_average_debt_to_capital",
    "avg_mkt_cap": "average_market_cap",
    "avg_pe_ratio": "weighted_average_pe_ratio",
    "avg_pb_ratio": "weighted_average_price_to_book_ratio",
    "avg_pcf_ratio": "weighted_average_price_to_cash_flow",
    "avg_ps_ratio": "weighted_average_price_to_sales_ratio",
    "avg_net_margin": "weighted_median_net_margin",
    "avg_roa": "weighted_median_return_on_assets",
    "avg_roe": "weighted_median_return_on_equity",
    "preferreds": "preferred_stock_exposure",
    "securitized": "securitized_fixed_income_exposure",
    "muni_exempt": "municipal_tax_exempt_bond_exposure",
    "muni_tax": "municipal_taxable_bond_exposure",
    "muni_exposure": "municipal_fixed_income_exposure",
    "corp_exposure": "corporate_bond_exposure",
    "corp_fi": "corporate_fixed_income_exposure",
    "govi_exp": "government_bond_exposure",
    "govi_fi": "government_fixed_income_exposure",
    "covered_bond": "covered_bond_exposure",
    "gov_bond": "government_related_bond_exposure",
    "converts": "convertible_bond_exposure",
    "asset_backed_sec": "asset_backed_security_exposure"
}

# List of new metric (column) names
NEW_METRICS = list(new_metrics_mapping.keys())

# SQL to retrieve fund symbols and their Fund_Type_ID from Funds_to_Screen
FUND_SYMBOLS_SQL = """
SELECT DISTINCT SymbolCUSIP AS Fund_Symbol, Fund_Type_ID
FROM Funds_to_Screen
"""

# -----------------------------
# Custom SSL Context and HTTP Adapter
# -----------------------------
context = ssl.create_default_context()
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # Use CERT_REQUIRED in production

class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

# -----------------------------
# Helper Functions for New YCP Calls
# -----------------------------
def build_points_lines_new(symbol, yc_code, is_mutual):
    """
    Build the points payload line for a YCP call for new metrics.
    Format: "symbol_for_api,yc_code"
    """
    symbol_for_api = f"M:{symbol}" if is_mutual else symbol
    return f"{symbol_for_api},{yc_code}"

def fetch_new_data_point(symbol, metric, fund_type_id):
    """
    Fetch a single data point for the new metric using the YCP endpoint.
    Uses new_metrics_mapping to obtain the YC function code.
    """
    is_mutual = (fund_type_id == 3)
    yc_code = new_metrics_mapping.get(metric)
    if not yc_code:
        logger.error(f"No YC mapping found for new metric '{metric}'.")
        return None
    points_line = build_points_lines_new(symbol, yc_code, is_mutual)
    payload = f"points={points_line}"
    api_url = f"{YCHARTS_API_URL}/v3/excel/points"
    logger.info(f"Fetching new data point for metric '{metric}' (YC Code: {yc_code}) for symbol '{symbol}' with payload: {payload}")
    try:
        response = session.post(api_url, headers=API_HEADERS, data=payload, timeout=60)
        response.raise_for_status()
        data = response.json()
        symbol_for_api = f"M:{symbol}" if is_mutual else symbol
        if 'response' in data and symbol_for_api in data['response']:
            results = data['response'][symbol_for_api].get("results", {})
            if yc_code in results:
                datapoints = results[yc_code].get("data")
                if not datapoints:
                    fallback = results[yc_code].get("")
                    if fallback and "results" in fallback:
                        datapoints = [fallback["results"]]
                if datapoints and isinstance(datapoints, list):
                    last_point = datapoints[-1]
                    if isinstance(last_point, list) and len(last_point) > 1:
                        value = last_point[1]
                        logger.info(f"Fetched new metric '{metric}' for {symbol}: {value}")
                        return value
        logger.warning(f"No valid data returned for symbol '{symbol}' on new metric '{metric}' (YC Code: {yc_code})")
        return None
    except requests.exceptions.RequestException as e:
        logger.error(f"API error for symbol '{symbol}' on new metric '{metric}' (YC Code: {yc_code}): {e}")
        return None

# -----------------------------
# Other Helper Functions for New Metrics
# -----------------------------
def verify_new_columns(engine, table_name, expected_columns):
    """
    Verify that all expected new metric columns exist in the table.
    """
    inspector = sqlalchemy.inspect(engine)
    actual_columns = [col['name'] for col in inspector.get_columns(table_name)]
    missing_columns = [col for col in expected_columns if col not in actual_columns]
    if missing_columns:
        logger.warning(f"Missing new columns in {table_name}: {missing_columns}")
    else:
        logger.info(f"All expected new columns are present in {table_name}.")

def check_and_update_new_data(engine, symbol, data):
    """
    Update (or insert) only the new metrics columns for a given symbol.
    Dynamic SQL is built based on NEW_METRICS.
    For new records, a default ProductName is supplied (using the symbol).
    """
    query_sql = "SELECT ProductName FROM Funds_to_Screen WHERE SymbolCUSIP = :symbol"
    
    # Build update SQL for new metrics only.
    update_sql = "UPDATE Funds_to_Screen SET " + ", ".join(f"{col} = :{col}" for col in NEW_METRICS) + " WHERE SymbolCUSIP = :symbol"
    
    # Build insert SQL that includes SymbolCUSIP, ProductName, and new metrics.
    columns = "SymbolCUSIP, ProductName, " + ", ".join(NEW_METRICS)
    placeholders = ":symbol, :ProductName, " + ", ".join(f":{col}" for col in NEW_METRICS)
    insert_sql = f"INSERT INTO Funds_to_Screen ({columns}) VALUES ({placeholders})"
    
    with engine.connect() as conn:
        try:
            result = conn.execute(sqlalchemy.text(query_sql), {'symbol': symbol}).fetchone()
            if result:
                conn.execute(sqlalchemy.text(update_sql), data)
                logger.info(f"Updated new metrics for symbol {symbol}")
            else:
                if "ProductName" not in data or data["ProductName"] is None:
                    data["ProductName"] = symbol
                conn.execute(sqlalchemy.text(insert_sql), data)
                logger.info(f"Inserted new record for new metrics for symbol {symbol}")
            conn.commit()
        except sqlalchemy.exc.SQLAlchemyError as e:
            logger.error(f"Database error for symbol {symbol} (new metrics): {e}")
            conn.rollback()

def process_symbol_new(symbol, fund_type_id, engine):
    """
    Process a single symbol to fetch new metrics data:
      - Iterates over each new metric and calls the YCP endpoint.
      - Builds a data dictionary keyed by new metric column names.
      - Updates (or inserts) the record in the database.
    """
    logger.info(f"Starting new metrics processing for symbol: {symbol}")
    data = {'symbol': symbol}
    for metric in NEW_METRICS:
        value = fetch_new_data_point(symbol, metric, fund_type_id)
        data[metric] = value
    # Ensure every key is present.
    for key in NEW_METRICS:
        data.setdefault(key, None)
    logger.debug(f"New data dictionary for {symbol}: {data}")
    check_and_update_new_data(engine, symbol, data)
    logger.info(f"Finished new metrics processing for symbol: {symbol}")

def main():
    start_time = time.time()
    logger.info("Starting new metrics data fetch and insertion process.")
    
    engine = sqlalchemy.create_engine(connection_string,
                                      pool_size=20,
                                      max_overflow=50,
                                      pool_timeout=300)
    
    # Verify new columns exist in the table.
    expected_new_columns = NEW_METRICS  # Only the new metric columns
    verify_new_columns(engine, "Funds_to_Screen", expected_new_columns)
    
    # Retrieve all symbols from the database.
    symbols_df = pd.read_sql(FUND_SYMBOLS_SQL, engine)
    symbols_list = symbols_df[['Fund_Symbol', 'Fund_Type_ID']].values.tolist()
    logger.info(f"Processing new metrics for {len(symbols_list)} symbols from the database.")
    
    # Process symbols in parallel.
    with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
        futures = []
        for symbol, fund_type_id in symbols_list:
            futures.append(executor.submit(process_symbol_new, symbol, fund_type_id, engine))
        for future in concurrent.futures.as_completed(futures):
            try:
                future.result()
            except Exception as exc:
                logger.error(f"Error processing symbol for new metrics: {exc}")
    
    total_time = time.time() - start_time
    logger.info(f"All new metrics processed successfully in {total_time:.2f} seconds")
    engine.dispose()

if __name__ == "__main__":
    main()


2025-02-10 16:01:53,784 - INFO - Starting new metrics data fetch and insertion process.
2025-02-10 16:01:53,975 - INFO - All expected new columns are present in Funds_to_Screen.
2025-02-10 16:01:53,994 - INFO - Processing new metrics for 1060 symbols from the database.
2025-02-10 16:01:53,996 - INFO - Starting new metrics processing for symbol: NTSX
2025-02-10 16:01:54,012 - INFO - Starting new metrics processing for symbol: HIPS
2025-02-10 16:01:54,013 - INFO - Starting new metrics processing for symbol: EAOA
2025-02-10 16:01:54,013 - INFO - Fetching new data point for metric 'expense_ratio' (YC Code: expense_ratio) for symbol 'NTSX' with payload: points=NTSX,expense_ratio
2025-02-10 16:01:54,015 - INFO - Starting new metrics processing for symbol: AOM
2025-02-10 16:01:54,015 - INFO - Fetching new data point for metric 'expense_ratio' (YC Code: expense_ratio) for symbol 'HIPS' with payload: points=HIPS,expense_ratio
2025-02-10 16:01:54,015 - INFO - Starting new metrics processing for 

In [9]:
#updating metadata but checking for the data first

import math
import ssl
import requests
import sqlalchemy
import pandas as pd
import time
import concurrent.futures
from requests.adapters import HTTPAdapter
import logging

# -----------------------------
# Logging Configuration
# -----------------------------
logging.basicConfig(level=logging.INFO,
                    format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# -----------------------------
# Database and API Configuration
# -----------------------------
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)
YCHARTS_API_URL = "https://api.ycharts.com"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

# -----------------------------
# New Metrics Mapping Dictionary
# -----------------------------
# Maps our new (shortened) column names to their corresponding YCharts function codes.
new_metrics_mapping = {
    "expense_ratio": "expense_ratio",
    "pct_top_10": "percent_of_assets_in_top_10_holdings",
    "pct_top_25": "percent_of_assets_in_top_25_holdings",
    "materials": "basic_materials_exposure",
    "comsvc": "communication_services_exposure",
    "concyc": "consumer_cyclical_exposure",
    "condef": "consumer_defensive_exposure",
    "energy": "energy_exposure",
    "finsvc": "financial_services_exposure",
    "healthcare": "healthcare_exposure",
    "industrials": "industrials_exposure",
    "realestate": "real_estate_exposure",
    "technology": "technology_exposure",
    "utilities": "utilities_exposure",
    "relative_composition": "relative_composition",
    "num_bonds": "number_of_bond_holdings",
    "num_stocks": "number_of_stock_holdings",
    "dev_mkt": "developed_market_exposure",
    "em_mkt": "emerging_market_exposure",
    "europe": "greater_europe_total_exposure",
    "lat_america": "latin_america_total_exposure",
    "namerica": "north_america_total_exposure",
    "africa_mideast": "africa_middle_east_total_exposure",
    "asia_em": "asia_emerging_total_exposure",
    "asia_dev": "asia_developed_total_exposure",
    "australia": "australasia_total_exposure",
    "india": "india_total_exposure",
    "w_avg_dc": "weighted_average_debt_to_capital",
    "avg_mkt_cap": "average_market_cap",
    "avg_pe_ratio": "weighted_average_pe_ratio",
    "avg_pb_ratio": "weighted_average_price_to_book_ratio",
    "avg_pcf_ratio": "weighted_average_price_to_cash_flow",
    "avg_ps_ratio": "weighted_average_price_to_sales_ratio",
    "avg_net_margin": "weighted_median_net_margin",
    "avg_roa": "weighted_median_return_on_assets",
    "avg_roe": "weighted_median_return_on_equity",
    "preferreds": "preferred_stock_exposure",
    "securitized": "securitized_fixed_income_exposure",
    "muni_exempt": "municipal_tax_exempt_bond_exposure",
    "muni_tax": "municipal_taxable_bond_exposure",
    "muni_exposure": "municipal_fixed_income_exposure",
    "corp_exposure": "corporate_bond_exposure",
    "corp_fi": "corporate_fixed_income_exposure",
    "govi_exp": "government_bond_exposure",
    "govi_fi": "government_fixed_income_exposure",
    "covered_bond": "covered_bond_exposure",
    "gov_bond": "government_related_bond_exposure",
    "converts": "convertible_bond_exposure",
    "asset_backed_sec": "asset_backed_security_exposure"
}

# List of new metric (column) names to update
NEW_METRICS = list(new_metrics_mapping.keys())

# SQL to retrieve fund symbols and their Fund_Type_ID from Funds_to_Screen
FUND_SYMBOLS_SQL = """
SELECT DISTINCT SymbolCUSIP AS Fund_Symbol, Fund_Type_ID
FROM Funds_to_Screen
"""

# -----------------------------
# Custom SSL Context and HTTP Adapter
# -----------------------------
context = ssl.create_default_context()
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # For debugging; use CERT_REQUIRED in production

class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

# -----------------------------
# Helper Functions for YCP Calls (New Metrics)
# -----------------------------
def build_points_lines_new(symbol, yc_code, is_mutual):
    """
    Build the points line for a YCP call for new metrics.
    Format: "symbol_for_api,yc_code"
    The "M:" prefix is added only for mutual funds.
    """
    symbol_for_api = f"M:{symbol}" if is_mutual else symbol
    return f"{symbol_for_api},{yc_code}"

def fetch_new_data_point(symbol, metric, fund_type_id):
    """
    Fetch a single data point for the new metric using the YCP endpoint.
    Uses new_metrics_mapping to obtain the correct YC function code.
    """
    is_mutual = (fund_type_id == 3)
    yc_code = new_metrics_mapping.get(metric)
    if not yc_code:
        logger.error(f"No YC mapping found for new metric '{metric}'.")
        return None
    points_line = build_points_lines_new(symbol, yc_code, is_mutual)
    payload = f"points={points_line}"
    api_url = f"{YCHARTS_API_URL}/v3/excel/points"
    logger.info(f"Fetching new data point for metric '{metric}' (YC Code: {yc_code}) for symbol '{symbol}' with payload: {payload}")
    try:
        response = session.post(api_url, headers=API_HEADERS, data=payload, timeout=60)
        response.raise_for_status()
        data = response.json()
        symbol_for_api = f"M:{symbol}" if is_mutual else symbol
        if 'response' in data and symbol_for_api in data['response']:
            results = data['response'][symbol_for_api].get("results", {})
            if yc_code in results:
                # Try the "data" key first
                datapoints = results[yc_code].get("data")
                if not datapoints:
                    fallback = results[yc_code].get("")
                    if fallback and "results" in fallback:
                        datapoints = [fallback["results"]]
                if datapoints and isinstance(datapoints, list):
                    last_point = datapoints[-1]
                    if isinstance(last_point, list) and len(last_point) > 1:
                        value = last_point[1]
                        logger.info(f"Fetched new metric '{metric}' for {symbol}: {value}")
                        return value
        logger.warning(f"No valid data returned for symbol '{symbol}' on new metric '{metric}' (YC Code: {yc_code})")
        return None
    except requests.exceptions.RequestException as e:
        logger.error(f"API error for symbol '{symbol}' on new metric '{metric}' (YC Code: {yc_code}): {e}")
        return None

# -----------------------------
# Helper Functions for Database Updates (New Metrics)
# -----------------------------
def verify_new_columns(engine, table_name, expected_columns):
    """
    Verify that all expected new metric columns exist in the table.
    """
    inspector = sqlalchemy.inspect(engine)
    actual_columns = [col['name'] for col in inspector.get_columns(table_name)]
    missing_columns = [col for col in expected_columns if col not in actual_columns]
    if missing_columns:
        logger.warning(f"Missing new columns in {table_name}: {missing_columns}")
    else:
        logger.info(f"All expected new columns are present in {table_name}.")

def check_and_update_new_data(engine, symbol, data):
    """
    Update (or insert) the new metric columns for a given symbol.
    The SQL is built dynamically based solely on NEW_METRICS.
    For new records, a default ProductName is supplied (using the symbol).
    """
    query_sql = "SELECT ProductName FROM Funds_to_Screen WHERE SymbolCUSIP = :symbol"
    update_sql = "UPDATE Funds_to_Screen SET " + ", ".join(f"{col} = :{col}" for col in NEW_METRICS) + " WHERE SymbolCUSIP = :symbol"
    columns = "SymbolCUSIP, ProductName, " + ", ".join(NEW_METRICS)
    placeholders = ":symbol, :ProductName, " + ", ".join(f":{col}" for col in NEW_METRICS)
    insert_sql = f"INSERT INTO Funds_to_Screen ({columns}) VALUES ({placeholders})"
    
    with engine.connect() as conn:
        try:
            result = conn.execute(sqlalchemy.text(query_sql), {'symbol': symbol}).fetchone()
            if result:
                conn.execute(sqlalchemy.text(update_sql), data)
                logger.info(f"Updated new metrics for symbol {symbol}")
            else:
                if "ProductName" not in data or data["ProductName"] is None:
                    data["ProductName"] = symbol
                conn.execute(sqlalchemy.text(insert_sql), data)
                logger.info(f"Inserted new record for new metrics for symbol {symbol}")
            conn.commit()
        except sqlalchemy.exc.SQLAlchemyError as e:
            logger.error(f"Database error for symbol {symbol} (new metrics): {e}")
            conn.rollback()

def process_symbol_new(symbol, fund_type_id, engine):
    """
    Process a single symbol for new metrics:
      - First, query the database for existing new metric values.
      - For each new metric, if the column already has a non-NULL value, use it;
        otherwise, call the YCP API to fetch the data.
      - Update (or insert) the new metric values in the database.
    """
    logger.info(f"Starting new metrics processing for symbol: {symbol}")
    data = {'symbol': symbol}
    
    # Query existing new metric values
    with engine.connect() as conn:
        query = "SELECT " + ", ".join(NEW_METRICS) + " FROM Funds_to_Screen WHERE SymbolCUSIP = :symbol"
        result = conn.execute(sqlalchemy.text(query), {'symbol': symbol}).fetchone()
    
    for metric in NEW_METRICS:
        if result is not None and result[metric] is not None:
            data[metric] = result[metric]
            logger.info(f"Existing value for {metric} found for {symbol}: {result[metric]}. Skipping API call.")
        else:
            value = fetch_new_data_point(symbol, metric, fund_type_id)
            data[metric] = value

    # Ensure every expected key is present.
    for key in NEW_METRICS:
        data.setdefault(key, None)
    logger.debug(f"New data dictionary for {symbol}: {data}")
    check_and_update_new_data(engine, symbol, data)
    logger.info(f"Finished new metrics processing for symbol: {symbol}")

def main():
    start_time = time.time()
    logger.info("Starting new metrics data fetch and insertion process.")
    
    engine = sqlalchemy.create_engine(connection_string,
                                      pool_size=20,
                                      max_overflow=50,
                                      pool_timeout=300)
    
    # Verify that all expected new columns exist.
    expected_new_columns = NEW_METRICS  # only our new metric columns
    verify_new_columns(engine, "Funds_to_Screen", expected_new_columns)
    
    # Retrieve all symbols from the database.
    symbols_df = pd.read_sql(FUND_SYMBOLS_SQL, engine)
    symbols_list = symbols_df[['Fund_Symbol', 'Fund_Type_ID']].values.tolist()
    logger.info(f"Processing new metrics for {len(symbols_list)} symbols from the database.")
    
    # Process symbols in parallel.
    with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
        futures = []
        for symbol, fund_type_id in symbols_list:
            futures.append(executor.submit(process_symbol_new, symbol, fund_type_id, engine))
        for future in concurrent.futures.as_completed(futures):
            try:
                future.result()
            except Exception as exc:
                logger.error(f"Error processing symbol for new metrics: {exc}")
    
    total_time = time.time() - start_time
    logger.info(f"All new metrics processed successfully in {total_time:.2f} seconds")
    engine.dispose()

if __name__ == "__main__":
    main()


2025-02-10 16:22:46,395 - INFO - Starting new metrics data fetch and insertion process.
2025-02-10 16:22:46,605 - INFO - All expected new columns are present in Funds_to_Screen.
2025-02-10 16:22:46,631 - INFO - Processing new metrics for 1060 symbols from the database.
2025-02-10 16:22:46,633 - INFO - Starting new metrics processing for symbol: NTSX
2025-02-10 16:22:46,636 - INFO - Starting new metrics processing for symbol: HIPS
2025-02-10 16:22:46,638 - INFO - Starting new metrics processing for symbol: EAOA
2025-02-10 16:22:46,641 - INFO - Starting new metrics processing for symbol: AOM
2025-02-10 16:22:46,644 - INFO - Starting new metrics processing for symbol: AOK
2025-02-10 16:22:46,646 - INFO - Starting new metrics processing for symbol: EAOK
2025-02-10 16:22:46,647 - INFO - Starting new metrics processing for symbol: EAOM
2025-02-10 16:22:46,650 - INFO - Starting new metrics processing for symbol: INCM
2025-02-10 16:22:46,654 - INFO - Starting new metrics processing for symbol:

In [ ]:
#Additional metadata using YCI calls

import requests
import sqlalchemy
import pandas as pd
import datetime
import time
import logging
import json
from concurrent.futures import ThreadPoolExecutor
from dateutil.relativedelta import relativedelta
import ssl
import certifi
from requests.adapters import HTTPAdapter
from tenacity import retry, stop_after_attempt, wait_exponential

# Set up logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# SQL Server connection configuration with increased pool settings
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/CWA_Fund_Database?"
    "driver=ODBC+Driver+18+for+SQL+Server&trusted_connection=yes&TrustServerCertificate=yes"
)
engine = sqlalchemy.create_engine(
    connection_string,
    pool_size=20,
    max_overflow=50,
    pool_timeout=300
)

# YCharts API configuration and headers
YCHARTS_API_URL = "https://api.ycharts.com"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "X-YCHARTSIP": "50.58.50.123",
    "Host": "api.ycharts.com",
    "Connection": "Keep-Alive"
}

# Define the YCI metrics
YCI_METRICS = [
    "index_fund", "inverse_fund", "leveraged_fund", "socially_responsible_fund", 
    "synthetic_replication_fund", "aum_usd", "open_to_existing_investors", 
    "open_to_new_investors", "ycharts_url", "investment_strategy", 
    "related_securities", "fund_family", "fund_of_funds"
]

# SQL query to fetch fund symbols from the Funds_to_Screen table
FUND_SYMBOLS_SQL = """
SELECT DISTINCT SymbolCUSIP AS Fund_Symbol, Fund_Type_ID
FROM Funds_to_Screen
"""

# Create a custom SSL context to bypass certificate verification (for debugging only)
context = ssl.create_default_context(cafile=certifi.where())
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # In production, use CERT_REQUIRED

# Create a custom HTTPAdapter using the SSL context
class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

# Create a global requests session with the custom adapter mounted for HTTPS
session = requests.Session()
session.mount("https://", CustomHTTPAdapter())

@retry(stop=stop_after_attempt(3), wait=wait_exponential(multiplier=1, min=4, max=10))
def get_api_url(symbol, fund_type_id, metric):
    """
    Construct the YCI API URL based on fund type and metric with retry logic.
    """
    if fund_type_id == 3:
        symbol_for_api = f"M:{symbol}"
        endpoint = "mutual_funds"
    else:
        symbol_for_api = symbol
        endpoint = "companies"
    return f"{YCHARTS_API_URL}/v3/{endpoint}/{symbol_for_api}/info/{metric}?retrieve_ttl=true"

@retry(stop=stop_after_attempt(3), wait=wait_exponential(multiplier=1, min=4, max=10))
def fetch_yci_metric(symbol, fund_type_id, metric):
    """
    Fetch a single YCI metric value for the given fund symbol with retry logic.
    """
    api_url = get_api_url(symbol, fund_type_id, metric)
    logger.info(f"Fetching {metric} for {symbol} using URL: {api_url}")
    try:
        response = session.get(api_url, headers=API_HEADERS, timeout=30)
        response.raise_for_status()
        data = response.json()
        response_key = f"M:{symbol}" if fund_type_id == 3 else symbol
        metric_value = data.get("response", {}).get(response_key, {}) \
                           .get("results", {}).get(metric, {}) \
                           .get("data")
        logger.info(f"Fetched {metric} for {symbol}: {metric_value}")
        return metric_value
    except Exception as e:
        logger.error(f"Error fetching {metric} for {symbol}: {e}")
        return None

def prepare_db_params(data):
    """
    Prepare the dictionary values for database insertion.
    If a value is a list or dict, convert it to a JSON string.
    """
    return { key: (json.dumps(val) if isinstance(val, (list, dict)) else val) for key, val in data.items() }

def update_fund_in_db(symbol, data):
    """
    Check if a record exists for the given symbol in Funds_to_Screen.
    If it exists, update it; otherwise, insert a new record.
    Uses engine.begin() for transaction management with error handling.
    """
    query_sql = "SELECT 1 FROM Funds_to_Screen WHERE SymbolCUSIP = :symbol"
    update_sql = """
    UPDATE Funds_to_Screen 
    SET index_fund = :index_fund,
        inverse_fund = :inverse_fund,
        leveraged_fund = :leveraged_fund,
        socially_responsible_fund = :socially_responsible_fund,
        synthetic_replication_fund = :synthetic_replication_fund,
        aum_usd = :aum_usd,
        open_to_existing_investors = :open_to_existing_investors,
        open_to_new_investors = :open_to_new_investors,
        ycharts_url = :ycharts_url,
        investment_strategy = :investment_strategy,
        related_securities = :related_securities,
        fund_family = :fund_family,
        fund_of_funds = :fund_of_funds
    WHERE SymbolCUSIP = :symbol
    """
    insert_sql = """
    INSERT INTO Funds_to_Screen 
    (SymbolCUSIP, index_fund, inverse_fund, leveraged_fund, socially_responsible_fund, synthetic_replication_fund, aum_usd, 
     open_to_existing_investors, open_to_new_investors, ycharts_url, investment_strategy, related_securities, fund_family, fund_of_funds)
    VALUES 
    (:symbol, :index_fund, :inverse_fund, :leveraged_fund, :socially_responsible_fund, :synthetic_replication_fund, :aum_usd, 
     :open_to_existing_investors, :open_to_new_investors, :ycharts_url, :investment_strategy, :related_securities, :fund_family, :fund_of_funds)
    """
    try:
        params = prepare_db_params(data)
        with engine.begin() as conn:
            result = conn.execute(sqlalchemy.text(query_sql), {"symbol": symbol}).fetchone()
            if result:
                conn.execute(sqlalchemy.text(update_sql), params)
                logger.info(f"Updated DB record for {symbol}")
            else:
                conn.execute(sqlalchemy.text(insert_sql), params)
                logger.info(f"Inserted DB record for {symbol}")
    except Exception as e:
        logger.error(f"Database error for {symbol}: {e}")
        # Note: In a more robust system, you might want to consider rolling back the transaction here
        # conn.rollback() 

def process_fund(row):
    """
    For a given fund (dict with keys 'Fund_Symbol' and 'Fund_Type_ID'),
    fetch all YCI metrics and update the database accordingly.
    """
    symbol = row["Fund_Symbol"]
    fund_type_id = row["Fund_Type_ID"]
    data = {"symbol": symbol}
    for metric in YCI_METRICS:
        data[metric] = fetch_yci_metric(symbol, fund_type_id, metric)
    update_fund_in_db(symbol, data)
    return symbol

def main():
    overall_start = time.time()
    logger.info("Starting YCI data fetch and update process.")
    
    funds_df = pd.read_sql(FUND_SYMBOLS_SQL, engine)
    funds = funds_df.to_dict(orient="records")
    total_funds = len(funds)
    logger.info(f"Retrieved {total_funds} funds to process.")
    
    processed_symbols = []
    # Use a ThreadPoolExecutor with max_workers set to 20
    with ThreadPoolExecutor(max_workers=20) as executor:
        for symbol in executor.map(process_fund, funds):
            processed_symbols.append(symbol)
    
    elapsed = time.time() - overall_start
    logger.info(f"Processed {len(processed_symbols)} funds in {elapsed:.2f} seconds.")
    
    if len(processed_symbols) != total_funds:
        logger.warning(f"Some funds might not have been processed. Expected {total_funds}, processed {len(processed_symbols)}")
    else:
        logger.info("🎉 YCI data fetch and update complete!")

if __name__ == "__main__":
    main()

2025-02-11 09:46:27,095 - INFO - Starting YCI data fetch and update process.
2025-02-11 09:46:27,249 - INFO - Retrieved 1060 funds to process.
2025-02-11 09:46:27,250 - INFO - Fetching index_fund for NTSX using URL: https://api.ycharts.com/v3/companies/NTSX/info/index_fund?retrieve_ttl=true
2025-02-11 09:46:27,253 - INFO - Fetching index_fund for HIPS using URL: https://api.ycharts.com/v3/companies/HIPS/info/index_fund?retrieve_ttl=true
2025-02-11 09:46:27,253 - INFO - Fetching index_fund for EAOA using URL: https://api.ycharts.com/v3/companies/EAOA/info/index_fund?retrieve_ttl=true
2025-02-11 09:46:27,258 - INFO - Fetching index_fund for AOM using URL: https://api.ycharts.com/v3/companies/AOM/info/index_fund?retrieve_ttl=true
2025-02-11 09:46:27,258 - INFO - Fetching index_fund for AOK using URL: https://api.ycharts.com/v3/companies/AOK/info/index_fund?retrieve_ttl=true
2025-02-11 09:46:27,264 - INFO - Fetching index_fund for EAOK using URL: https://api.ycharts.com/v3/companies/EAOK/i

In [2]:
#Update for new benchmarks timeseries info

import math
import certifi
import ssl
import requests
import sqlalchemy
import pandas as pd
import datetime
from dateutil.relativedelta import relativedelta
import time
import concurrent.futures
from requests.adapters import HTTPAdapter

# Configuration
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)

YCHARTS_API_URL = "https://api.ycharts.com/v3"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

METRICS = [
    ("five_year_total_monthly_return", "5 Year Return"),
    ("three_year_total_monthly_return", "3 Year Return"),
    ("one_year_total_monthly_return", "1 Year Return"),
    ("nine_total_monthly_return", "9 Month Return"),
    ("six_total_monthly_return", "6 Month Return"),
    ("three_total_monthly_return", "3 Month Return"),
    ("total_monthly_return", "Monthly Return")
]

BATCH_SIZE = 5000  # Experiment with this value

# Create a custom SSL context
context = ssl.create_default_context(cafile=certifi.where())
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # For debugging only! Use CERT_REQUIRED for production.

# Custom HTTPAdapter to apply our SSL context
class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

# Create a session and mount the adapter for HTTPS requests
session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

# Date Configurations
TODAY = datetime.date.today()
END_DATE = TODAY.replace(day=1) - datetime.timedelta(days=1)  # Last day of the previous month
TWENTY_YEARS_AGO = END_DATE - relativedelta(years=20)

def get_start_date(earliest_date, default_start):
    """Determine the start date for data fetching."""
    if earliest_date and earliest_date > default_start:
        return earliest_date
    return default_start

def check_existing_data(engine, symbol, metric_db_name, start_date, end_date):
    """Check if there's data for the benchmark, metric, and date range in the database."""
    check_sql = """
    SELECT COUNT(*) 
    FROM Benchmark_Returns_Timeseries 
    WHERE Benchmark_Symbol = :symbol 
      AND Metric = :metric 
      AND Date BETWEEN :start_date AND :end_date
    """
    with engine.connect() as conn:
        count = conn.execute(sqlalchemy.text(check_sql), {
            'symbol': symbol,
            'metric': metric_db_name,
            'start_date': start_date,
            'end_date': end_date
        }).scalar()
        return count > 0  # True if data exists, False otherwise

def insert_benchmark_data(engine, batch_data, batch_size=5000):
    """Insert data into the database in batches, checking for duplicates."""
    insert_sql = """
    INSERT INTO Benchmark_Returns_Timeseries (Benchmark_Symbol, Date, ReturnValue, Metric)
    VALUES (:symbol, :date, :value, :metric)
    """
    
    check_sql = """
    SELECT 1 
    FROM Benchmark_Returns_Timeseries 
    WHERE Benchmark_Symbol = :symbol 
      AND Date = :date 
      AND Metric = :metric
    """
    
    unique_data = []
    inserted_count = 0
    with engine.connect() as conn:
        try:
            for item in batch_data:
                existing = conn.execute(sqlalchemy.text(check_sql), item).fetchone()
                if not existing:  # Data doesn't exist, proceed with insert
                    unique_data.append(item)
                    inserted_count += 1
                    if len(unique_data) >= batch_size:
                        conn.execute(sqlalchemy.text(insert_sql), unique_data)
                        conn.commit()
                        unique_data = []  # Reset the batch
            if unique_data:  # Insert any remaining data
                conn.execute(sqlalchemy.text(insert_sql), unique_data)
                conn.commit()
            print(f"Inserted {inserted_count} new data points out of {len(batch_data)}.")
        except sqlalchemy.exc.SQLAlchemyError as sqle:
            print(f"Database error in batch insert: {sqle}")
            conn.rollback()
    return inserted_count

def process_benchmark(symbol, metric, metric_db_name, engine):
    """Process each benchmark for a specific metric, check existing data before API call."""
    
    start_date = get_start_date(None, TWENTY_YEARS_AGO)
    if not start_date:
        print(f"Skipping {symbol} for {metric}: no valid start date.")
        return None

    # Check if data already exists for this benchmark, metric, and date range
    if check_existing_data(engine, symbol, metric_db_name, start_date, END_DATE):
        print(f"Data for {symbol} and {metric} already exists, skipping API call.")
        return None

    start_date_str = start_date.strftime('%Y-%m-%d')
    end_date_str = END_DATE.strftime('%Y-%m-%d')

    api_url = f"{YCHARTS_API_URL}/indices/{symbol}/series/{metric}?retrieve_ttl=true&start_date={start_date_str}&end_date={end_date_str}"

    try:
        response = session.get(api_url, headers=API_HEADERS)
        response.raise_for_status()

        parsed_data = response.json()
        data_map = {}

        if 'response' in parsed_data and symbol in parsed_data['response']:
            for date, value in parsed_data['response'][symbol]['results'][metric]['data']:
                if symbol not in data_map:
                    data_map[symbol] = {}
                data_map[symbol][date] = {metric: value}

    except requests.exceptions.RequestException as e:
        print(f"API error for {symbol} on metric {metric}: {e}")
        return None

    if data_map:  
        print(f"Processed {symbol} for {metric}")
        return data_map
    return None

def main():
    start_time = time.time()
    
    engine = sqlalchemy.create_engine(connection_string, 
                                      pool_size=20, 
                                      max_overflow=50,
                                      pool_timeout=300)

    # Fetch symbols from the Benchmarks table
    sql = """
    SELECT Benchmark_Symbol
    FROM Benchmarks
    """
    symbols_df = pd.read_sql(sql, engine)
    symbols = symbols_df['Benchmark_Symbol'].tolist()

    total_inserted = 0
    for metric, metric_db_name in METRICS:
        print(f"\n🚀 Loading Metric: {metric}")
        all_data = []  # Collect all data for this metric
        
        with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
            futures = []
            for symbol in symbols:
                futures.append(executor.submit(process_benchmark, symbol, metric, metric_db_name, engine))  
            
            for future in concurrent.futures.as_completed(futures):
                try:
                    data_map = future.result()
                    if data_map:
                        for symbol, dates in data_map.items():
                            for date_str, metric_data in dates.items():
                                for metric_val, value in metric_data.items():
                                    if value is not None:
                                        try:
                                            date_obj = datetime.datetime.strptime(date_str, "%Y-%m-%d").date()
                                            decimal_value = round(float(value), 6)
                                            all_data.append({
                                                'symbol': symbol,
                                                'date': date_obj,
                                                'value': decimal_value,
                                                'metric': metric_db_name
                                            })
                                        except ValueError as ve:
                                            print(f"Data conversion error for {symbol} on {date_str}: {ve}")
                except Exception as exc:
                    print(f'An error occurred for {metric}: {exc}')

        # Insert all collected data in one go
        if all_data:
            total_inserted += insert_benchmark_data(engine, all_data)

    total_time = time.time() - start_time
    print(f"\n🎉 All done loading all metrics! Total time: {total_time:.2f} seconds")
    print(f"Total data points inserted: {total_inserted}")
    print(f"Total benchmarks processed: {len(symbols)}")
    print(f"Average time per benchmark per metric: {total_time / (len(symbols) * len(METRICS)):.2f} seconds")

    # Check pool status for debugging
    pool_stats = engine.pool.status()
    print(f"Pool Status: {pool_stats}")

    engine.dispose()

if __name__ == "__main__":
    main()


🚀 Loading Metric: five_year_total_monthly_return
Data for ^ALMLPTR and five_year_total_monthly_return already exists, skipping API call.
Data for ^BBUTB13MTR and five_year_total_monthly_return already exists, skipping API call.
Data for ^CRUSREITTR and five_year_total_monthly_return already exists, skipping API call.
Data for ^BBMBTR and five_year_total_monthly_return already exists, skipping API call.
Data for ^BBUGCR13YT and five_year_total_monthly_return already exists, skipping API call.
Data for ^BBUGCR15YT and five_year_total_monthly_return already exists, skipping API call.
Data for ^BBEMUSDATR and five_year_total_monthly_return already exists, skipping API call.
Data for ^BBUSCOHYTR and five_year_total_monthly_return already exists, skipping API call.
Data for ^BBGATR and five_year_total_monthly_return already exists, skipping API call.
Data for ^MSACPCXJPT and five_year_total_monthly_return already exists, skipping API call.
Data for ^BBUSATR and five_year_total_monthly_retur

In [3]:
import math
import certifi
import ssl
import requests
import sqlalchemy
import pandas as pd
import datetime
from dateutil.relativedelta import relativedelta
import time
import concurrent.futures
from requests.adapters import HTTPAdapter

# Configuration
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)

YCHARTS_API_URL = "https://api.ycharts.com/v3"
API_HEADERS = {
    "X-YCHARTSAUTHORIZATION": "yIIphqbsQysnTvWWxfW33w",  # Replace with your actual API key
    "X-YCHARTSEXCELSESSION": "b645cd897b2446bfa3796acfa3a879db",
    "X-YCHARTSEXCELVERSION": "4.4",
    "X-YCHARTSOPERATINGSYSTEM": "Microsoft Windows NT 10.0.26100.0",
    "Content-Type": "application/x-www-form-urlencoded"
}

METRICS = [
    ("five_year_total_monthly_return", "5 Year Return"),
    ("three_year_total_monthly_return", "3 Year Return"),
    ("one_year_total_monthly_return", "1 Year Return"),
    ("nine_total_monthly_return", "9 Month Return"),
    ("six_total_monthly_return", "6 Month Return"),
    ("three_total_monthly_return", "3 Month Return"),
    ("total_monthly_return", "Monthly Return")
]

BATCH_SIZE = 5000  # Experiment with this value

# Create a custom SSL context
context = ssl.create_default_context(cafile=certifi.where())
context.check_hostname = False
context.verify_mode = ssl.CERT_NONE  # For debugging only! Use CERT_REQUIRED for production.

# Custom HTTPAdapter to apply our SSL context
class CustomHTTPAdapter(HTTPAdapter):
    def init_poolmanager(self, *args, **kwargs):
        kwargs['ssl_context'] = context
        return super().init_poolmanager(*args, **kwargs)

# Create a session and mount the adapter for HTTPS requests
session = requests.Session()
session.mount('https://', CustomHTTPAdapter())

# Date Configurations
TODAY = datetime.date.today()
END_DATE = TODAY.replace(day=1) - datetime.timedelta(days=1)  # Last day of the previous month
TWENTY_YEARS_AGO = END_DATE - relativedelta(years=20)

def get_start_date(earliest_date, default_start):
    """Determine the start date for data fetching."""
    if earliest_date and earliest_date > default_start:
        return earliest_date
    return default_start

def check_existing_data(engine, symbol, metric_db_name, start_date, end_date):
    """Check if there's data for the benchmark, metric, and date range in the database."""
    check_sql = """
    SELECT COUNT(*) 
    FROM Benchmark_Returns_Timeseries 
    WHERE Benchmark_Symbol = :symbol 
      AND Metric = :metric 
      AND Date BETWEEN :start_date AND :end_date
    """
    with engine.connect() as conn:
        count = conn.execute(sqlalchemy.text(check_sql), {
            'symbol': symbol,
            'metric': metric_db_name,
            'start_date': start_date,
            'end_date': end_date
        }).scalar()
        return count > 0  # True if data exists, False otherwise

def insert_benchmark_data(engine, batch_data, batch_size=5000):
    """Insert data into the database in batches, checking for duplicates."""
    insert_sql = """
    INSERT INTO Benchmark_Returns_Timeseries (Benchmark_Symbol, Date, ReturnValue, Metric)
    VALUES (:symbol, :date, :value, :metric)
    """
    
    check_sql = """
    SELECT 1 
    FROM Benchmark_Returns_Timeseries 
    WHERE Benchmark_Symbol = :symbol 
      AND Date = :date 
      AND Metric = :metric
    """
    
    unique_data = []
    inserted_count = 0
    with engine.connect() as conn:
        try:
            for item in batch_data:
                existing = conn.execute(sqlalchemy.text(check_sql), item).fetchone()
                if not existing:  # Data doesn't exist, proceed with insert
                    unique_data.append(item)
                    inserted_count += 1
                    if len(unique_data) >= batch_size:
                        conn.execute(sqlalchemy.text(insert_sql), unique_data)
                        conn.commit()
                        unique_data = []  # Reset the batch
            if unique_data:  # Insert any remaining data
                conn.execute(sqlalchemy.text(insert_sql), unique_data)
                conn.commit()
            print(f"Inserted {inserted_count} new data points out of {len(batch_data)}.")
        except sqlalchemy.exc.SQLAlchemyError as sqle:
            print(f"Database error in batch insert: {sqle}")
            conn.rollback()
    return inserted_count

def process_benchmark(symbol, metric, metric_db_name, engine):
    """Process each benchmark for a specific metric, check existing data before API call."""
    
    start_date = get_start_date(None, TWENTY_YEARS_AGO)
    if not start_date:
        print(f"Skipping {symbol} for {metric}: no valid start date.")
        return None

    # Check if data already exists for this benchmark, metric, and date range
    if check_existing_data(engine, symbol, metric_db_name, start_date, END_DATE):
        print(f"Data for {symbol} and {metric} already exists, skipping API call.")
        return None

    start_date_str = start_date.strftime('%Y-%m-%d')
    end_date_str = END_DATE.strftime('%Y-%m-%d')

    api_url = f"{YCHARTS_API_URL}/indices/{symbol}/series/{metric}?retrieve_ttl=true&start_date={start_date_str}&end_date={end_date_str}"

    try:
        response = session.get(api_url, headers=API_HEADERS)
        response.raise_for_status()

        parsed_data = response.json()
        data_map = {}

        if 'response' in parsed_data and symbol in parsed_data['response']:
            for date, value in parsed_data['response'][symbol]['results'][metric]['data']:
                if symbol not in data_map:
                    data_map[symbol] = {}
                data_map[symbol][date] = {metric: value}

    except requests.exceptions.RequestException as e:
        print(f"API error for {symbol} on metric {metric}: {e}")
        return None

    if data_map:  
        print(f"Processed {symbol} for {metric}")
        return data_map
    return None

def main():
    start_time = time.time()
    
    engine = sqlalchemy.create_engine(connection_string, 
                                      pool_size=20, 
                                      max_overflow=50,
                                      pool_timeout=300)

    # Specify the exact symbols we want to process
    symbols = [
        "^BBMB15YTR", "^BBUSCRTR", "^BBUSMBSTR", "^BBUSTTR", "^BBUTISTR", "^LGALSEUS", 
        "^MSACAS", "^MSACSMCNTR", "^MSACXUSNTR", "^MSACXUSSCN", "^MSEMLA", "^MSIN", 
        "^MSMX", "^MSWMMTR", "^MSWTR", "^PEATR", "^RLVTR", "^RMCTR", "^RMVTR", 
        "^RUJTR", "^RUOTR", "^RUTTR", "^SPXUSTR", "^STRB"
    ]

    total_inserted = 0
    for metric, metric_db_name in METRICS:
        print(f"\n🚀 Loading Metric: {metric}")
        all_data = []  # Collect all data for this metric
        
        with concurrent.futures.ThreadPoolExecutor(max_workers=20) as executor:
            futures = []
            for symbol in symbols:
                futures.append(executor.submit(process_benchmark, symbol, metric, metric_db_name, engine))  
            
            for future in concurrent.futures.as_completed(futures):
                try:
                    data_map = future.result()
                    if data_map:
                        for symbol, dates in data_map.items():
                            for date_str, metric_data in dates.items():
                                for metric_val, value in metric_data.items():
                                    if value is not None:
                                        try:
                                            date_obj = datetime.datetime.strptime(date_str, "%Y-%m-%d").date()
                                            decimal_value = round(float(value), 6)
                                            all_data.append({
                                                'symbol': symbol,
                                                'date': date_obj,
                                                'value': decimal_value,
                                                'metric': metric_db_name
                                            })
                                        except ValueError as ve:
                                            print(f"Data conversion error for {symbol} on {date_str}: {ve}")
                except Exception as exc:
                    print(f'An error occurred for {metric}: {exc}')

        # Insert all collected data in one go
        if all_data:
            total_inserted += insert_benchmark_data(engine, all_data)

    total_time = time.time() - start_time
    print(f"\n🎉 All done loading all metrics! Total time: {total_time:.2f} seconds")
    print(f"Total data points inserted: {total_inserted}")
    print(f"Total benchmarks processed: {len(symbols)}")
    print(f"Average time per benchmark per metric: {total_time / (len(symbols) * len(METRICS)):.2f} seconds")

    # Check pool status for debugging
    pool_stats = engine.pool.status()
    print(f"Pool Status: {pool_stats}")

    engine.dispose()

if __name__ == "__main__":
    main()


🚀 Loading Metric: five_year_total_monthly_return
Processed ^BBMB15YTR for five_year_total_monthly_return
Processed ^MSACXUSSCN for five_year_total_monthly_return
Processed ^RLVTR for five_year_total_monthly_return
Processed ^BBUTISTR for five_year_total_monthly_return
Processed ^MSACXUSNTR for five_year_total_monthly_return
Processed ^MSWTR for five_year_total_monthly_return
Processed ^RMVTR for five_year_total_monthly_return
Processed ^MSACAS for five_year_total_monthly_return
Processed ^MSIN for five_year_total_monthly_return
Processed ^MSMX for five_year_total_monthly_return
Processed ^BBUSMBSTR for five_year_total_monthly_return
Processed ^RUJTR for five_year_total_monthly_return
Processed ^BBUSTTR for five_year_total_monthly_return
Processed ^MSACSMCNTR for five_year_total_monthly_return
Processed ^BBUSCRTR for five_year_total_monthly_return
Processed ^MSWMMTR for five_year_total_monthly_return
Processed ^PEATR for five_year_total_monthly_return
Processed ^RMCTR for five_year_tot

In [11]:
#fix missing symbols in funds to screen

import pandas as pd
import logging
from sqlalchemy import create_engine, text
from sqlalchemy.exc import IntegrityError

# -----------------------------------------------------------------------------
# Setup Logging
# -----------------------------------------------------------------------------
logging.basicConfig(
    filename="funds_import_log.txt",
    level=logging.INFO,
    format="%(asctime)s - %(levelname)s - %(message)s"
)
logging.info("Script started.")

# -----------------------------------------------------------------------------
# Setup Database Connection
# -----------------------------------------------------------------------------
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)
engine = create_engine(connection_string)

# -----------------------------------------------------------------------------
# Helper function to clean a DataFrame's key columns
# -----------------------------------------------------------------------------
def clean_dataframe(df):
    if 'SymbolCUSIP' in df.columns:
        df['SymbolCUSIP'] = df['SymbolCUSIP'].astype(str).str.strip().str.upper()
    if 'ExpenseRatio' in df.columns:
        # Remove any '%' and commas before conversion
        df['ExpenseRatio'] = pd.to_numeric(
            df['ExpenseRatio'].astype(str).str.replace('%', '', regex=False).str.replace(',', '', regex=False),
            errors='coerce'
        )
    return df

# -----------------------------------------------------------------------------
# Helper function to perform row-by-row insertion
# -----------------------------------------------------------------------------
def insert_rows(df, table_name, connection):
    inserted_rows = []
    insert_stmt = text(f"""
        INSERT INTO {table_name}
           (ProductName, SymbolCUSIP, ETFComplianceCategory, ExpenseRatio, 
            Fund_Type_ID, YC_Broad_Category_ID, YC_Broad_Asset_Class_ID, 
            YC_Global_Category_ID, YC_Category_ID, CWA_Broad_Category_ID)
        VALUES
           (:ProductName, :SymbolCUSIP, :ETFComplianceCategory, :ExpenseRatio, 
            :Fund_Type_ID, :YC_Broad_Category_ID, :YC_Broad_Asset_Class_ID, 
            :YC_Global_Category_ID, :YC_Category_ID, :CWA_Broad_Category_ID)
    """)
    for idx, row in df.iterrows():
        params = {
            "ProductName": row["ProductName"],
            "SymbolCUSIP": row["SymbolCUSIP"],
            "ETFComplianceCategory": row["ETFComplianceCategory"],
            "ExpenseRatio": row["ExpenseRatio"],
            "Fund_Type_ID": row["Fund_Type_ID"],
            "YC_Broad_Category_ID": row["YC_Broad_Category_ID"],
            "YC_Broad_Asset_Class_ID": row["YC_Broad_Asset_Class_ID"],
            "YC_Global_Category_ID": row["YC_Global_Category_ID"],
            "YC_Category_ID": row["YC_Category_ID"],
            "CWA_Broad_Category_ID": row["CWA_Broad_Category_ID"]
        }
        try:
            connection.execute(insert_stmt, params)
            inserted_rows.append(params)
        except IntegrityError as ie:
            # Likely a duplicate key error – log and skip this row
            logging.warning(f"Skipping duplicate for SymbolCUSIP: {row['SymbolCUSIP']}")
        except Exception as e:
            logging.error(f"Error inserting {row['SymbolCUSIP']}: {e}")
    return inserted_rows

# -----------------------------------------------------------------------------
# STEP 1: Process NORMAL FUNDS (Apply Exclusion List)
# -----------------------------------------------------------------------------
exclusion_categories = [7, 8, 9, 10, 25, 26, 27]
exclusion_str = ", ".join(str(x) for x in exclusion_categories)

query_normal = f"""
SELECT 
    ProductName,
    SymbolCUSIP,
    ETFComplianceCategory,
    ExpenseRatio,
    Fund_Type_ID,
    YC_Broad_Category_ID,
    YC_Broad_Asset_Class_ID,
    YC_Global_Category_ID,
    YC_Category_ID,
    CWA_Broad_Category_ID
FROM RJ_Import
WHERE CWA_Broad_Category_ID NOT IN ({exclusion_str})
"""

normal_df = pd.read_sql(query_normal, engine)
logging.info(f"Normal funds fetched: {normal_df.shape[0]}")
normal_df = clean_dataframe(normal_df)

# Get existing symbols from Funds_to_Screen
existing_df = pd.read_sql("SELECT SymbolCUSIP FROM Funds_to_Screen", engine)
if not existing_df.empty:
    existing_df['SymbolCUSIP'] = existing_df['SymbolCUSIP'].astype(str).str.strip().str.upper()
existing_symbols = set(existing_df['SymbolCUSIP'].tolist())

# Filter out records that already exist and drop duplicates
new_normal_df = normal_df[~normal_df['SymbolCUSIP'].isin(existing_symbols)]
logging.info(f"Normal funds to insert before deduplication: {new_normal_df.shape[0]}")
new_normal_df = new_normal_df.drop_duplicates(subset=["SymbolCUSIP"])
logging.info(f"Normal funds to insert after deduplication: {new_normal_df.shape[0]}")

inserted_normal = []
with engine.begin() as connection:
    inserted_normal = insert_rows(new_normal_df, "Funds_to_Screen", connection)

symbols_normal = [row["SymbolCUSIP"] for row in inserted_normal]
logging.info("Inserted normal funds: " + ", ".join(symbols_normal))

# -----------------------------------------------------------------------------
# STEP 2: Process MANUAL OVERRIDE FUNDS (Ignore Exclusion List)
# -----------------------------------------------------------------------------
manual_symbols = ['RSST', 'RSBT', 'RSSY', 'RSBY', 'RSBA']
manual_symbols_str = ", ".join([f"'{sym}'" for sym in manual_symbols])

query_manual = f"""
SELECT 
    ProductName,
    SymbolCUSIP,
    ETFComplianceCategory,
    ExpenseRatio,
    Fund_Type_ID,
    YC_Broad_Category_ID,
    YC_Broad_Asset_Class_ID,
    YC_Global_Category_ID,
    YC_Category_ID,
    CWA_Broad_Category_ID
FROM RJ_Import
WHERE SymbolCUSIP IN ({manual_symbols_str})
"""

manual_df = pd.read_sql(query_manual, engine)
logging.info(f"Manual funds fetched: {manual_df.shape[0]}")
manual_df = clean_dataframe(manual_df)

# Refresh existing funds from Funds_to_Screen
existing_df = pd.read_sql("SELECT SymbolCUSIP FROM Funds_to_Screen", engine)
if not existing_df.empty:
    existing_df['SymbolCUSIP'] = existing_df['SymbolCUSIP'].astype(str).str.strip().str.upper()
existing_symbols = set(existing_df['SymbolCUSIP'].tolist())

new_manual_df = manual_df[~manual_df['SymbolCUSIP'].isin(existing_symbols)]
logging.info(f"Manual funds to insert before deduplication: {new_manual_df.shape[0]}")
new_manual_df = new_manual_df.drop_duplicates(subset=["SymbolCUSIP"])
logging.info(f"Manual funds to insert after deduplication: {new_manual_df.shape[0]}")

inserted_manual = []
with engine.begin() as connection:
    inserted_manual = insert_rows(new_manual_df, "Funds_to_Screen", connection)

symbols_manual = [row["SymbolCUSIP"] for row in inserted_manual]
logging.info("Inserted manual funds: " + ", ".join(symbols_manual))

# -----------------------------------------------------------------------------
# STEP 3: Export Inserted Funds Log to Excel
# -----------------------------------------------------------------------------
# Create DataFrames from inserted records for Excel export
if inserted_normal or inserted_manual:
    df_normal_inserted = pd.DataFrame(inserted_normal)
    df_manual_inserted = pd.DataFrame(inserted_manual)
    excel_file = "inserted_funds_log.xlsx"
    with pd.ExcelWriter(excel_file) as writer:
        if not df_normal_inserted.empty:
            df_normal_inserted.to_excel(writer, sheet_name="Normal Funds", index=False)
        if not df_manual_inserted.empty:
            df_manual_inserted.to_excel(writer, sheet_name="Manual Funds", index=False)
    logging.info(f"Exported inserted funds log to {excel_file}")
else:
    logging.info("No new funds were inserted; nothing to export.")

logging.info("Script finished.")


In [12]:
import pandas as pd
import logging
import sys
from sqlalchemy import create_engine, text
from sqlalchemy.exc import IntegrityError

# -----------------------------------------------------------------------------
# Setup Logging: Log to both console and file
# -----------------------------------------------------------------------------
logger = logging.getLogger()
logger.setLevel(logging.INFO)

# Clear any existing handlers
if logger.hasHandlers():
    logger.handlers.clear()

# Create formatter
formatter = logging.Formatter("%(asctime)s - %(levelname)s - %(message)s")

# Create console handler and set level to INFO
console_handler = logging.StreamHandler(sys.stdout)
console_handler.setLevel(logging.INFO)
console_handler.setFormatter(formatter)
logger.addHandler(console_handler)

# Create file handler which logs even debug messages
file_handler = logging.FileHandler("funds_import_log.txt", mode="w")
file_handler.setLevel(logging.INFO)
file_handler.setFormatter(formatter)
logger.addHandler(file_handler)

logger.info("Script started.")

# -----------------------------------------------------------------------------
# Setup Database Connection
# -----------------------------------------------------------------------------
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)
engine = create_engine(connection_string)

# -----------------------------------------------------------------------------
# Helper function to clean a DataFrame's key columns
# -----------------------------------------------------------------------------
def clean_dataframe(df):
    if 'SymbolCUSIP' in df.columns:
        df['SymbolCUSIP'] = df['SymbolCUSIP'].astype(str).str.strip().str.upper()
    if 'ExpenseRatio' in df.columns:
        # Remove '%' and commas before conversion to numeric
        df['ExpenseRatio'] = pd.to_numeric(
            df['ExpenseRatio'].astype(str).str.replace('%', '', regex=False)
              .str.replace(',', '', regex=False),
            errors='coerce'
        )
    return df

# -----------------------------------------------------------------------------
# Helper function to perform row-by-row insertion
# -----------------------------------------------------------------------------
def insert_rows(df, table_name, connection):
    inserted_rows = []
    insert_stmt = text(f"""
        INSERT INTO {table_name}
           (ProductName, SymbolCUSIP, ETFComplianceCategory, ExpenseRatio, 
            Fund_Type_ID, YC_Broad_Category_ID, YC_Broad_Asset_Class_ID, 
            YC_Global_Category_ID, YC_Category_ID, CWA_Broad_Category_ID)
        VALUES
           (:ProductName, :SymbolCUSIP, :ETFComplianceCategory, :ExpenseRatio, 
            :Fund_Type_ID, :YC_Broad_Category_ID, :YC_Broad_Asset_Class_ID, 
            :YC_Global_Category_ID, :YC_Category_ID, :CWA_Broad_Category_ID)
    """)
    for idx, row in df.iterrows():
        params = {
            "ProductName": row["ProductName"],
            "SymbolCUSIP": row["SymbolCUSIP"],
            "ETFComplianceCategory": row["ETFComplianceCategory"],
            "ExpenseRatio": row["ExpenseRatio"],
            "Fund_Type_ID": row["Fund_Type_ID"],
            "YC_Broad_Category_ID": row["YC_Broad_Category_ID"],
            "YC_Broad_Asset_Class_ID": row["YC_Broad_Asset_Class_ID"],
            "YC_Global_Category_ID": row["YC_Global_Category_ID"],
            "YC_Category_ID": row["YC_Category_ID"],
            "CWA_Broad_Category_ID": row["CWA_Broad_Category_ID"]
        }
        try:
            connection.execute(insert_stmt, params)
            inserted_rows.append(params)
        except IntegrityError as ie:
            logger.warning(f"Skipping duplicate for SymbolCUSIP: {row['SymbolCUSIP']}")
        except Exception as e:
            logger.error(f"Error inserting {row['SymbolCUSIP']}: {e}")
    return inserted_rows

# -----------------------------------------------------------------------------
# STEP 1: Process NORMAL FUNDS (Apply Exclusion List)
# -----------------------------------------------------------------------------
exclusion_categories = [7, 8, 9, 10, 25, 26, 27]
exclusion_str = ", ".join(str(x) for x in exclusion_categories)

query_normal = f"""
SELECT 
    ProductName,
    SymbolCUSIP,
    ETFComplianceCategory,
    ExpenseRatio,
    Fund_Type_ID,
    YC_Broad_Category_ID,
    YC_Broad_Asset_Class_ID,
    YC_Global_Category_ID,
    YC_Category_ID,
    CWA_Broad_Category_ID
FROM RJ_Import
WHERE CWA_Broad_Category_ID NOT IN ({exclusion_str})
"""

normal_df = pd.read_sql(query_normal, engine)
logger.info(f"Normal funds fetched: {normal_df.shape[0]}")
normal_df = clean_dataframe(normal_df)

# Get already imported funds from Funds_to_Screen
existing_df = pd.read_sql("SELECT SymbolCUSIP FROM Funds_to_Screen", engine)
if not existing_df.empty:
    existing_df['SymbolCUSIP'] = existing_df['SymbolCUSIP'].astype(str).str.strip().str.upper()
existing_symbols = set(existing_df['SymbolCUSIP'].tolist())

# Filter out records that already exist and drop duplicates
new_normal_df = normal_df[~normal_df['SymbolCUSIP'].isin(existing_symbols)]
logger.info(f"Normal funds to insert before deduplication: {new_normal_df.shape[0]}")
new_normal_df = new_normal_df.drop_duplicates(subset=["SymbolCUSIP"])
logger.info(f"Normal funds to insert after deduplication: {new_normal_df.shape[0]}")

inserted_normal = []
with engine.begin() as connection:
    inserted_normal = insert_rows(new_normal_df, "Funds_to_Screen", connection)

symbols_normal = [row["SymbolCUSIP"] for row in inserted_normal]
logger.info("Inserted normal funds: " + ", ".join(symbols_normal))

# -----------------------------------------------------------------------------
# STEP 2: Process MANUAL OVERRIDE FUNDS (Ignore Exclusion List)
# -----------------------------------------------------------------------------
manual_symbols = ['RSST', 'RSBT', 'RSSY', 'RSBY', 'RSBA']
manual_symbols_str = ", ".join([f"'{sym}'" for sym in manual_symbols])

query_manual 


2025-02-13 12:20:57,489 - INFO - Script started.
2025-02-13 12:20:57,588 - INFO - Normal funds fetched: 5610
2025-02-13 12:20:57,614 - INFO - Normal funds to insert before deduplication: 0
2025-02-13 12:20:57,617 - INFO - Normal funds to insert after deduplication: 0
2025-02-13 12:20:57,618 - INFO - Inserted normal funds: 


"\nSELECT \n    ProductName,\n    SymbolCUSIP,\n    ETFComplianceCategory,\n    ExpenseRatio,\n    Fund_Type_ID,\n    YC_Broad_Category_ID,\n    YC_Broad_Asset_Class_ID,\n    YC_Global_Category_ID,\n    YC_Category_ID,\n    CWA_Broad_Category_ID\nFROM RJ_Import\nWHERE SymbolCUSIP IN ('RSST', 'RSBT', 'RSSY', 'RSBY', 'RSBA')\n"

In [13]:
#determine which are the new symbols due to bad logging from chatgpt

import pandas as pd
from sqlalchemy import create_engine

# Define your connection string
connection_string = (
    "mssql+pyodbc://JULIANS_LAPTOP\\SQLEXPRESS/"
    "CWA_Fund_Database?driver=ODBC+Driver+18+for+SQL+Server"
    "&trusted_connection=yes&TrustServerCertificate=yes"
)

# Create the SQLAlchemy engine
engine = create_engine(connection_string)

# Define the query: look for rows where YC_BM_Symbol is NULL or blank (empty string after trimming)
query = """
SELECT SymbolCUSIP, ProductName, YC_BM_Symbol
FROM Funds_to_Screen
WHERE (YC_BM_Symbol IS NULL OR LTRIM(RTRIM(YC_BM_Symbol)) = '')
"""

# Execute the query and load the results into a DataFrame
df = pd.read_sql(query, engine)

# Export the DataFrame to an Excel file
output_file = "blank_YC_BM_Symbols.xlsx"
df.to_excel(output_file, index=False)

print(f"Exported {df.shape[0]} symbols with blank YC_BM_Symbol to {output_file}")


Exported 4526 symbols with blank YC_BM_Symbol to blank_YC_BM_Symbols.xlsx
